In [1]:
#@title [Notebook config]
nb_mode = "run" #@param ["run", "load"]
nb_save_figs = False #@param {type:"boolean"}
nb_save_figs = nb_save_figs and nb_mode == "run"
nb_export_figs = False #@param {type:"boolean"}
nb_export_format = "pdf" #@param ["png", "jpeg", "svg", "pdf"]

In [2]:
#@title [Ignore warnings]
import warnings
warnings.filterwarnings('ignore')
warnings.simplefilter('ignore')

In [3]:
#@title [Install & Imports]
#%pip install -q addict
#%pip install -q autodiscjax
#%pip install -q plotly
#%pip install -q matplotlib
#%pip install -q py-markdown-table
#%pip install -q shapely

import jax
jax.config.update('jax_platform_name', 'cpu')

from addict import Dict
from autodiscjax import DictTree
import csv
from fractions import Fraction
from io import StringIO
from IPython.display import display, HTML, Image, Markdown
import jax.numpy as jnp
import matplotlib.colors as mcolors
import numpy as np
import PIL
import plotly
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from py_markdown_table.markdown_table import markdown_table
from shapely import Point, Polygon, unary_union
import re
import requests
from scipy.stats import ttest_ind
import textwrap

In [4]:
#@title [Plot utils]

# when need to display only a subset of points in trajectory scatters (otherwise html very big)
def downsample_traj(traj, scaling_vector=np.ones((2,)), eps=0.05):
    """
    traj: (2, T) array
    scaling_vector: 2D array
    eps: we discard all points that are closer to eps
    """

    scaling_vector = scaling_vector[:, np.newaxis]
    traj = traj/scaling_vector
    traj_filt  = [traj[:, i] for i in range(10)]
    ids_filt = [i for i in range(10)]
    
    eps_max = 2
    
    
    for i, e in enumerate(traj.T):
        if i>=10 and (np.linalg.norm(e-traj_filt[-1], ord=2) > eps or i>len(traj.T)-10):
            traj_filt.append(e)
            ids_filt.append(i)
    traj_filt = np.array(traj_filt).T
    ids_filt = np.array(ids_filt)
    return traj_filt*scaling_vector, ids_filt

# color to visualize time from trajectory start point A (red) to trajectory end point B (cyan) 
n_points = 100 
c = [mcolors.hsv_to_rgb((step / (2*n_points), 1, 1)) for step in range(n_points)]
traj_cscale=[(x.item(), f'rgb({int(color[0]*255)}, {int(color[1]*255)}, {int(color[2]*255)})') for (x, color) in zip(jnp.linspace(0., 1., len(c)), c)]

# default colors
default_colors = ['rgb(204,121,167)', 
                  'rgb(0,114,178)',
                  'rgb(230,159,0)',  
                  'rgb(0,158,115)',
                  'rgb(127,127,127)',
                  'rgb(240,228,66)',
                  'rgb(148,103,189)',
                  'rgb(86,180,233)',
                  'rgb(213,94,0)',
                  'rgb(140,86,75)',
                  'rgb(214,39,40)',
                  'rgb(0,0,0)']
transparency = 0.6
default_colors_shade = ['rgba' + color[3:-1]  + ', ' + str(transparency) + ')' for color in default_colors]

default_dashes = ['solid', 'longdash', 'dot', 'dash', 'dashdot', 'longdashdot',
                 'solid', 'longdash', 'dot', 'dash', 'dashdot', 'longdashdot']


# plotly default layout
default_layout = Dict(
    font=Dict(
        size=10,
    ),
    title=Dict(font_size=10),
    
    xaxis=Dict(
        titlefont=Dict(size=10),
        tickfont=Dict(size=10),
        title_standoff=5,
        linecolor='rgba(0, 0, 0, .1)',
    ),
    
    yaxis=Dict(
        titlefont=Dict(size=10),
        tickfont=Dict(size=10),
        title_standoff=5,
        gridcolor='rgba(0, 0, 0, .1)',
        linecolor='rgba(0, 0, 0, .1)',
        #zerolinecolor='rgba(0, 0, 0, .1)'
    ),
    
    updatemenus=[],
    autosize=True,

    plot_bgcolor='rgba(0, 0, 0, 0)', 
    paper_bgcolor='rgba(0, 0, 0, 0)', 

    margin = Dict(
        l=20,
        r=20,
        b=20,
        t=20
        ),

    legend=Dict(
        xanchor='left',
        yanchor='top',
        y=1,
        x=1,
        font_size=10,
     ),     

    )

default_annotation_layout = Dict(
    font_size=10,
)

def make_title(fig_idx, fig, title, figtitle_fontsize="1em",title_fontsize="0.8em"):
    return f'<span style="font-size: {title_fontsize}; color: rgba(0, 0, 0, 0.6)">' + f'<b style="font-size: {figtitle_fontsize};">Figure {fig_idx}: </b>' + t + '</span><br><br>'

def make_html_fig(fig_idx, fig, width, height, title, size_unit="px", figtitle_fontsize="1em", title_fontsize="0.8em", full_html=False, include_plotlyjs=False, config={}):
    if isinstance(fig, go.Figure):
        # autosize fig
        fig.layout.autosize = True
        fig.layout.width = None
        fig.layout.height = None
        
        # convert to html
        default_config = {'displaylogo': False, 'modeBarButtonsToRemove': ['select', 'lasso2d', 'autoScale']}
        for k,v in config.items():
            default_config[k] = v
        html_fig = fig.to_html(config=default_config, full_html=full_html, include_plotlyjs=include_plotlyjs, default_width='100%', default_height='100%')
        html_fig = html_fig[:4]+ f' style="aspect-ratio: {str(Fraction(width,height))};"'+ html_fig[4:]# add aspect ratio
        
    elif isinstance(fig, str) and fig.split(".")[-1] in ["png","jpg","jpeg"]:
        html_fig = f'<div><img src="{fig}" alt="Figure {fig_idx}" style="aspect-ratio: {str(Fraction(width,height))}; width:100%;"></div>'

    # change div style and append title
    div_tag = f'<div id="figure-{fig_idx}" style="margin-top: 50px; max-width: {width}{size_unit};">'
    if title is None:
        title_tag = ""
    else:
        title_tag = f'<span style="font-size: {title_fontsize}; color: rgba(0, 0, 0, 0.6)">' + f'<b style="font-size: {figtitle_fontsize};">Figure {fig_idx}: </b>' + title + '</span>'
    html_fig = div_tag + html_fig +  title_tag + '</div>'
    # html_fig = html_fig +  title_tag
    
    return html_fig


def export_img_fig(fig_idx, fig, width, height, img_format=None, scale=1):
    
    if isinstance(fig, go.Figure):
        # autosize fig
        fig.layout.autosize = True
        fig.layout.width = None
        fig.layout.height = None

        # convert to img
        format=img_format if img_format is not None else nb_export_format
        img_fig = fig.write_image(f"figures/paper_fig_{fig_idx}.{format}", width=width, height=height, scale=scale, format=format)
    
    return

display(HTML('<script src="https://cdnjs.cloudflare.com/ajax/libs/plotly.js/2.18.2/plotly.min.js" integrity="sha512-D52Rvz8mPwpAIIg9bRTFYiyy3GlBIE7kN8wGscKV+EgN8tJB7x7scvLlCBsK2KfYXQvPclyv1uY6E8+0HU+sfA==" crossorigin="anonymous" referrerpolicy="no-referrer"></script>'))

In [5]:
#@title [Load data and set variables]

if nb_mode == "run":
    # Model Families
    model_families = Dict()
    model_families_2 = Dict()
    with open("../experimental_campaign/resources/bio_models_database.csv", "r") as f:
        reader = csv.DictReader(f)
        for row in reader:
            model_idx = int(row["model_idx"])
            model_families[model_idx] = row["model_class"]
            model_families_2[model_idx] = row["model_class_2"]

    # Experiment Variants & Data
    experiment_variants = {1: "random search", 3: "curiosity search"}#, 2: "imgep m=3"}
    experiment_data = DictTree.load("../experimental_campaign/analysis/experiment_data_statistics.pickle")
    evaluation_data = DictTree.load("../experimental_campaign/analysis/evaluation_data_statistics.pickle")
    evaluation_data_examples = DictTree.load("../experimental_campaign/analysis/evaluation_data_examples.pickle")
    
    # Random networks versatility
    random_networks_versatility = jnp.load("../experimental_campaign/resources/random_networks_versatility.npy")

    # Util variables
    model_ids = np.array([key[0] for key in experiment_data.keys()])
    observed_node_names = np.array([key[1] for key in experiment_data.keys()])
    deltaT = 0.1
    epsilon = 0.05
    robustness_threshold = 0.05
    std_ratio = 1/4

# AI-driven Automated Discovery Tools Reveal Diverse Behavioral Competencies of Biological Networks

Authors | Affiliation | Published
--------|-------------|----------
[Mayalen Etcheverry](https://mayalenetcheverry.com) | [INRIA, Flowers team](https://flowers.inria.fr/), [Poietis](https://poietis.com/) | September, 2023
[Clément Moulin-Frier](http://clement-moulin-frier.github.io/) | [INRIA, Flowers team](https://flowers.inria.fr/) |
[Pierre-Yves Oudeyer](http://www.pyoudeyer.com/) | [INRIA, Flowers team](https://flowers.inria.fr/) |
[Michael Levin](https://drmichaellevin.org/) | [The Levin Lab, Tufts University](https://drmichaellevin.org/)| <a href="https://github.com/flowersteam/curious-exploration-of-grn-competencies/tree/main/notebooks/paper.ipynb" target="_blank" id="colablink" class="colab-root"><span id="reprotext">Reproduce in </span><span class="colab-span">Notebook</span></a>

[TOC]

## Abstract

Many applications in biomedicine and synthetic bioengineering depend on
the ability to understand, map, predict, and control the complex,
context-sensitive behavior of chemical and genetic networks. The
emerging field of diverse intelligence has offered frameworks with which
to investigate and exploit surprising problem-solving capacities of
unconventional agents. However, for systems that are not conventional
animals used in behavior science, there are few quantitative tools that
facilitate exploration of their competencies, especially when their complexity 
makes it infeasible to use unguided exploration. Here, we formalize and investigate a
view of gene regulatory networks as agents navigating a problem space.
We develop automated tools to efficiently map the repertoire of robust
goal states that GRNs can reach despite perturbations. 
These tools rely on two main contributions that
we make in this paper: (1) Using curiosity-driven exploration
algorithms, originating from the AI community to explore the range of
behavioral abilities of a given system, that we adapt and leverage to
automatically discover the range of reachable goal states of GRNs and
(2) Proposing a battery of empirical tests inspired by implementation-agnostic 
behaviorist approaches to assess their navigation competencies. Our
data reveal that models inferred from real biological data can reach a
surprisingly wide spectrum of steady states, while showcasing various
competencies that living agents often exhibit, in physiological network
dynamics and that do not require structural changes of network
properties or connectivity. Furthermore, we investigate the
applicability of the discovered "behavioral catalogs" for comparing the
evolved competencies across classes of evolved biological networks, as
well as for the design of drug interventions in biomedical contexts or
for the design of synthetic gene networks in bioengineering. Altogether,
these automated tools and the resulting emphasis on behavior-shaping and
exploitation of innate competencies open the path to better
interrogation platforms for exploring the complex behavior of biological
networks in an efficient and cost-effective manner. To read the
interactive version of this paper, please visit [https://developmentalsystems.org/curious-exploration-of-grn-competencies/paper.html](https://developmentalsystems.org/curious-exploration-of-grn-competencies/paper.html).

## Introduction

Developing methods to recognize, map, predict, and control the complex,
context-sensitive behavior of chemical and genetic networks is an
essential frontier of research in science and engineering. These
systems, such as gene regulatory networks and protein pathways, are
known to be instructive drivers of embryogenesis, cell behavior, and
complex physiology [^sanz-ezquerroEditorialSignalingPathways2017][^padilla-longoriaGeneRegulatoryNetwork2008][^huangCellFatesHighDimensional2005].
Understanding the control properties of these systems is critical not
only for the study of evolutionary developmental biology [^davidsonEmergingPropertiesAnimal2010][^peterEvolutionGeneRegulatory2011][^tusscherEvolutionNetworksBody2011][^kimHowCriticalityGene2018][^srivastavaCasualResemblanceRigorous2021],
but also for comprehending and intervening in various disease states,
including cancer [^singhDifferentialGeneRegulatory2018][^qinExplorationDiseasespecificGene2019][^fazilatyGeneRegulatoryNetwork2019],
and for the construction of novel synthetic biologicals in
bioengineering contexts[^daviesSyntheticMorphologyActive2022][^todaProgrammingSelforganizingMulticellular2018][^todaEngineeringSyntheticMorphogen2020][^hoNovelSyntheticBiology2021][^santorelliSyntheticDevelopmentBuilding2019].

Thus, much work has gone into mathematical modeling and computational
inference of both protein pathways and gene regulatory network models [^dejongModelingSimulationGenetic2002][^schlittCurrentApproachesGene2007][^fetrowNewComputationalApproaches2018][^delgadoComputationalMethodsGene2019],
which has resulted in the development of large collections of
publicly-available models such as the Biomodels database [^glontBioModelsExpandingHorizons2018][^malik-sheriffBioModels15Years2020]. Yet,
despite the wealth of available models, scientists still largely lack an
effective understanding of the range of possible behaviors that these
models can exhibit under different initial conditions and environmental
stimuli, and are in search of systematic methods to reveal and optimize
those behaviors via external interventions. The full extent of the
computational and control properties of such networks are not yet
well-understood; while dynamical systems theory has been extensively
used to characterize their behavior [^kauffman1993origins][^kauffman1995home], it is not
known what other sets of tools might reveal and exploit interesting
properties of this ubiquitous biological substrate. The field of diverse intelligence (also known as basal cognition) 
has suggested that strong functional symmetries between
pathway networks and neural networks could imply the existence of
learning and other kinds of behavior in this unconventional substrate [^abramsonBehavioristApproachesInvestigating2021][^baluskaHavingNoHead2016][^dodig-crnkovicCognitionMorphologicalMorphogenetic2022][^timsitIdeaMolecularBrains2021][^katzEmbodyingProbabilisticInference2018].
Specifically, it has been hypothesized that gene regulatory networks
(GRNs) and other molecular networks could be endowed with surprising
navigation competencies allowing them to robustly reach diverse
homeostatic or allostatic states despite a wide range of perturbations [^csermelyLearningSignalingNetworks2020][^gyurkoAdaptationLearningMolecular2013][^fieldsCompetencyNavigatingArbitrary2022a][^watsonAssociativeMemoryGene2010], and that
exploiting these innate competencies could provide a promising roadmap
for the design of interventions in regenerative medicine and
bioengineering contexts [^mathewsCellularSignalingPathways2023][^lagasseFutureMedicineMolecular2023].

However, significant challenges remain in practice for the exploration
and behavior-shaping of these innate competencies, which presents a
barrier to the use of these ideas in regenerative medicine and
bioengineering. Because of the non-linearity and redundancy in pathway
dynamics, passive exploration strategies such as random screening are
likely to either fail in uncovering the full range of potential
behaviors or require time and energy beyond the available resources.
Here, we formalize and investigate a view of gene regulatory networks as
agents navigating a problem space. We propose a framework and automated
tools, leveraging (1) curiosity-driven goal-directed exploration
algorithms coming from recent advances in machine learning and (2) a
battery of empirical tests inspired from behaviorist approaches, for
mapping the repertoire of robust goal states that GRNs can reach within
this problem space despite various perturbations.  A key novelty of this work is the use of AI-based exploration tools to map the space of possible behaviors in biological networks, which opens interesting avenues for efficient mapping of unfamiliar system behaviors,
yielding transferable insights for diverse problem-solving once such a
map is discovered.

The challenge of exploring and mapping spaces of complex and
self-organized behaviors appears in many fields such as diverse
intelligence in biological systems, minimal active matter or robotics:
many systems in these areas provide a rich space of evolved, engineered,
and hybrid systems that offer many of the same fundamental problems of
behavior and control regardless of specific composition or provenance
[^clawsonEndlessFormsMost2022]. These span many
orders of spatio-temporal scale, from molecular assemblies to swarms of
complex organisms [^timsitIdeaMolecularBrains2021][^kristSimpleTheoryMolecular2021][^cejkovaDropletsLiquidRobots2017][^hanczycModelsMinimalPhysical2011]. One set of
approaches seeks to develop tools to identify the optimal level of
control, ranging from physical rewiring to various methods from
cybernetics and behavioral sciences, to reveal and exploit the native
competencies and computational capacities of these systems [^daviesSyntheticMorphologyActive2022]. Specifically, it
is increasingly realized that the level of competency (and thus the
appropriate level of control) often cannot be guessed by inspection of a
system's components, and that its position on a spectrum ranging from
passive matter to complex metacognition must be determined empirically
[^clawsonEndlessFormsMost2022][^rosenbluethBehaviorPurposeTeleology1943][^bongardLivingThingsAre2021][^levinTechnologicalApproachMind2022].
This is critical not only for fundamental understanding of evolution of
bodies and minds [^baluskaHavingNoHead2016][^lyonBiogenicApproachCognition2006][^barandiaranWhatMakesCertain2006][^di2000minimal][^mcgivernActiveMaterialsMinimal2020][^levinDarwinAgentialMaterials2023], but also for the
design of interventions in biomedicine and synthetic morphology contexts
[^pezzuloRememberingBodyApplications2015][^pezzuloTopdownModelsBiology2016]. Yet, a
common property in many of these systems is that it is expensive in time
and energy to conduct experiments: empirical exploration needs to be
made under limited resources. Thus, methods for automating *efficient*
exploration and discovery of a diversity of behaviors in these spaces
may be widely useful. As explained below, we will here leverage methods
from developmental artificial intelligence initially designed for the
specific purpose of exploring a diversity of behaviors using a limited
budget of experiments.

One especially fascinating set of systems concerns cellular molecular
pathways, or gene regulatory networks (GRNs). In the lab or clinic,
these pathways are usually treated as simple machines, with intervention
strategies focusing on rewiring their structure to achieve a desired
outcome: adding or removing nodes (gene therapy), or changing connection
weights (by targeting promoter sequences or protein structures)
[^wongRevealingTargetedTherapy2008][^samuelCorrectingCalciumDysregulation2018][^krzysztonGenecircuitTherapyHorizon2021][^baumInsertionalMutagenesisGene2007]. However,
the emergent, generative nature of development and physiology ensure
that it is often very hard to know which genes/proteins to modify, and
how, in order to reach a complex desired system-level outcome
[^loboLinearencodingModelExplains2014]. Moreover, the
responses of cells and tissues to drugs changes over time, making it
even more difficult to infer specific interventions (e.g. drugs) that
will induce a stable improvement in pathway state *in vivo*. Indeed,
with the exception of antibiotics and surgery, most available treatment
modalities do not solve the underlying problem -- they seek to mitigate
symptoms, which recur (or expand) once the drug is withdrawn. This is
because current therapeutics function bottom-up, attempting to force
specific molecular states, as it has been challenging to develop methods
for shifting complex tissues and organs towards a stable health profile.
Next-generation solutions, which would offer true healing (stable
correction), require an understanding of the homeostatic and allostatic
properties of networks with respect to how they traverse the space of
transcriptional, physiological and anatomical states. An understanding
of the behavior policies of networks as they dynamically navigate these
problem spaces is essential for predicting what stimuli can be used to
re-set their setpoints and guide them to autonomously maintain a healthy
state. In the language of behavioral neuroscience, this strategy
corresponds to exploiting their native robustness, decision-making, and
navigational competencies to induce predictable, long-lasting changes in
functionality.

Significant challenges remain in revealing and controlling the range
of behaviors that can self-organize in these cellular and molecular
pathways . To characterize steady-state concentrations and responses to
small perturbations, conventional methods rely on piecewise-linear
approximation of the system behavior [^stadterBenchmarkingNumericalIntegration2021][^ingallsFrequencyDomainApproach2004][^ingallsSensitivityAnalysisModel2008][^donzeParameterSynthesisNonlinear2010][^dangComputingReachableStates2011], but
struggle with higher-dimensional systems or wider parameter ranges which
limits their applicability [^donzeRobustnessAnalysisBehavior2011]. Other works have
proposed the porting of tools from network control theory to identify
sets of control nodes allowing to drive the network behavior toward
target steady states [^rozumLeveragingNetworkStructure2022]. These methods
typically exploit the network topology [^rozumLeveragingNetworkStructure2022][^steinwayCombinatorialInterventionsInhibit2015][^zanudoCellFateReprogramming2015][^zanudoStructurebasedControlComplex2017][^cifuentesfontanalsControlStrategyIdentification2020] or
regulatory structure [^murrugarraIdentificationControlTargets2016][^chooPhenotypeControlKernel2018][^chooMinimalInterveningControl2019] to identify
control strategies based either on permanent knockout/activation of
genes or on temporary perturbations, the latter being preferable in
biomedical context.

However, these approaches often require prior knowledge of target
attractor states or are limited to Boolean network models. Other works
have explored the use of machine learning tools, such as evolutionary
search [^paladuguSilicoEvolutionFunctional2006][^francoisEvolvingPhenotypicNetworks2014][^nomanEvolvingRobustGene2015] and
gradient-descent optimization [^hiscockAdaptingMachinelearningAlgorithms2019][^shenFindingGeneNetwork2021], for controlling
continuous ODE biomolecular networks with high-dimensional parameter
spaces, mainly in the context of synthetic circuit engineering [^camachoNextGenerationMachineLearning2018][^volkBiosystemsDesignMachine2020]. While providing
powerful optimization tools, these approaches tend to focus on rewiring
network structure and connectivity. Moreover, the choice of a predefined
fitness function and parameter range initialization is not only critical
to the success of optimization [^francoisEvolvingPhenotypicNetworks2014] but largely
restricts exploration of the behavior space [^shenFindingGeneNetwork2021].

In contrast, an alternative line of research proposes exploring and
leveraging the inherent molecular mechanisms of adaptivity and
robustness in cellular pathways as a promising approach for drug
interventions that do not rely on genomic editing or gene therapy [^csermelyLearningSignalingNetworks2020][^kitanoRobustnessbasedApproachSystemsoriented2007]. Recently,
a broad, substrate-independent behavior science perspective suggests novel properties of gene regulatory networks (GRNs)
and other biological networks [^manickaCognitiveLensPrimer2019][^abramsonBehavioristApproachesInvestigating2021]. This perspective
views GRNs as agents that convert activation levels of specific genes
(inputs) to those of effector genes (outputs), with intermediate nodes
in between, leading to strategies for controlling network behavior based
on a specific history of inputs (experience) rather than through network
rewiring. Notably, the concept of training a chemical pathway using
pulsed input stimuli (node activation or suppression drugs) has been
formalized, and several networks have been analyzed to establish a
taxonomy of memory types found in biological GRNs and pathways [^biswasGeneRegulatoryNetworks2021][^biswasLearningTranscriptionalNetwork2023].

Here, building upon recent research [^fieldsCompetencyNavigatingArbitrary2022a][^biswasGeneRegulatoryNetworks2021][^biswasLearningTranscriptionalNetwork2023], we take the next
step and investigate a view of gene regulatory networks as agents
navigating a problem space toward target goal states with varying
degrees of competency ([Figure 1](#147n2zr)-a). We seek to implement a definition of goal that abstracts it from conventional associations with human or other advanced brains and facilitates the use of tools from cybernetics, behavior science, and control theory to understand broader aspects of biological regulation. Here we use the term “goal” state to refer to a system’s steady state, which it expends effort to reach despite interventions or barriers - a definition appropriate to the study of basal (or minimal) proto-cognitive regulatory systems.. Our definition of goal does not imply “purpose” (high-level goals where an agent has the meta-cognition to think about having goals and what they might be), and we do not attribute high-level competencies (such as re-setting one’s own goals) to GRNs.

Our particular focus lies in investigating two types of navigation
competencies: *versatility*, which refers to the capacity to reach
diverse goal states under different interventions, and *robustness*,
which refers to the ability to reach a goal state despite various
perturbations. The primary scientific question we aim to address is:
What is the repertoire of robust goal states that a GRN can actively
reach through *minimal* and *non-genetic* interventions within a
*navigation task* context, and can we develop systematic methods and
automated tools to aid scientists in discovering this repertoire?

In [6]:
#@title [Figure 1]
fig_idx = 1

if nb_mode == "run":
    fig = f"figures/paper_fig_{fig_idx}.png"
            
elif nb_mode == "load":
    fig = f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.png"
    
# Fig size and title
width, height = int(2654*0.5), int(1584*0.5)
t = 'Overview of the proposed framework. (a) MOTIVATION: We often focus on studying the navigation and behavior of organisms in conventional three-dimensional environments, neglecting the intelligence underlying competencies at sub-organismal scales [^fieldsCompetencyNavigatingArbitrary2022a]. ' \
'To better understand navigation competencies in unconventional organisms solving problems in unconventional spaces (e.g., embryos in morphological space), it is essential to construct comprehensive "behavioral catalogs" for these novel entities, ' \
'which in turn requires sophisticated exploration methods to discover the extent of possible behaviors. Images are taken and adapted from [^latiesSocietyExperimentalAnalysis1987][^amdamMeasuringAnimalPreferences2012][^mcleoldBehavioralPerspectivePsychology2022][^muruganMechanosensationMediatesLongRange2021][^mikhaltsovParameciumBursaria2013][^bongardTherePlentyRoom2023]. ' \
'(b) EXPERIMENTAL DESIGNS: We formalize GRN behavior as a navigation task and propose to investigate it by defining abstract and observer-dependent "problem spaces" that we use to organize the observed biological behaviors and their exploration in practice. ' \
'(c) AUTOMATED EXPERIMENTATION: Pseudo-code of the curiosity-driven goal exploration process we use to automate the discovery of behavioral abilities that the GRN can exhibit in behavior space. ' \
'(d) EMPIRICAL TESTS: We use a battery of empirical tests to identify the robust goal states of the systems, i.e. the one that can be attained under a wide variety of perturbation (including noise in gene expression, and pushes or walls during traversal of transcription space). ' \
'(e) PERSPECTIVES: We explore several potential reuses of the discovered "behavioral catalog" and proposed framework across evolutionary biology, biomedicine and bioengineering contexts.'

# Render Fig
html_fig = make_html_fig(fig_idx, fig, width, height, None, config={'scrollZoom': True})
display(HTML(html_fig))
if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [7]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

To address this question in practice, our experimental framework
revolves around the definition of "problem spaces", which we use as
tractable components of the GRN's overall state space ([Figure1](#147n2zr)-b), and on a set of methodological
contributions which we organize around three sub-questions:

1.  *Automated discovery of diverse behavioral abilities with autotelic curiosity search* ([Figure 1](#147n2zr)-c): 
    What is the range of possible goal states that GRNs can exhibit and how
    can we devise efficient exploration strategies to automatically
    identify these goal states? Defining goal states as attractor
    states of the underlying gene regulatory network, we show that
    traditional screening methods can be very inefficient in
    discovering the range of possible goal states. To address this, we
    propose to use intrinsically-motivated goal exploration processes
    (IMGEP) [^baranesActiveLearningInverse2013][^forestierIntrinsicallyMotivatedGoal2022], a recent
    family of diversity-driven machine learning approaches also known
    as *autotelic* *curiosity search* which was recently shown to form
    a useful discovery assistant for revealing the behavioral
    diversity of unfamiliar systems such as chemical oil-droplet
    systems[^grizouCuriousFormulationRobot2020],
    physical non-equilibrium systems [^falkCuriositydrivenSearchNovel2023] and models of
    continuous cellular automata [^reinkeIntrinsicallyMotivatedDiscovery2020][^etcheverryHierarchicallyOrganizedLatent2020][^hamonLearningSensorimotorAgency2022].

2.  *Evaluation of the navigation competencies* ([Figure
    1](#147n2zr)-d): How competent is the GRN, in terms
    of robustness to perturbations, in attaining the diverse
    previously-identified goal states? Prior studies have offered
    definitions of robustness in biological networks, characterized as
    the degree of variation in functionality [^kitanoTheoryBiologicalRobustness2007] or phenotypic
    trait [^felixPervasiveRobustnessBiological2015] under
    specific environmental or genetic changes. However, these studies
    often consider a predefined functionality and random perturbations
    in network parameters [^ingoliaTopologyRobustnessDrosophila2004][^maRobustnessModularDesign2006][^nomanEvolvingRobustGene2015] or specific
    gene knockouts [^deutscherMultipleKnockoutAnalysis2006].
    Environmental perturbations on the other hand are often limited to
    random variations in initial conditions within a predefined range
    [^donzeRobustnessAnalysisBehavior2011][^vondassowSegmentPolarityNetwork2000].
    Here, inspired from behaviorist approaches, we test hypotheses
    about non-genetic resistance with respect to various navigation
    competencies that living agents often exhibit, and that do not
    require structural changes of network properties or connectivity.
    Those tests assess the system's ability to maintain robustness
    despite various perturbations encountered during traversal,
    including developmental noise in gene expression levels, sudden
    "pushes" within transcriptional space, and the presence of
    energy barriers or "walls" acting as force fields in the
    environment.

3.  *Potential reuses of the discovered "behavioral catalog" and
    framework* ([Figure 1](#147n2zr)-e): Can the
    constructed behavioral catalogs be useful for fundamental research
    and practical therapeutic applications, and can the framework be
    easily applied to other systems and problem spaces? We propose
    that the discovered competencies may provide valuable insights for
    understanding evolvability and developmental robustness, and
    provide a fertile source for the design of interventions in
    biomedicine and synthetic morphology contexts. We also suggest
    that the framework and automated tools, which are observer-focused
    and substrate-independent, could be transposed to other
    systems and problem spaces.

The overall framework is summarized in Figure 1. Applying it on a
database of 30 continuous (ODE) models from the Biomodels website,
consisting of a total of 432 systems defined as GRN model-behavior space
tuples, revealed several interesting insights. First, results suggested
that most of the surveyed systems are capable of reaching a surprisingly
wide spectrum of steady states depending on their initial state.
Interestingly, random screening strategies were not able to reveal this
diversity of reachable states (or at least not in a sample efficient
way), confirming the need for more advanced exploration strategies like
curiosity search. Secondly, among the discovered steady states, we were
able to identify several robust goal states i.e. ones that the system
consistently reaches despite various perturbations during traversal of
transcriptional space. Altogether, these findings seem to suggest that
cell phenotype and functionality could be the result of a multi-step
program [^steinwayCombinatorialInterventionsInhibit2015] that could
be flexibly and robustly reprogrammed by appropriate stimuli
[^levinTechnologicalApproachMind2022]. Finally, we
demonstrate possible reuses of this "behavioral catalog" for comparing
the network's competencies across different classes of organisms, as
well as for the design of non-genetic drug interventions. We also
demonstrate an alternative reuse of the framework to reveal new kinds of
reachable "goals" in synthetic gene networks, suggesting alternative
strategies for the design of gene networks in a bioengineering context.

An interactive executable version of the paper, as well as step-by-step
tutorials and notebooks can be found online at
[[https://developmentalsystems.org/curious-exploration-of-grn-competencies]{.underline}](https://developmentalsystems.org/curious-exploration-of-grn-competencies).
The full codebase of the proposed automated experimentation pipeline is
written end-to-end in JAX, a high-performance numerical computing
library that we leverage for parallel experimentation and computational
speedups of the ODE models time-course simulations.


## Results

### Generalizing GRN behavior as a navigation task

**Dynamical Systems Terminology** | **Behavioral Science Terminology** | **Proposed Isomorphism** | **Navigation Task Terminology**
-----|-----|-----|-----
**system**: a set of interconnected elements that interact to produce emergent behavior | **organism**: a living being that responds to stimuli and adapts to its environment | Both are collections of lower-level elements that interact to produce emergent behavior and can adapt at the system level | **agent** or **GRN** 
**phase-space trajectory**: set of states taken by the system when starting from one particular initial condition | **behavioral trajectory**: the sequence of states that an organism exhibits in response to stimuli | Both represent the sequence of states or behaviors that a system or individual experiences over time | **trajectory**
**initial condition**: initial state of a system's variables and parameters that condition its dynamics | **stimuli**: events that might (or might not) trigger a response in an organism | Both represent incoming variations that set a system or organism in motion | **intervention** or **perturbation** 
**critical parameter:** a parameter or condition that, if changed, can cause a system to undergo a qualitative change or phase transition | **salient stimuli:** stimuli that are particularly relevant or meaningful to an organism, either because they are associated with reward or punishment or because they are novel or unexpected | Both represent the incoming variations that have a significant impact on a system's steady-state or organism's response  | **effective intervention**
**steady-state (or attractor)**: a stable state (or set of states), towards which the system tends to evolve over time | **observed response**: outcome or endpoint of a behavioral trajectory towards which an organism converges | Both represent the endpoint that a system or organism is moving towards | **reached endpoint** or **goal**
**robust attractor:** stable attractor toward which the system tends to evolve under various initial conditions and perturbations | **target goal:** it is assumed that an organism engages in a goal-directed manner when it exhibits new ways or actions to achieve a similar outcome when faced with novel circumstances | Both represent a stable endpoint or goal that the system successfully attains under various perturbations | **robust goal**
 **controllability**: degree to which the system's dynamics (and resulting steady states) can be controlled or manipulated | **trainability:** degree to which an organism's behavior can be modified or shaped by experience or conditioning | Both represent the capacity of a system or individual to be influenced or changed by controlled interventions | **versatility** 
 
<span style="font-size: 0.8em; color: rgba(0, 0, 0, 0.6)"><b style="font-size: 1em;">Table 1: </b> Glossary of terms used in this paper, with the proposed isomorphism  which generalizes concepts from dynamical complex systems and behavioral sciences under a common navigation task perspective. 
 </span><br><br>

The GRNs analyzed in this study are biological pathway networks taken from the BioModels repository [^glontBioModelsExpandingHorizons2018][^malik-sheriffBioModels15Years2020]. The term "GRN" is used broadly to include protein interaction, gene regulatory, and metabolic networks. In these mathematical models, the dynamic interactions between nodes of the network (molecular species) are modeled with a system of ordinary differential equations, enabling to quantitatively simulate time-course behavior (model rollouts) and observe the dynamics of node activities over time (Figure 2a). Here, following a terminology which aims to integrate concepts from dynamical complex systems with concepts from behavioral sciences, we propose to conceptualize GRN behavior as a *navigation task* (Table 1). Model rollouts are viewed as "trajectories" in transcriptional space where network steady states are "goal states" (endpoints) that the "agent" (GRN) can reach with varying levels of competencies. As for living agents, these competencies may range from unstable locomotion patterns to more advanced forms of goal-directed behavior like path following, obstacle avoidance, or even forms of spatial memory and foresight. In this paper, we are particularly interested in investigating two forms of navigation competencies that we refer to as *versatility*, the capacity to reach diverse goal states under various interventions, and *robustness*, the capacity to reach a goal state despite various perturbations. Note that versatility and robustness are studied with respect to different sources of incoming environmental variation, respectively interventions and perturbations.


| **Problem Space** | **Generic definition** | **Specific definition in this study** |
| --- | --- | --- | 
| **Observation Space (O)** | Space of raw observations made during the GRN model rollout to measure its state or behavior | Records node activities over time as $o = \left( y(0),\ldots,y(T) \right)$, where y(t) is an n-dimensional vector (n = number of nodes) and T is the measured reaction time |
| **Behavior Space (Z)** | A projection of the observation space used by the experimenter to encode the "goal states" of a model rollout into a tractable (lower-dimensional) space | Encodes the trajectory endpoint of a model rollout. Represents a cell phenotype defined by the state values of some nodes (relevant biological markers), such that $z = \left( y_{i1}(T),\cdots y_{im}(T) \right)$ (we use m=2 in this study for simplicity and visualization) |
| **Intervention Space (I)** | A space where interventions represent controlled sources of incoming variation that the experimenter can exert on the GRN model rollout to drive it toward novel or targeted states | Sets the initial state $i = \left( y_{1}(0),\ldots,y_{n}(0) \right)$ of a model rollout. Defined as a hyper-rectangle $I ⊆ ℝⁿ$ where the boundaries are proportional to the min and max values taken by the respective nodes from default initial conditions |
| **Perturbation Space (U)** | A space where perturbations represent external sources of incoming variation, used by the experimenter to characterize the robustness of a given goal state | Includes three classes of (stochastic) perturbations including noise perturbation $U_{n}$, push perturbation $U_{p}$, and wall perturbation $U_{w}$ |


<span style="font-size: 0.8em; color: rgba(0, 0, 0, 0.6)"><b style="font-size: 1em;">Table 2: </b> Problem spaces used in this study </span><br><br>

To investigate these competencies in practice, our experimental framework is based on the definition of "problem spaces", which include the observation space (O), behavior space (Z), intervention space (I) and perturbation space (U) as defined in Table 2. To be consistent with our navigation task terminology introduced in Table 1, we refer to a behavior z as the reached "goal state" of a GRN trajectory. However these "goals" may lie on a continuum between complete robustness and high sensitivity, and our primary interest lies in identifying *robust* goals of the system. Whereas several choices could be made for the intervention space I and perturbation space U, we intentionally consider *minimal* and *non-genetic* interventions to investigate the "native" goal states of the GRN, and *environmental obstacles* to investigate for navigation competencies classically observed in other living agents. Examples of simulations, interventions, and perturbations are illustrated in Figure 2.

Then, a typical analysis using our framework relies on a 2-step procedure, detailed in the subsequent sections. First, to assess the versatility of the GRN, we define an exploration strategy which organizes the sequence of interventions $i_{1},\ldots,i_{N}$ used to drive the system toward a maximally diverse set of reachable endpoints \{ $z_{k} \in Z$ \}$_{k = 1,N}$ , while being given a limited budget of experiments N. Secondly, to assess the robustness of the discovered goal states \{${ z}_{k} \in Z$ \}, we conduct a battery of empirical tests to characterize their degree of sensitivity to novel perturbations, with a fixed experimental budget of P perturbations per selected behavior z. At the end of this 2-step procedure, we obtain the "behavioral catalog" (H) of the studied GRN, which includes the history of experiments $H = $ \{$( i_{k},o_{k},z_{k},~$ \{ $( u_{p},o_{p},z_{p} ),~p = 1...P$ \} $ ),~~k = 1\ldots N$ \}. 

Following this framework, the behavioral catalog is constructed for a database of 30 biological networks consisting of a total of 432 systems, where a system is defined as a (GRN model, intervention space (I), behavior space (Z)) tuple, as described in Materials and Methods and Table S1. These catalogs provide valuable empirical observations and insights into the navigation competencies of the studied GRNs, particularly in their ability to consistently achieve diverse goal states under various tested perturbations. Statistical analyses of the results are presented in Figures 3, 5, and 7, and specific results for the RKIP-ERK signaling pathway [^kwang-hyunMathematicalModelingInfluence2003] are shown in Figures 2, 4, 6, and 8.

In [8]:
#@title [Figure 2]
fig_idx = 2

# Compute or Load Fig
if nb_mode == "run":
    
    fig = make_subplots(rows=2, cols=3, 
                        subplot_titles=("<b>(a) observation</b>", 
                                        "<b>(b) behavior</b>", 
                                        "<b>(c) intervention</b>",
                                        "<b>(d) noise perturbation</b>",
                                        "<b>(e) push perturbation</b>",
                                        "<b>(f) wall perturbation</b>"), horizontal_spacing=0.1, vertical_spacing=0.1)
    fig.update_layout(default_layout)
    fig.update_annotations(default_annotation_layout)
    
    tutofig_to_rowcol = {'1': (1, 1), '2': (1, 2), '3': (1, 3),
                         '6': (2, 1), '7': (2, 2), '8': (2, 3)}
    show_tutofig1_legend = False
    
    for tutofig_idx, (row, col) in tutofig_to_rowcol.items():
        # tuto_fig_json = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/tuto1_fig_{tutofig_idx}.json").text
        # tuto_fig = plotly.io.from_json(tuto_fig_json)
        tuto_fig = plotly.io.read_json(f"figures/tuto1_fig_{tutofig_idx}.json")
        
        plot_idx = fig._grid_ref[row-1][col-1][0].trace_kwargs['xaxis'][1:]

        for d in tuto_fig.data:
            if d.xaxis == "x":
                continue
            else:
                d.xaxis = f'x{plot_idx}'
                d.yaxis = f'y{plot_idx}'
                
                d.showlegend = False

                if tutofig_idx == '2':
                    d.marker.colorbar.xanchor="left"
                    d.marker.colorbar.x = 0.4
                    d.marker.colorbar.yanchor="top"
                    d.marker.colorbar.y = 1.
                    d.marker.colorbar.len = 0.2
                else:
                    d.marker.colorbar = {}

                fig.add_trace(d, row=row, col=col)

        for a in tuto_fig.layout.annotations:
            if a.xref == "x":
                continue
            else:
                if a.xref is not None:
                    a.xref = re.sub('\d', plot_idx, a.xref)
                if a.yref is not None:
                    a.yref = re.sub('\d', plot_idx, a.yref)
                if a.axref is not None:
                    a.axref = re.sub('\d', plot_idx, a.axref)
                if a.ayref is not None:
                    a.ayref = re.sub('\d', plot_idx, a.ayref)

            fig.add_annotation(a, row=row, col=col)
        
        if not hasattr(tuto_fig.layout, 'xaxis2'):
            fig.update_xaxes(tuto_fig.layout.xaxis, **default_layout.xaxis, row=row, col=col)
            fig.update_yaxes(tuto_fig.layout.yaxis, **default_layout.yaxis, row=row, col=col)
        else:
            xaxes = tuto_fig.layout.xaxis2.to_plotly_json()
            xaxes.pop('anchor', None)
            xaxes.pop('domain', None)
            fig.update_xaxes(xaxes, **default_layout.xaxis, row=row, col=col)
            yaxes = tuto_fig.layout.yaxis2.to_plotly_json()
            yaxes.pop('anchor', None)
            yaxes.pop('domain', None)
            fig.update_yaxes(yaxes, **default_layout.yaxis, row=row, col=col)
            
        if show_tutofig1_legend and tutofig_idx == '1':
            legend = tuto_fig.layout.legend
            legend.x=0.28
            legend.xanchor="right"
            legend.font.size=10
            fig.update_layout(legend=legend)
        

    # Serialize fig to json and save
    if nb_save_figs:
        fig.write_json(f"figures/paper_fig_{fig_idx}.json")
        
            
elif nb_mode == "load":
    json_fig = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.json").text
    fig = plotly.io.from_json(json_fig)

    
# Fig size and title
width, height = 940,280*2
t = "Illustration of the experimental setup and chosen problem spaces on an example GRN model which has 10 nodes and models the influence of RKIP on the ERK Signaling Pathway [^kwang-hyunMathematicalModelingInfluence2003]. "\
"(a) Time-course evolution of the different nodes y1, ..., y10 (one color per node) when starting from the default initial conditions (as provided in [^kwang-hyunMathematicalModelingInfluence2003]). "\
r"The observation captures the states taken through time $o=[y(t=0), ..., y(t=T)]$ where $y=[y_1, ..., y_{10}]$. "\
"(b) Corresponding trajectory in transcriptional space (phase space), for two target nodes (ERK, RKIPP_RP), from t=0 (A, in red) to T=1000 seconds (B, in cyan). "\
r"We can see that the trajectory converges to endpoint B in less than 100 seconds, and then stay there. The behavior (or reached goal state) is the endpoint $B = \left\lbrack y_{ERK}(T),y_{RKIPRP}(T) \right\rbrack$, "\
r"where T is chosen big enough to ensure convergence. (c) The intervention is setting the initial state of the system trajectory (for all nodes): $i = [y_1(t=0), ..., y_{10}(t=0)]$. "\
"(d-e) Example of perturbations used in this paper. (d) Noise perturbation, here applied to all 10 nodes every 5 secs until t=80 secs. (e) Push perturbation, here applied to the two target nodes (ERK, RKIPP_RP) at t=3 seconds. "\
"(f) Wall perturbation, also applied to the two target nodes (ERK, RKIPP_RP), here at 10% and 90% of the total distance traveled. "\
'Supplementary Figure S1 shows examples of other possible "drug" or "genome" interventions that can be implemented in the accompanying software, as well as the possibility to perform interventions (or perturbations) in parallel using batched computations.'


# Render Fig
html_fig = make_html_fig(fig_idx, fig, width, height, None)
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [9]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

### Curiosity Search Uncovers a Diversity of Reachable Goal States

In [10]:
# Taken from https://stackoverflow.com/questions/67505252/plotly-box-p-value-significant-annotation
def add_p_value_annotation(fig, array_columns, subplot=None, _format=dict(interline=0.07, text_height=1.07, color='black')):
    ''' Adds notations giving the p-value between two box plot data (t-test two-sided comparison)
    
    Parameters:
    ----------
    fig: figure
        plotly boxplot figure
    array_columns: np.array
        array of which columns to compare 
        e.g.: [[0,1], [1,2]] compares column 0 with 1 and 1 with 2
    subplot: None or int
        specifies if the figures has subplots and what subplot to add the notation to
    _format: dict
        format characteristics for the lines

    Returns:
    -------
    fig: figure
        figure with the added notation
    '''
    # Specify in what y_range to plot for each pair of columns
    y_range = np.zeros([len(array_columns), 2])
    for i in range(len(array_columns)):
        y_range[i] = [1.01+i*_format['interline'], 1.02+i*_format['interline']]

    # Get values from figure
    fig_dict = fig.to_dict()

    # Get indices if working with subplots
    if subplot:
        if subplot == 1:
            subplot_str = ''
        else:
            subplot_str =str(subplot)
        indices = [] #Change the box index to the indices of the data for that subplot
        for index, data in enumerate(fig_dict['data']):
            #print(index, data['xaxis'], 'x' + subplot_str)
            if data['xaxis'] == 'x' + subplot_str:
                indices = np.append(indices, index)
        indices = [int(i) for i in indices]
    else:
        subplot_str = ''

    # Print the p-values
    for index, column_pair in enumerate(array_columns):
        if subplot:
            data_pair = [indices[column_pair[0]], indices[column_pair[1]]]
        else:
            data_pair = column_pair

        # Mare sure it is selecting the data and subplot you want
        #print('0:', fig_dict['data'][data_pair[0]]['name'], fig_dict['data'][data_pair[0]]['xaxis'])
        #print('1:', fig_dict['data'][data_pair[1]]['name'], fig_dict['data'][data_pair[1]]['xaxis'])

        # Get the p-value
        pvalue = ttest_ind(
            fig_dict['data'][data_pair[0]]['y'],
            fig_dict['data'][data_pair[1]]['y'],
            equal_var=False,
        )[1]
        if pvalue >= 0.05:
            symbol = 'ns'
        elif pvalue >= 0.01: 
            symbol = '*'
        elif pvalue >= 0.001:
            symbol = '**'
        else:
            symbol = '***'
        # Vertical line
        fig.add_shape(type="line",
            xref="x"+subplot_str, yref="y"+subplot_str+" domain",
            x0=column_pair[0], y0=y_range[index][0], 
            x1=column_pair[0], y1=y_range[index][1],
            line=dict(color=_format['color'], width=2,)
        )
        # Horizontal line
        fig.add_shape(type="line",
            xref="x"+subplot_str, yref="y"+subplot_str+" domain",
            x0=column_pair[0], y0=y_range[index][1], 
            x1=column_pair[1], y1=y_range[index][1],
            line=dict(color=_format['color'], width=2,)
        )
        # Vertical line
        fig.add_shape(type="line",
            xref="x"+subplot_str, yref="y"+subplot_str+" domain",
            x0=column_pair[1], y0=y_range[index][0], 
            x1=column_pair[1], y1=y_range[index][1],
            line=dict(color=_format['color'], width=2,)
        )
        ## add text at the correct x, y coordinates
        ## for bars, there is a direct mapping from the bar number to 0, 1, 2...
        fig.add_annotation(dict(font=dict(color=_format['color'],size=14),
            x=(column_pair[0] + column_pair[1])/2,
            y=y_range[index][1]*_format['text_height'],
            showarrow=False,
            text=symbol,
            textangle=0,
            xref="x"+subplot_str,
            yref="y"+subplot_str+" domain"
        ))
    return fig

In [11]:
#@title [Figure 3]
fig_idx = 3

if nb_mode == "run":
    
    fig = make_subplots(rows=3, cols=6, vertical_spacing=0.07, horizontal_spacing=0.05, row_heights=[1.5,1,1],
                        subplot_titles=["<b>(a) Diversity discovered by random and curiosity search</b><br>  <br>  "] + [None]+
                        ["<b>(b) Examples where curiosity search is useful </b><br> <br> Model 69, Nodes (0,4)"]+["Model 455, Nodes (4,5)", "Model 647, Nodes (0,6)"] + 
                        ["<b>(c) Examples where random search is sufficient </b><br> <br> Model 272, Nodes (2,3)"]+["Model 240, Nodes (1,4)", "Model 641, Nodes (1,2)"],
                        specs=[[{"colspan":3, "b":0.05, "r": 0.05}, None, None, {"colspan":3, "b":0.05}, None, None],
                               [{"colspan":2}, None, {"colspan":2}, None, {"colspan":2}, None],
                               [{"colspan":2}, None, {"colspan":2}, None, {"colspan":2}, None]])
    fig.update_layout(default_layout, margin_t=40)
    fig.update_annotations(default_annotation_layout)
    
    # STATISTICS
    all_covered_areas = Dict()
    for trace_idx, (exp_idx, exp_name) in enumerate(experiment_variants.items()):
        covered_areas = jnp.array([experiment_data[system_key].covered_areas[exp_idx][epsilon] for system_key in experiment_data.keys()])/ (1+2*epsilon)**2
        covered_areas *= 100
        all_covered_areas[exp_idx] = covered_areas
        x = jnp.arange(covered_areas.shape[-1])
        y = covered_areas.mean(0)
        y_upper = y + std_ratio*covered_areas.std(0)
        y_lower = y - std_ratio*covered_areas.std(0)

        if exp_name == "random search":
            ys = [covered_areas[:, 450], covered_areas[:, 900]]
            names = [exp_name+"<br>(n=450)", exp_name+"<br>(n=900)"]
            legendname = "random search (RS)"
        else:
            ys = [covered_areas[:, 450]]
            names = [exp_name+"<br>(n=450)"]
            legendname = "curiosity search (IMGEP)"
            
        fig.add_trace(go.Scatter(x=x, y=y, line=dict(color=default_colors[trace_idx]),
                                 legendgroup=exp_name, name=legendname, hovertemplate = '(%{x:.2f}, %{y:.2f})<extra></extra>'), row=1, col=1)
        fig.add_trace(go.Scatter(x=jnp.concatenate([x, x[::-1]]), y=jnp.concatenate([y_upper, y_lower[::-1]]), 
                                 fill='toself', fillcolor=default_colors_shade[trace_idx],
                                 line=dict(color='rgba(0,0,0,0)'), hoverinfo="skip", 
                                 legendgroup=exp_name, showlegend=False), row=1, col=1)
        fig.add_vline(x=450, line_width=2, line_dash="dash", annotation_text="n=450", row=1, col=1)
        fig.add_vline(x=900, line_width=2, line_dash="dash", annotation_text="n=900", row=1, col=1)
        
        for (y, name) in zip(ys, names):
            fig.add_trace(go.Box(y=y, name=name, legendgroup=exp_name, showlegend=False, 
                                 line=dict(color=default_colors[trace_idx]), fillcolor=default_colors_shade[trace_idx],
                                 boxpoints='all', pointpos=0., hovertemplate = '<b>%{text}</b><br>'+'<i>Diversity</i>: %{y:.2f}<extra></extra>',
                                 text = [f'Model #{model_idx}, nodes {node_names[0]}, {node_names[1]}' for (model_idx, node_names) 
                                        in zip(model_ids, observed_node_names)]
                                   ), row=1, col=4)
            
    # Significance tests
    x1 = []
    x2 = []
    for exploration_run in range(90, 900, 20):
        # 1) compare imgep discoveries with last random search discoveries
        p_value = ttest_ind(all_covered_areas[3][:, min(exploration_run, 450-1)], all_covered_areas[1][:, 900-1]).pvalue
        if p_value < 0.05 and all_covered_areas[3][:, min(exploration_run, 450-1)].mean() >= all_covered_areas[1][:, 900-1].mean():
            x1.append(exploration_run)
        p_value = ttest_ind(all_covered_areas[3][:, min(exploration_run, 450-1)], all_covered_areas[1][:, exploration_run]).pvalue
        if p_value < 0.05:
            x2.append(exploration_run)
    fig.add_trace(go.Scatter(x=x2, y=[62]*len(x), mode="markers", marker=Dict(size=4, color=default_colors[-3], symbol="circle"), name="IMGEP(n)>RS(n)"), row=1, col=1)
    fig.add_trace(go.Scatter(x=x1, y=[60]*len(x), mode="markers", marker=Dict(size=4, color=default_colors[-1], symbol="circle"), name="IMGEP(n)>RS(900)"), row=1, col=1)
    
    fig = add_p_value_annotation(fig, [[0,2], [1,2]], subplot=2, _format=dict(interline=0.07, text_height=1.07, color='black'))
    

    fig.update_xaxes(title_text="n (# exploration runs)", row=1, col=1)
    fig.update_yaxes(**default_layout.yaxis, title_text="discovered diversity (% of covered area)", row=1)
    
    # EXAMPLES
    imgep_perfs = all_covered_areas[3][:, -1]-all_covered_areas[1][:, 450]
    imgep_sorted_perfs = imgep_perfs.argsort()
    example_ids = jnp.concatenate([imgep_sorted_perfs[-3:][::-1], imgep_sorted_perfs[jnp.array([4,1,0])]])

    n_traces_per_example = {}
    for rel_idx, sample_idx in enumerate(example_ids):
        n_traces_per_example[str(sample_idx)] = 0
        system_key = list(experiment_data.keys())[sample_idx]
        model_idx, observed_nodes_ids = system_key

        for (exp_idx, exp_name) in reversed(experiment_variants.items()):
            if exp_name == "random search":
                col_idx = 0
            else:
                col_idx = 1
            
            # Plot scatter of reached endpoints
            x = experiment_data[system_key].normalized_reached_endpoints[exp_idx][:, 0]
            y = experiment_data[system_key].normalized_reached_endpoints[exp_idx][:, 1]
            fig.add_trace(go.Scatter(x=x, y=y, name=exp_name, legendgroup=exp_name, showlegend=False, 
                                     mode='markers', marker_color=default_colors[col_idx], marker_size=4,
                                     hovertemplate = 'i=%{pointNumber} (%{x:.2f}, %{y:.2f})<extra></extra>'), 
                          row=2+rel_idx//3, col=1+2*(rel_idx%3))

            # Plot corresponding polygons
            poly = experiment_data[system_key].union_polygon[exp_idx][epsilon]
            x, y = [], []
            if poly.geom_type == 'MultiPolygon':
                for geom in poly.geoms:
                    geom_x, geom_y = geom.exterior.coords.xy
                    x.append(np.array(geom_x))
                    y.append(np.array(geom_y))
            elif poly.geom_type == 'Polygon':
                geom_x, geom_y = poly.exterior.coords.xy
                x.append(np.array(geom_x))
                y.append(np.array(geom_y))
            for x, y in zip(x,y):
                fig.add_trace(go.Scatter(x=x, y=y, name=exp_name, fill="toself", fillcolor=default_colors_shade[col_idx],
                                         line=dict(color=default_colors[col_idx]), hoverinfo="skip", legendgroup=exp_name, showlegend=False),  
                              row=2+rel_idx//3, col=1+2*(rel_idx%3))
    
    for row_idx in [2,3]:
        for col_idx in [1,3,5]:
            # Add background shape
            fig.add_vrect(x0=0.-1.8*epsilon, x1=1+1.8*epsilon, 
                          fillcolor="#BAE1FF", opacity=.8,
                          line=dict(color="#6C8EBF", width=2), 
                          annotation_text="Behavior Space <i>Z</i>", annotation_position="right bottom", annotation_font=dict(color='black', size=14),
                          layer="below", row=row_idx, col=col_idx)
            fig.update_xaxes(visible=False, range=[0.-2*epsilon, 1.+2*epsilon], row=row_idx, col=col_idx)
            fig.update_yaxes(visible=False, range=[0.-2*epsilon, 1.+2*epsilon], row=row_idx, col=col_idx)
    
    
    # Serialize fig to json and save
    if nb_save_figs:
        fig.write_json(f"figures/paper_fig_{fig_idx}.json")
        
            
elif nb_mode == "load":
    json_fig = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.json").text
    fig = plotly.io.from_json(json_fig)

# Display Fig
width, height = 940, 920
t = f"Curiosity search uncovers a wide spectrum of reachable states in behavior space Z. "\
"(a) Diversity of endpoints discovered by random search (pink) and curiosity search (blue) for the 432 systems. "\
r"Diversity is measured as the volume of the union of the set of hyperballs of radius $\epsilon$ that have for centers the discovered endpoints \{$z \in Z$\} as depicted by the shaded area in (b-c) with $\epsilon = 0.05$. "\
"(a-left) Mean and standard deviation curves of the diversity of behaviors discovered throughout exploration (with random search having twice more experiments n=900). Dots indicate significance (p<0.05) when testing curiosity search (n) against random search (n) in brown, "\
"and against random search (n=900) in black, with a Welch's t-test. Standard deviation is divided by 4 for visibility. "\
"(a-right) Detail of the diversity obtained in the left plot for all 432 systems at n=450 and n=900, where *** indicate significance (p<0.001). "\
"(b-c) Discovered endpoints at the end of exploration (n=450) by random search (pink) and curiosity search (blue) for 6 example systems of our database. "\
"(b) Examples of systems for which curiosity search is much more sample-efficient than random search in finding a diversity of reachable states in behavior space Z. "\
r"(c) Examples of systems with low-redundancy mapping $I \rightarrow Z$ such that random search in $I$ is already quite efficient in covering behavior space Z, and curiosity search performs equivalently."

html_fig = make_html_fig(fig_idx, fig, width, height, None)
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [12]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

One advantage of modeling GRN behavior within a tractable behavior space Z is that we can then deploy strategies to efficiently discover and map that space. Notably, recent diversity-driven machine learning techniques such as Novelty Search [^lehmanExploitingOpenEndednessSolve2008][^lehmanAbandoningObjectivesEvolution2011], Quality Diversity [^cullyRobotsThatCan2015][^pughQualityDiversityNew2016] and Intrinsically-Motivated Goal Exploration Processes (IMGEP) [^baranesActiveLearningInverse2013][^forestierIntrinsicallyMotivatedGoal2022] are explicitly designed to efficiently explore a so-called "behavior space" or "goal space" which is basically a (predefined or learned) model of the overall state space. In particular IMGEPs, which were originally developed for the learning of inverse models of highly-redundant mapping in robotics context [^baranesActiveLearningInverse2013], were recently shown to successfully assist discovery in complex self-organizing systems [^grizouCuriousFormulationRobot2020][^falkCuriositydrivenSearchNovel2023][^reinkeIntrinsicallyMotivatedDiscovery2020][^etcheverryHierarchicallyOrganizedLatent2020].

Here, we propose to use an IMGEP to control GRN initial states and maximize the diversity of discovered endpoints \{$z \in Z$ \} within a limited budget of $N$ experiments. The IMGEP operates in two phases: initially, $N_{int}$ interventions are sampled randomly from $I$ to populate history $H$, then remaining interventions are generated through a goal-directed process which relies on several key internal models. Those including a goal-embedding module $(R)$ that encodes observations $(o)$ into the IMGEP goal space $(Ƭ)$, a goal generator module $(G)$ that samples goals from the goal space based on intrinsic motivation incentives (e.g. to promote novelty or learning progress), and a goal-conditioned optimization policy $(\Pi)$ that generates candidate intervention parameters to achieve the current goal. Given those internal models, the goal-directed phase iterates through 1) sample a target goal $g \sim G(H)$, 2) infer intervention parameters to achieve that goal $i \sim \Pi(g,H)$, 3) conduct an experiment with the intervention i, observe the outcome o, and compute the reached goal $z = R(o)$, and 4) store the tuple $(i,o,z)$ in history $H$. Here, we use the GRN behavior space Z as the IMGEP goal space $Ƭ = Z$. Hence "target goal" refers to a goal sampled by IMGEP while "reached goal" refers to an actual endpoint of the GRN trajectory, discovered by IMGEP while targeting a potentially different point in Z. Throughout exploration, the IMGEP dynamically refines its Z-traversal strategy based on the knowledge acquired by its discoveries. Here we opt for a simple IMGEP variant such that the exploration process can be seen as performing novelty search in behavior space Z [^doncieuxNoveltySearchTheoretical2019]. The pseudocode of our IMGEP pipeline is shown in Figure 1-c and details about the internal models are provided in Materials and Methods. The final outcome is a "behavioral catalog" of the GRN, containing the diverse goal states discovered by IMGEP: $H =$  \{ $( i_{k},o_{k},z_{k} ),~~k = 1\ldots N$\}.

We deploy the IMGEP, also known as "curiosity search," on all 432 systems in the biological network database. Our evaluation focuses on two related competencies: the IMGEP agent's ability to empirically reveal a diversity of reachable goal states in the (GRN, I, Z) system, referred to as "discovered diversity," and the GRN agent's competency to naturally reach diverse goal states, referred to as "versatility." The true versatility of the GRN is unknown and can only be inferred through empirical exploration and proxy metrics.

For evaluating diversity, we measure the area covered in Z by the IMGEP discoveries using the threshold-coverage metric [^benureauSelfExplorationSensorimotor] and compare it with the area covered by the diversity of a naive random screening strategy (which uniformly samples interventions in $I$). In Figure 3, the diversity discovered by the two exploration variants is shown for the 432 $(GRN,I,Z)$ systems, where random search is given a budget of experiments $N$ which is twice bigger (N=900) as the one given to the curiosity-search algorithm (N=450). Interestingly we see that, on average, at n=290 the curiosity search already significantly outperforms the final diversity achieved by random search, while only utilizing one-third of its experimental budget (N=900). Whereas we are dealing with numerical systems and our codebase allow for efficient and parallel execution, each experiment still consists of $\frac{T}{\Delta T} = 25000$ model steps, where each step integrates the ODE system. Repeating that N times for each of the 432 systems starts to be very costly, which is why having efficient exploration strategies is very valuable (and would be even more valuable when scaling the framework to larger databases). Even more critical, as illustrated in Figure 3-b, it seems that, for some systems, random search is not able to discover the "latent" regions revealed by the IMGEP in Z, or it would need an extremely large budget of experiments. On the other hand, as illustrated in Figure 3-c, there are some systems for which random search is already quite efficient in revealing diverse behaviors in Z, and for which IMGEP performs equivalently.

In fact, the goal-directed strategy of the IMGEP is particularly beneficial for $(GRN,I,Z)$ systems with high nonlinearity or redundancy in their $I \rightarrow Z$ mapping, as seen in Figure 4 and studied in robotics contexts [^benureauSelfExplorationSensorimotor]. Redundancy implies that many interventions in $I$ lead to similar effects in $Z$, as illustrated in Figure 2 where various interventions and perturbations converge to the same endpoint. In these systems, random search will preferentially discover points in areas of high redundancy in Z whereas the IMGEP, whose exploration is directed uniformly in goal space, should cover different levels of redundancy equally. In general, when dealing with large intervention spaces and limited experimental budgets, curiosity search can be particularly useful for efficiently navigating Z-space.

In [13]:
#@title [Figure 4]
fig_idx = 4

if nb_mode == "run":

    tutofig_idx = 17
    fig = plotly.io.read_json(f"figures/tuto1_fig_{tutofig_idx}.json")


    # Serialize fig to json and save
    if nb_save_figs:
        fig.write_json(f"figures/paper_fig_{fig_idx}.json")
        
            
elif nb_mode == "load":
    json_fig = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.json").text
    fig = plotly.io.from_json(json_fig)

# Display Fig
width, height = 940, 800
t = r"Illustration of the non linearity and redundancy of the $I \rightarrow Z$ mapping, and of the interest of using goal-directed exploration strategies.  "\
"Plot shows the reachable points discovered by curiosity search (a) and by random search (b)  in the behavior space Z and their corresponding starting points in the intervention space I, for the RKIP-ERK signaling pathway system [^kwang-hyunMathematicalModelingInfluence2003]. "\
"The intervention space is 10-dimensional, and here we show the TSNE reduction in 2D. We apply HDBSCAN clustering [^mcinnes2017hdbscan] on the points discovered in Z, which produced the 4 clusters for curiosity search (displayed in gray, green, purple and orange; non-assigned points are displayed in light blue) "\
"and 2 clusters for random search  (displayed in light and dark orange). We then visualize where those regions in behavior space mapped back in the intervention space, by applying the same coloring. "\
r"(a) Looking at the curiosity search discoveries, we can see the non-linearity of the $I \rightarrow Z$ mapping, where small regions of intervention space can map to large regions of the behavior space (like the orange area) and reversely (gray area). "\
"We can also see the redundancy of the behavior space which is clearly concentrated in the left border of the space (ERK close to zero) which can seemingly be reached from very large portions of the intervention space (gray area). "\
"(b) Looking at random search discoveries, we can understand that it is very inefficient as it spends most of its exploration budget in the region of intervention space that converges to the left border in Z, "\
"and fails to explore the orange, purple and green regions discovered by curiosity search which seemingly lead to the more novelty in Z."

html_fig = make_html_fig(fig_idx, fig, width, height, None)
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [14]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

Finally, as the IMGEP efficiently drives the GRN into diverse goal states with minimal interventions, we propose that the diversity achieved by the IMGEP can serve as a good proxy metric of the GRN versatility. Notably, analysis of example systems in Figure 3 reveals that many GRNs can reach a broad spectrum of steady states. Whereas our database is limited to certain systems (see Materials and Methods) and might not be representative of all biological pathways, this observation underlines the existence of various phenotypes that can be realized. It also highlights the critical importance of identifying salient interventions that can effectively control cellular states within this spectrum of possibilities, notably as many cancer types are due to epigenetically non-identical cells [^bellPrinciplesMechanismsNongenetic2020].

### Empirical Tests Reveal Robust Navigation Competencies

In [15]:
if nb_mode == "run":
    
    test_tasks = {
            "noise_std": [0.001, 0.005, 0.01],
            "noise_period": [10, 5, 1],
            "push_magnitude": [0.05, 0.1, 0.15],
            "push_number": [1, 2, 3],
            "wall_length": [0.05, 0.1, 0.15],
            "wall_number": [1, 2, 3]
        }
            
    # Calc Median Sensitivity per test
    sensitivity_data = {}
    for var_name, var_range in test_tasks.items():
        for var_val in var_range:
            sensitivity_data[f"{var_name}_{var_val}"] = []

    eval_model_ids = []
    eval_node_ids = []
    for system_key in evaluation_data.keys():
        valid_system_key = True
        for var_name, var_range in test_tasks.items():
            for var_val in var_range:
                endpoints_sensitivity = evaluation_data[system_key].endpoints_sensitivity[3][var_name][var_val]
                valid_points_ids = ~jnp.isnan(endpoints_sensitivity) & ~jnp.isinf(endpoints_sensitivity)
                if valid_points_ids.sum()<0.5*len(valid_points_ids):
                    valid_system_key = False
                    continue
                sensitivity_data[f"{var_name}_{var_val}"].append(jnp.median(endpoints_sensitivity[valid_points_ids]))
        if valid_system_key:
            eval_model_ids.append(system_key[0])
            eval_node_ids.append(system_key[1])
    eval_system_keys = [(model_idx, node_ids) for (model_idx, node_ids) in zip(eval_model_ids, eval_node_ids)]
    eval_model_ids = np.array(eval_model_ids)
    eval_node_ids = np.array(eval_node_ids)
    
    for var_name, var_range in test_tasks.items():
        for var_val in var_range:
            sensitivity_data[f"{var_name}_{var_val}"] = jnp.array(sensitivity_data[f"{var_name}_{var_val}"])

    # Average results per group "noise", "push" and "wall"   
    avg_sensitivity_data = {"noise": None, "push": None, "wall": None}
    for test_key, test_data in sensitivity_data.items():
        test_group = test_key.split("_")[0]
        if avg_sensitivity_data[test_group] is None:
            avg_sensitivity_data[test_group] = test_data / 6
        else:
            avg_sensitivity_data[test_group] += test_data / 6

In [16]:
#@title [Figure 5]
fig_idx = 5

if nb_mode == "run":
    # one system per row, one example of task/traj per col
    display_examples = {
        (10, (3,7)): [("noise_std", "0.001", 7, 0, "bottom left"), ("noise_std", "0.005", 25, 0, "bottom right"), 
                      ("noise_std", "0.01", 34, 0, "bottom right"), ("noise_period", "10", 43, 0, "top right"),
                      ("noise_period", "5", 32, 0, "bottom left"),  ("noise_period", "1", 7, 0, "bottom left")],
        (52,(4,7)): [("noise_std", "0.001", 31, 0, "top left"), ("noise_std", "0.005", 36, 0, "top left"), 
                      ("noise_std", "0.01", 27, 0, "top left"), ("noise_period", "10", 19, 0, "top left"),
                      ("noise_period", "5", 35, 0, "top left"),  ("noise_period", "1", 40, 0, "top left")
                    ],
        (647,(2,10)): [("push_magnitude", "0.05", 38, 0, "top right"), ("push_magnitude", "0.1", 6, 0, "top left"), 
                      ("push_magnitude", "0.15", 0, 0, "bottom right"), ("push_number", "1", 10, 0, "bottom right"),
                      ("push_number", "2", 15, 0, "bottom right"),  ("push_number", "3", 13, 0, "bottom right")
                    ],
        (284, (4,6)): [("push_magnitude", "0.05", 4, 0, "top left"), ("push_magnitude", "0.1", 13, 0, "top right"), 
                      ("push_magnitude", "0.15", 30, 0, "bottom right"), ("push_number", "1", 43, 0, "top right"),
                      ("push_number", "2", 32, 0, "top right"),  ("push_number", "3", 3, 0, "top left")
                    ],
        (84, (4,6)): [("wall_length", "0.05", 5, 0, "top left"), ("wall_length", "0.1", 7, 0, "top left"), 
                      ("wall_length", "0.15", 15, 0, "top right"), ("wall_number", "1", 35, 0, "top left"),
                      ("wall_number", "2", 21, 0, "top left"),  ("wall_number", "3", 38, 0, "bottom right")
                    ], 
        (272, (2,3)): [("wall_length", "0.05", 29, 0, "top left"), ("wall_length", "0.1", 28, 0, "bottom right"), 
                      ("wall_length", "0.15", 42, 0, "bottom right"), ("wall_number", "1", 10, 0, "top left"),
                      ("wall_number", "2", 5, 0, "bottom right"),  ("wall_number", "3", 30, 0, "bottom right")
                    ],
                       } 
    annotate_examples = True
    annotate_wall = False
    annotate_push = False
    annotate_start_end_points = True

    fig = make_subplots(rows=3+6, cols=6, specs=[[{"rowspan":3, "colspan":3, "b":0.05, "r": 0.05}, None, None, {"colspan":3, "b":0.02}, None, None], 
                                                   [None, None,  None, {"colspan":3, "b":0.02}, None, None], 
                                                   [None, None,  None, {"colspan":3, "b":0.05}, None, None]]+[[{}, {}, {}, {}, {}, {}]]*6,
                       subplot_titles=["<b>(a) Robustness tests statistics</b>"] + [None]*3+
                        ["<b>(b) NOISE not-robust </b>"]+[""]*5+ ["<b>(c) NOISE robust </b>"]+[""]*5+
                        ["<b>(d) PUSH not-robust </b>"]+[""]*5+ ["<b>(e) PUSH robust </b>"]+[""]*5+
                        ["<b>(f) WALL not-robust </b>"]+[""]*5+ ["<b>(g) WALL robust </b>"]+[""]*5,
                       row_titles=[f"Model {system_key[0]} <br> Nodes ({system_key[1][0]}, {system_key[1][1]})" for system_key in display_examples.keys()],
                       vertical_spacing=0.02, horizontal_spacing=0.,)

    fig.update_layout(default_layout)
    fig.update_annotations(default_annotation_layout)

    # ------------------------------------- Row 1-2-3 col 1-2: results per group  ----------------------------------------------

    ## Box plots
    for trace_idx, (group_key, group_data) in enumerate(avg_sensitivity_data.items()):
        fig.add_trace(go.Violin(x=np.array(group_key), y=group_data, name=group_key, showlegend=False,
                             points="all", pointpos=0., marker_size=4,
                             line=dict(color=default_colors[trace_idx+3]), fillcolor=default_colors_shade[trace_idx+3],
                             hovertemplate = '<b>%{text}</b><br>'+'<i>Robustness</i>: %{y:.2f}',
                             text = [f'Model #{model_idx}, nodes ({node_names[0]}, {node_names[1]})' for (model_idx, node_names) in zip(eval_model_ids, eval_node_ids)]
                            ),
                      row=1, col=1
                     )

    ## Display selected examples
    if annotate_examples:
        for point_idx, (system_key, example) in enumerate(display_examples.items()):
            key_idx = eval_system_keys.index(system_key)
            x = ["noise", "push", "wall", np.nan]
            y = [avg_sensitivity_data["noise"][key_idx], avg_sensitivity_data["push"][key_idx], avg_sensitivity_data["wall"][key_idx], np.nan]

            fig.add_trace(go.Scatter(x=x, y=y, hoverinfo='skip', #hovertemplate = '<b>%{text}</b><br>'+'<i>Robustness</i>: %{y:.2f}', text=text, 
                                     name=f"{system_key}", showlegend=False,
                                     mode="markers+lines", line=dict(width=1, color=default_colors_shade[point_idx+6]), marker=dict(size=6, color=default_colors[point_idx+6])), row=1, col=1)
            
            annotation_x = example[0][0].split("_")[0]
            annotation_y = avg_sensitivity_data[annotation_x][key_idx]
            annotation_sign = 1 if annotation_y<0.1 else -1
            fig.add_annotation(x=annotation_x, y=annotation_y, ay=annotation_sign*30, text=f"Model {system_key[0]} <br> Nodes ({system_key[1][0]}, {system_key[1][1]})", 
                               arrowcolor=default_colors_shade[point_idx+6], font=dict(color=default_colors[point_idx+6]), row=1, col=1)

    ## Update axes
    fig.update_yaxes(title=dict(text="sensitivity"), row=1, col=1)


    # ------------------------------------- Row 1-2-3 col 2-4-5-6: results per test per group  ----------------------------------------------

    n_tests = len(test_tasks)
    n_vars = len(list(test_tasks.values())[0])
    xticks = sum([list(range(i*n_vars+1+i,i*n_vars+1+i+n_vars)) for i in range(n_tests)], [])

    for trace_idx, (test_key, test_data) in enumerate(sensitivity_data.items()):
        if "noise" in test_key:
            row_idx = 1
        if "push" in test_key:
            row_idx = 2
        if "wall" in test_key:
            row_idx = 3
        fig.add_trace(go.Violin(x=np.array([xticks[trace_idx]]*len(test_data)), y=test_data, name=test_key, showlegend=False,
                                points="all", pointpos=0., marker_size=4,
                                line=dict(color=default_colors[trace_idx//6+3]), fillcolor=default_colors_shade[trace_idx//6+3],
                                hovertemplate = '<b>%{text}</b><br>'+'<i>Robustness</i>: %{y:.2f}',
                                text = [f'Model #{model_idx}, nodes ({node_names[0]}, {node_names[1]})' for (model_idx, node_names) in zip(eval_model_ids, eval_node_ids)]
                            ),
                      row=row_idx, col=4
                     )

    xticks_labels = [f'{test_key.split("_")[-1]}' for test_key in sensitivity_data.keys()]
    for i, task_name in enumerate(test_tasks.keys()):
        xticks_labels[i*n_vars+n_vars//2] += f'<br> {" ".join(task_name.split("_"))}'
    for row_idx in range(3):
        fig.update_xaxes(**default_layout.xaxis, tickmode='array', tickvals=xticks[row_idx*6:(row_idx+1)*6], 
                         ticktext=xticks_labels[row_idx*6:(row_idx+1)*6], tickangle=0, row=row_idx+1, col=4)
        fig.update_yaxes(**default_layout.yaxis, nticks=3, title=dict(text="sensitivity", standoff=1), range=[0., 0.3], row=row_idx+1, col=4)


    #------------------------------------- Row 4-9: Perturbed Trajectories Examples ----------------------------------------------
    for row_idx, (system_key, examples) in enumerate(display_examples.items()):
        model_idx, node_ids = system_key

        for col_idx, (task_name, task_var, eval_traj_idx, perturb_idx, annotation_position) in enumerate(examples):
            
            # load trajs prior and after perturb
            traj_prior_perturb = np.array(evaluation_data_examples[3][system_key][task_name][task_var][eval_traj_idx]["system_outputs_prior_perturb"].ys[np.array(node_ids)])
            traj_after_perturb = np.array(evaluation_data_examples[3][system_key][task_name][task_var][eval_traj_idx][perturb_idx]["system_outputs_after_perturb"].ys[np.array(node_ids)])
            traj_after_perturb_ts = np.array(evaluation_data_examples[3][system_key][task_name][task_var][eval_traj_idx][perturb_idx]["system_outputs_after_perturb"].ts)

            # downsample them
            scaling_vector = np.maximum(np.nanmax(traj_prior_perturb, 1), np.nanmax(traj_after_perturb, 1))
            scaling_vector -= np.minimum(np.nanmin(traj_prior_perturb, 1), np.nanmin(traj_after_perturb, 1))
            traj_prior_perturb, display_ts = downsample_traj(traj_prior_perturb, scaling_vector, 1e-2)
            traj_after_perturb, eval_display_ts = downsample_traj(traj_after_perturb, scaling_vector, 1e-2)
            traj_after_perturb_ts = traj_after_perturb_ts[eval_display_ts]
            
            # plot them
            fig.add_trace(go.Scattergl(x=traj_prior_perturb[0], y=traj_prior_perturb[1], showlegend=False, mode="lines",
                                    line=dict(color="rgba(0,0,0,.6)", width=1), hoverinfo="skip"),
                          row=row_idx+4, col=col_idx+1)

            fig.add_trace(go.Scattergl(x=traj_after_perturb[0], y=traj_after_perturb[1], showlegend=False, mode="markers",
                                       marker=dict(color=traj_after_perturb_ts, colorscale=traj_cscale, size=2),  
                                       hoverinfo="skip"), 
                          row=row_idx+4, col=col_idx+1)


            # Plot walls
            if "wall" in task_name:
                if "number" in task_name:
                    n_walls = int(task_var)
                else:
                    n_walls = 1
                for wall_idx in range(n_walls):
                    x = evaluation_data_examples[3][system_key][task_name][task_var][eval_traj_idx][perturb_idx]["perturbation_params"].y[node_ids[0]][wall_idx].squeeze()
                    y = evaluation_data_examples[3][system_key][task_name][task_var][eval_traj_idx][perturb_idx]["perturbation_params"].y[node_ids[1]][wall_idx].squeeze()
                    fig.add_trace(go.Scatter(x=x, y=y, mode="lines", line_color=default_colors[-1], line_width=2, showlegend=False), row=row_idx+4, col=col_idx+1)
                    if annotate_wall:
                        fig.add_annotation(x=x.mean(), y=y.mean(),  text="wall", font=dict(color='gray', size=8), row=row_idx+4, col=col_idx+1)

            # Annotate pushes
            if "push" in task_name and annotate_push:
                    if "number" in task_name:
                        n_pushs = int(task_var)
                    else:
                        n_pushs = 1
                    for push_idx in range(n_pushs):
                        push_timestep = int(evaluation_data_examples[3][system_key]["push_ts"][n_pushs][push_idx]/deltaT)
                        x = evaluation_data_examples[3][system_key][task_name][task_var][eval_traj_idx]["system_outputs_prior_perturb"].ys[node_ids[0], push_timestep]
                        y = evaluation_data_examples[3][system_key][task_name][task_var][eval_traj_idx]["system_outputs_prior_perturb"].ys[node_ids[1], push_timestep]
                        fig.add_annotation(x=x, y=y,  text="push", font=dict(color='gray', size=8), row=row_idx+4, col=col_idx+1)


            # Annotate Start and End Points  
            if annotate_start_end_points:
                A = traj_prior_perturb[:,0]
                B = traj_prior_perturb[:,-1]
                Bp = traj_after_perturb[:,-1]
                fig.add_annotation(x=A[0], y=A[1], showarrow=False, text="A", row=row_idx+4, col=col_idx+1)
                fig.add_annotation(x=B[0], y=B[1], showarrow=False, text=f"B", row=row_idx+4, col=col_idx+1)
                fig.add_annotation(x=Bp[0], y=Bp[1], showarrow=False, text=f"B'", row=row_idx+4, col=col_idx+1)
                
                
            # Annotate Borders and task info
            x0 = jnp.minimum(traj_prior_perturb[0].min(), traj_after_perturb[0].min())
            x1 = jnp.maximum(traj_prior_perturb[0].max(), traj_after_perturb[0].max())
            fig.add_vrect(x0=x0, x1=x1, line=dict(color='rgba(0, 0, 0, 0.1)', width=1), 
                          annotation_text=f"{task_name.split('_')[-1]}={task_var}, traj #{eval_traj_idx}", annotation_position=annotation_position, annotation_font=dict(color='gray', size=8),
                          row=row_idx+4, col=col_idx+1)
            # idx = fig._grid_ref[row_idx+4-1][col_idx+1-1][0].trace_kwargs['xaxis']
            # fig.add_vrect(xref=f"{idx} domain", x0=0., x1=1.,
            #               line=dict(color='rgba(0, 0, 0, 0.1)', width=1), 
            #               annotation_text=f"{task_name.split('_')[-1]}={task_var}, traj #{eval_traj_idx}", annotation_position=annotation_position, annotation_font=dict(color='gray', size=8),
            #               row=row_idx+4, col=col_idx+1)


            # Update axes
            fig.update_xaxes(title=None, showticklabels=False, visible=False, row=row_idx+4, col=col_idx+1)
            fig.update_yaxes(title=None, showticklabels=False, visible=False, row=row_idx+4, col=col_idx+1)

    
    # Serialize fig to json and save
    if nb_save_figs:
        fig.write_json(f"figures/paper_fig_{fig_idx}.json")
        
            
elif nb_mode == "load":
    json_fig = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.json").text
    fig = plotly.io.from_json(json_fig)

# Display Fig
width, height = 940, 1140
t = "Identification of robust traversal strategies in transcriptional space. "\
"(a) Violin plots show, for each of the 432 systems (one point per system), the median sensitivity (over the K representative goal states) to the noise (green), push (gray) and wall (yellow) perturbation families. "\
"Violin plots on the right detail the median sensitivity for the 18 sub-families. "\
"(b-g) Each row provides examples of perturbed trajectories of either extremely-robust or extremely-sensitive example (GRN, Z) system (on average over the K goal states) for the three families of perturbations, as shown by annotations in (a). "\
"For instance, the first row (b) shows perturbed trajectories of the (model #10, nodes (3,7)) system which has the highest sensitivity to noise whereas the last row (g) shows trajectories of the (model #272, nodes (2,3)) system which has a nearly perfect robustness to walls. "\
"Each image contains an example trajectory for a given $(i,u)$, and one $u$ per sub-family is shown per column. "\
r"For instance, in the first row (b), the trajectories are perturbed with the different sub-families of noise $\left( \sigma_{n} \in \lbrack 0.001,0.005,0.1\rbrack,p_{n} \in \lbrack 10,5,1\rbrack \right)$ which can be seen as various levels of difficulty. "\
"For each trajectory we annotate the starting position (A), endpoint prior perturbation (B), and endpoint after perturbation (B'), and show the original trajectory in black. The perturbed trajectory is shown in colorscale (from red at t=0 to cyan at t=3000 secs). "\
"(b) Except for few cases (trajectory #43), the system (model #10, nodes (3,7)) system is not robust to noise as its trajectories are easily deviated from the original endpoint. "\
"(c) The (model #52, nodes (4,7)) system however, except for rare cases (trajectory #35), consistently reaches its original target despite encountering various amounts of noise. Interestingly, trajectories #36 and #40 consistently follows a complex up->right-down->left path, despite the induced noise. "\
"(d) The (model #647, nodes (2,10)) system, except for few cases (trajectory #0), is typically deviated from its original trajectory when being pushed away. Interestingly though, it seems to follow similar (parallel) trajectories. "\
"(e) The (model #284, nodes (4,6)) system, is an example of an extremely robust system which, despite many push configurations (in magnitude and number), consistently returns to its original trajectory. Interestingly, the trajectories of this system are relatively complex with several loops and detours. "\
"(f) The (model #84, nodes (4,6)) system is not very robust to walls, and typically deviates or blocked when it encounters a wall. "\
"(g) The (model #272, nodes (2,3)) system is another example of an extremely robust system which, despite many wall configurations (in length and number), consistently returns to its original path. Once again interestingly, the trajectories of this system are relatively complex with several loops and detours."
html_fig = make_html_fig(fig_idx, fig, width, height, None)
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [17]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

We are then interested in characterizing the degree of robustness of the previously-discovered "goal states" in order to identify the ones that can consistently be reached by the GRN despite encountering various perturbations. Whereas many studies have proposed rigorous analysis of the "robustness" of biological networks [^kitanoTheoryBiologicalRobustness2007][^felixPervasiveRobustnessBiological2015], the generated perturbations often target variations in the regulatory rules (i.e. variations at the hardware level) and variations are often sampled independently (and prior) to observations of the GRN dynamical behaviors [^donzeRobustnessAnalysisBehavior2011][^nomanEvolvingRobustGene2015][^ingoliaTopologyRobustnessDrosophila2004][^maRobustnessModularDesign2006][^vondassowSegmentPolarityNetwork2000][^rizkGeneralComputationalMethod2009]. Here instead, we propose to conduct a battery of empirical tests that draw inspiration from classical "displacement experiments" [^walcottPigeonHomingObservations1996][^luschiTestingNavigationalAbilities2001] and "barrier experiments" [^bisch-knadenEgocentricInformationHelps2001] commonly used in behavioral sciences to assess the navigation competencies of various animals. As illustrated in Figure 2, we consider *environmental* perturbations that perturb the GRN trajectory with 1) various degree of noise in the gene expression levels, 2) sudden "pushes" during the GRN traversal of transcriptional space, and 3) energy barriers or "walls" acting as new force fields that constrain the GRN traversal. Importantly, those perturbations are *conditioned* on the observed behavior of the GRN. The magnitude of the noise and of the pushes is scaled proportionally to the extent of the observed trajectories, and the walls are generated in locations of the space that the GRN would "naturally" visit without the induced perturbation. While intuitive from a behaviorist point of view, where one would adapt experimentation when testing animals in different contexts (e.g. to study homing behavior of an ant and of a sea turtle, or of an ant in food deprivation and in reproduction phase) [^abramson1994primer], robustness studies in systems biology often neglect those aspects. We propose that a behaviorist lens on robustness can help understanding forms of non-genetic resistance in transcriptional space, which is crucial for the development of therapeutic strategies [^bellPrinciplesMechanismsNongenetic2020].

To assess the degree of robustness of the discovered goal states, our evaluation procedure is the following. For each (GRN, I,Z) system of the database, we retrieve a representative set of trajectories previously discovered using the curiosity-search algorithm and subject these trajectories to $P = s \times r$ perturbations conditioned on the GRN goal-reaching trajectory $i \rightarrow z$ prior perturbation. Here, s represents the different perturbation distributions which correspond to various "tests" and "levels of difficulty" (e.g. noise magnitude and frequency, number of walls, etc.) and $r$ is the number of (stochastic) perturbations sampled per family. The pseudocode is illustrated in Figure 1-c and details about the different family of perturbations are provided in Materials and Methods. At the end of this process, the behavioral catalog is augmented with the perturbed trajectories<br> $H =$ \{$( i_{k},o_{k},z_{k},~$\{$( u_{p},o_{p},z_{p}),~p = 1\ldots P$\}$),~~k = 1\ldots K$\}.

As the use of "spaces" comes with the notion of similarity and distance, we can then easily evaluate the *sensitivity* of a goal state $z$ with respect to a set of perturbation \{$u_{p},p = 1\ldots P$\} as the average distance in behavior space Z between the original trajectory endpoint $z$ and the perturbed trajectories endpoints \{${ z}_{p}$\}. Here our distance is simply the Euclidean distance, normalized by the extent of the trajectory prior perturbation in Z. We can then identify the so-called "robust goals" of the systems as the ones that have the lower sensitivity to perturbations. These sensitivity analyses can be useful in two important ways. On the one hand, they allow us to quickly identify the "extreme" examples of robustness, both at the system-level and at the goal-level, providing several insights into the degree of "competencies" that some biological networks might exhibit in their relative space (Figure 5). On the other hand, these analyses also allow us to map the *heterogeneity* of cellular responses and to better understand how non-genetic perturbations might modulate the *landscape* of reachable cell phenotypes (Figure 6).

Figure 5 shows the median sensitivity, over the representative goal states, for the 432 systems of our database and for the noise, push and wall perturbations families (as well as for the s=18 sub-families which correspond to varying degrees of perturbations). Overall, even though we observe varying degrees of sensitivity between systems (and between magnitudes of perturbations, which is expected), one first and interesting observation is that the median sensitivity remains relatively low, suggesting that GRNs could not only exhibit versatility (with respect to the considered interventions) but also robustness (with respect to the considered perturbations). In fact, looking at the "extreme" examples, we can identify quite impressive examples of complex and yet highly-robust space traversal strategies, with non-linear trajectories exhibiting many "detours" and "loops" but yet consistently reaching the same endpoint despite several pushes (Figure 5-e) or walls (Figure 5-g) on the way.

In [18]:
#@title [Figure 6]
fig_idx = 6

if nb_mode == "run":

    tutofig_idx = 23
    fig = plotly.io.read_json(f"figures/tuto1_fig_{tutofig_idx}.json")

    # Serialize fig to json and save
    if nb_save_figs:
        fig.write_json(f"figures/paper_fig_{fig_idx}.json")
        
            
elif nb_mode == "load":
    json_fig = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.json").text
    fig = plotly.io.from_json(json_fig)

# Display Fig
width, height = 940, 400
t = "Energy landscape visualization based on the trajectory-based landscape generation method [here](#fn:venkatachalapathyTrajectorybasedEnergyLandscapes2021), and constructed from different set of GRN trajectories, respectively trajectories generated "\
"(a) by the random search exploration, (b) by the curiosity-driven exploration, and (c) by the robustness tests experiments." 
html_fig = make_html_fig(fig_idx, fig, width, height, None)
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [19]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

Figure 6 shows how the constructed catalog $H$ can be used to generate the energy landscape of the studied system. In biology, landscape formalisms have been used to comprehend the underlying dynamics of several systems, such as cell cycles and cell differentiation [^liLandscapeFluxReveal2014][^liQuantifyingCellFate2013]. It is believed that such system-level visualizations could be particularly useful to apprehend non-genetic heterogeneity in the context of cancer treatment and stem cell differentiation [^bellPrinciplesMechanismsNongenetic2020][^venkatachalapathyTrajectorybasedEnergyLandscapes2021]. A recent landscape-generation method only proposes to approximate the pseudopotential energy through simulation trajectories obtained throughout exploration of the system [^venkatachalapathyTrajectorybasedEnergyLandscapes2021], making it a widely applicable method which we can directly apply here. However, the paper relied on Monte Carlo simulation to generate the trajectories. Due to the previously mentioned non-linearity and redundancy of the $I \rightarrow Z$ mapping, this can lead to poor estimation of the overall energy landscape (Figure 6-a). Instead, when generating the landscape from the trajectories discovered by our curiosity search exploration, we are able to reveal a new and wide "valley" of reachable states (Figure 6-b). Interestingly, the landscape-generation method can also be used to better comprehend the effect of external cues on the gene regulatory network, by visualizing how much they deform the energy landscape for instance leading to new shaped valleys (Figure 6-c). For the example system RKIP-ERK pathway [^kwang-hyunMathematicalModelingInfluence2003], results highlighted a specific region of behavior space (with low RKIP and high ERK activation levels) that seems to be particularly robust, i.e. consistently reached by the GRN from certain initial conditions, and that might be associated with tumor development [^leeLossRafKinase2006].

### Possible reuses of the behavioral catalog and framework

Our framework generated a catalog of stimuli, responses, and navigation tests for the different GRN models contained in our database. Creating and sharing such a "behavioral catalog" with the scientific community is possibly one of the more exciting aspects of the work with new organisms. Furnished with such an empirically based data-set and detailed observations, one can 1) conduct statistical analysis across the population of studied organisms to inform fundamental research questions and 2) reuse the acquired knowledge to design specific behavior-shaping experiments in organisms of interest. As our framework focuses on observable behavior and is agnostic about the internal construction of the organism, another exciting perspective is to deploy it to different problem spaces and other classes of natural, chimeric or synthetic organisms. This section illustrates preliminary experiments along those three types of reuse.

#### To develop insights on the degree of sophistication of the different GRNs

In [20]:
#@title [Figure 7]
fig_idx = 7

if nb_mode == "run":
    
    fig = make_subplots(rows=1, cols=2, column_titles=["<b>(a) Versatility</b>","<b>(b) Versatility - Wall Robustness</b>"], column_widths=[1, 1.2]) #vertical_spacing=0.05
    fig.update_layout(default_layout)
    fig.update_annotations(default_annotation_layout)
    

    # ------------------------------------- A) Versatility per Class  ----------------------------------------------
    covered_areas = []
    for system_key in eval_system_keys:
        reached_endpoints = (evaluation_data[system_key].endpoints_prior_perturbation[3]-experiment_data[system_key].analytic_bc_space_min)/(experiment_data[system_key].analytic_bc_space_max-experiment_data[system_key].analytic_bc_space_min)
        covered_areas.append(unary_union([Point(endpoint).buffer(epsilon) for endpoint in reached_endpoints]).area / (1+2*epsilon)**2)
    covered_areas = np.array(covered_areas)
 
    
    for row_idx, (cur_model_families, classes) in enumerate([(model_families, ['Plants', 'Bacteria', 'Amphibians', 'Rodents', 'Homo sapiens',  'n/a', 'Generic', 'Slime Mold'])]):

        # Random networks
        fig.add_trace(go.Violin(x=["Random Networks"]*len(random_networks_versatility),
                                y=random_networks_versatility,
                                name=f"Random Networks (n={len(random_networks_versatility)})",
                                box_visible=False,
                                meanline_visible=True,
                                points="all",
                                pointpos=0.,
                                line=dict(color=default_colors[-1]),
                                fillcolor=default_colors_shade[-1],
                                hovertemplate = '<b>%{text}</b><br>'+'<i>Versatility</i>: %{y:.2f}'
                               ),
                      row=row_idx+1, col=1
                     )
        
        # Biological networks per class
        eval_model_classes = np.array([cur_model_families[model_idx] for model_idx in eval_model_ids])
        for trace_idx, model_class in enumerate(classes):
            fig.add_trace(go.Violin(x=eval_model_classes[eval_model_classes==model_class],
                                    y=covered_areas[eval_model_classes==model_class],
                                    name=f"{model_class} (n={(eval_model_classes==model_class).sum()})",
                                    legendgroup=model_class,
                                    box_visible=False,
                                    meanline_visible=True,
                                    points="all",
                                    pointpos=0.,
                                    line=dict(color=default_colors[trace_idx]),
                                    fillcolor=default_colors_shade[trace_idx],
                                    hovertemplate = '<b>%{text}</b><br>'+'<i>Versatility</i>: %{y:.2f}',
                                    text = [f'Model #{model_idx}, nodes {node_names[0]}, {node_names[1]}' for (model_idx, node_names) 
                                            in zip(eval_model_ids[eval_model_classes==model_class], eval_node_ids[eval_model_classes==model_class])]
                                   ),
                          row=row_idx+1, col=1
                         )
        
    # ------------------------------------- B) Versatility-Robustness Pareto-Curves per Class  ----------------------------------------------
    sensitivity_thresholds = jnp.linspace(0., 0.4, 20)
    avg_endpoints_sensitivity = {}
    for key_idx, system_key in enumerate(eval_system_keys):
        avg_endpoints_sensitivity[system_key] = jnp.zeros(45)
        for var_name, var_range in test_tasks.items():
            if "wall" in var_name:
                for var_val in var_range:
                    avg_endpoints_sensitivity[system_key] += evaluation_data[system_key].endpoints_sensitivity[3][var_name][var_val] / 6
                
    for row_idx, (cur_model_families, classes) in enumerate([(model_families, ['Plants', 'Bacteria', 'Amphibians', 'Rodents', 'Homo sapiens',  'n/a', 'Generic', 'Slime Mold'])]):
                                                         # (model_families_2, ['cell division', 'tissue morphostasis', 'stress response', 'tissue organization', 'proliferation', 'sporulation', 
                                                         #                     'cell signaling', 'programmed cell death', 'metabolic control', 'cancer', 'system physiology'])]):
        eval_model_classes = np.array([cur_model_families[model_idx] for model_idx in eval_model_ids])
        for trace_idx, model_class in enumerate(classes):
            y = []
            y_upper = []
            y_lower = []
            for sensitivity_threshold in sensitivity_thresholds:
                robust_covered_areas = []
                for key_idx, system_key in enumerate(eval_system_keys):
                    if eval_model_classes[key_idx] == model_class:
                        robust_endpoints_ids = jnp.where(avg_endpoints_sensitivity[system_key]<=sensitivity_threshold)
                        reached_endpoints = evaluation_data[system_key].endpoints_prior_perturbation[3][robust_endpoints_ids]
                        reached_endpoints = (reached_endpoints-experiment_data[system_key].analytic_bc_space_min)/(experiment_data[system_key].analytic_bc_space_max-experiment_data[system_key].analytic_bc_space_min)
                        robust_covered_areas.append(unary_union([Point(endpoint).buffer(epsilon) for endpoint in reached_endpoints]).area / (1+2*epsilon)**2)
                y_mean = np.array(robust_covered_areas).mean()
                y_std = np.array(robust_covered_areas).std()
                y.append(y_mean)
                y_upper.append(y_mean+std_ratio*y_std)
                y_lower.append(y_mean-std_ratio*y_std)

            fig.add_trace(go.Scatter(x=sensitivity_thresholds,
                                     y=y,
                                     mode="lines+markers",
                                     name=model_class,
                                     legendgroup=model_class,
                                     showlegend=False,
                                     line=dict(color=default_colors[trace_idx]),
                                   ),
                          row=row_idx+1, col=2
                         )
            fig.add_trace(go.Scatter(x=np.concatenate([sensitivity_thresholds, sensitivity_thresholds[::-1]]), 
                                     y=np.concatenate([y_upper, y_lower[::-1]]), 
                                     fill='toself', 
                                     fillcolor=default_colors_shade[trace_idx],
                                     line=dict(color='rgba(0,0,0,0)'), 
                                     hoverinfo="skip", 
                                     name=model_class,
                                     legendgroup=model_class, 
                                     showlegend=False), 
                          row=row_idx+1, col=2)
            fig.update_xaxes(title="robustness threshold x (average sensitivity < x)", autorange="reversed", row=row_idx+1, col=2)        
        
    # Update axes
    fig.update_xaxes(**default_layout.xaxis) 
    fig.update_yaxes(**default_layout.yaxis, title_text="versatility (% of covered area)")
    
    # Serialize fig to json and save
    if nb_save_figs:
        fig.write_json(f"figures/paper_fig_{fig_idx}.json")
        
            
elif nb_mode == "load":
    json_fig = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.json").text
    fig = plotly.io.from_json(json_fig)
    #fig = plotly.io.read_json(f"figures/paper_fig_{fig_idx}.json")
    

# Display Fig
width, height = 940, 400
t = "Analysis and comparison of the degree of sophistication, in terms of versatility and robustness, between different classes of GRN. "\
'We categorize the GRNs by class of organism they belong to: plant, bacteria, slime mold, amphibian, rodent, homo sapiens, or generic. "n/a" refers to network models for which this information is not available. '\
"(a) Violin plots show the versatility of the 432 systems (one point per system) for each class. Versatility of one system is measured as the area covered by all the goal states discovered by curiosity search (equivalent to what we call diversity in Figure 3). "\
"(b) Trade-off (aka Pareto) mean and standard deviation curves that represent the trade-off among versatility and wall robustness performances as taken by the different classes of GRNs (standard deviation is divided by 4 for visibility). "\
"For each system, versatility (y-value) is measured as the area covered by the set of robustly achieved goal states, where the criterion of goal-achievement is a binary which tests whether the goal-reaching sensitivity (on average overall wall perturbations) is below a certain threshold (x-values). "\
"Violin plots in (a) are ordered in ascending order according to the class mean y-value at x=0.4 in (b)."

html_fig = make_html_fig(fig_idx, fig, width, height, None)
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [21]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

A first use-case we explore is to conduct statistical analysis to categorize versatility and robustness in the surveyed networks on the basis of species in evolutionary strata. We consider seven categories, namely, plant, bacteria, slime mold, amphibian, rodent, homo sapiens, or generic. Here, generic corresponds to the networks not associated with any species but related to generalized biological processes. Please note that the surveyed database is relatively small with respect to the wealth of available models and biological pathways, so we can hardly claim that these results represent the true distribution of competencies across these organism categories. Still, as shown in Figure 7, results suggested interesting patterns.

First, on average, generic and Homo sapiens GRNs exhibit higher versatility (mean 0.228 and 0.238) compared to rodent and amphibian GRNs (mean 0.163 and 0.169), which in turn show higher versatility than bacteria and plant GRNs (mean 0.136 and 0.117). These findings are particularly intriguing in the context of the recently-formulated hypothesis of multi-scale competency architecture [^levinTechnologicalApproachMind2022]: could the observed variation in versatility among different classes of GRNs contribute to the degree of versatility observed at higher-level scales? Collecting such experimental data for broader classes of organisms and GRNs will be crucial to understand how competencies at the molecular scale can impact the overall functionality and adaptability of organisms at higher scales, and to understand how evolution might have exploited this modular architecture for shaping the observed adaptivity and reprogrammability of biological systems.

Secondly, when comparing with the versatility of random networks (in black), generated to follow the same distributions of network size and connectivity as biological networks (as proposed in [^biswasLearningTranscriptionalNetwork2023], see Materials and Methods), we observe that random network versatility is much lower (<0.026) than the versatility observed in biological networks. Once again, it is difficult to draw strong conclusions as the gene circuit model used for the random networks is relatively limited, whilst generic and studied across a range of biological contexts [^reinitzMechanismEveStripe1995][^jaegerDynamicalAnalysisRegulatory2004][^cotterellAtlasGeneRegulatory2010][^molinelliPerturbationBiologyInferring2013], and it will be interesting to scale the comparison to a broader and more complex range of ODE-based random models. Still, these findings hint that versatility prevalence might be a strong invariant of biological intelligence shaped by evolutionary processes.

Finally, we categorize the versatility-robustness tradeoff in the different categories of organisms. The idea is to compare the GRN competencies to robustly achieve diverse goal states, for different robustness thresholds. In Figure 7-b, we plot the mean and standard deviation pareto curves for the different categories of organisms and observe that, in average, the pareto-optimal solutions are mostly achieved by generic cell GRNs, even though bacteria GRNs can robustly reach more goal states for exigent robustness criteria (high x-values). The slime mold GRN can reach highly diverse goal states but the tradeoff quickly drops with wall perturbations, and there is only one system in our database belonging to this category so results might be not representative. Once again, those results are very interesting as generic cells GRNs are a building block that has been extensively reused by evolution across several organisms and contexts, bacteria have evolved to be very resistant (e.g. to antibiotics), and slime molds are a unicellular organism well known for its diverse capabilities, especially navigational ones [^vallverduSlimeMouldFundamental2018][^beekmanBrainlessMultiHeadedDecision2015][^saigusaAmoebaeAnticipatePeriodic2008][^nakagakiIntelligentBehaviorsAmoeboid2008].

#### For the development of therapeutic interventions

In [22]:
#@title [Figure 8]
fig_idx = 8

if nb_mode == "run":
    tutofig_idx = 24
    fig = plotly.io.read_json(f"figures/tuto1_fig_{tutofig_idx}.json")

    # Serialize fig to json and save
    if nb_save_figs:
        fig.write_json(f"figures/paper_fig_{fig_idx}.json")
        
            
elif nb_mode == "load":
    json_fig = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.json").text
    fig = plotly.io.from_json(json_fig)

# Display Fig
width, height = 940, 300
t = "Identification of stimuli-based stepwise intervention triggering robust re-set of disease states into healthy physiological states. "\
"(a) The 10 most robust identified goal states (average sensitivity <0.05) and the corresponding reaching trajectories are displayed for the example RKIP-ERK signaling pathway [^kwang-hyunMathematicalModelingInfluence2003]. "\
'We can see that most of them converge toward attractors in the "disease" region (orange). (b) Discovered stepwise stimuli intervention on MEKPP which we apply on states stuck in the "disease" region for 100 seconds. '\
'(c) The discovered intervention successfully brings back all points from the "disease" region closer to the target endpoint in the "healthy" region, and this under various tested perturbations (as shown in Supplementary Figure S2). '\
"The optimization procedure that led to the discovery of this intervention is described in the main text."

html_fig = make_html_fig(fig_idx, fig, width, height, None)
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [23]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

Understanding forms of non-genetic resistance and non-genetic heterogeneity is crucial across a wide range of cancer and treatment contexts [^bellPrinciplesMechanismsNongenetic2020]. Here, we illustrate how the constructed behavioral catalog can provide a fertile source for the design of therapeutic strategies, notably in the context of network control, using again the example of the RKIP-ERK signaling pathway [^kwang-hyunMathematicalModelingInfluence2003]. In Figure 4, we saw that curiosity search revealed four clusters of reachable steady states for this system. From a clinical perspective, one might denote the green cluster as "healthy" region of behavior space and the orange cluster as "disease" region of the behavior space, as high levels of ERK and low-levels of RKIP are often linked to tumor development [^leeLossRafKinase2006]. In Figure 8-a, we plot those two clusters as well as the 10 more robust goal-reaching behaviors from the behavioral catalog of this system, i.e. the goal states with the lower average sensitivity to the induced perturbations. We see that 6 out of the 10 more robust trajectories end up in the "disease" region, suggesting that certain configurations of initial state are very likely to reach that region despite chemical blockers (here pushes, walls, and noise), which was also visible on the system's energy landscape in Figure 6-c. Looking at the six trajectories, it seems that they all follow similar patterns where RKIP activation level increases past a certain threshold, and only then converge toward the disease region. This might already provide an interesting biomarker for prediction of tumor development, but what we are really interested here is to build upon that knowledge to develop stimuli-based interventions allowing to re-set the GRN setpoints from the identified "disease" steady states back to steady states within the identified "healthy" region . To do so, we define a parameterized stimuli-based intervention and a performance function, and search for parameters that optimize this performance. For the intervention function, we use a piecewise constant function that determines which nodes to intervene on (here MEKPP), when to apply the intervention (here every 10 seconds for 100 seconds), and with what amplitude (which are the parameters that we are seeking to optimize). The choice of the intervention function, which is arbitrary in this example, would typically depend on the experimental constraints, e.g. which nodes can be targeted with drugs and at which precision. For the performance function, we define the centroid of the "healthy" region as the target setpoint and compute performance of the stepwise intervention as the average distance of the novel setpoints (after intervention when starting from the 6 disease setpoints) to the target setpoint, and under a distribution of stochastic walls, pushes and noise perturbations. Hence a successful intervention should re-set the disease setpoints to healthy setpoints for all discovered disease states and robustly across the various tested perturbations. For optimization, we simply perform random search as this was sufficient here to discover one intervention (as shown in Figure 8-b) that successfully reset the setpoints (as shown in Figure 8-c) under various tested perturbations (as shown in Supplementary Figure S2). Here random search was sufficient to find a successful intervention, but more advanced optimization strategies like evolutionary algorithms or stochastic gradient descent could be envisaged for harder problems. Overall, mapping the "latent" behavioral abilities of GRNs in healthy physiology and disease states may have important implications for the identification of robust stimuli-based interventions that focus on behavior shaping instead of micromanaging all molecular states, and that can be exploited in therapeutic contexts.

#### As an alternative strategy to gene circuit engineering

In [24]:
#@title [Figure 9]
fig_idx = 9

if nb_mode == "run":
    
    # TODO!

    tutofig_idx = 4
    fig = plotly.io.read_json(f"figures/tuto2_fig_{tutofig_idx}.json")
    
    # Serialize fig to json and save
    if nb_save_figs:
        fig.write_json(f"figures/paper_fig_{fig_idx}.json")
        
            
elif nb_mode == "load":
    json_fig = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.json").text
    fig = plotly.io.from_json(json_fig)

# Display Fig
width, height = 940, 650
t = "Comparison of three alternative strategies for the design of oscillator circuits: curiosity search (blue), random search (pink), and gradient descent (orange). "\
"(a-c) Given a budget of 5000 experiments, curiosity search is able to find 1167 oscillator circuits (ones showing sustained oscillations), whereas random search only finds 42 oscillators and gradient descent does not discover any (starting from a single random initialization). "\
"(a) 3D scatter plot of the 42 random search discoveries (pink) and 1167 curiosity search ones (blue) in the (amplitude, main frequency, offset) analytic behavior space. "\
"(b) Box plots projecting points from the 3D scatter plot into the respective (amplitude, main frequency, offset) axes. "\
"(c) Diversity discovered throughout exploration, where diversity is measured with a binning-based space coverage metric (20 bins per dimension). "\
r"(d) Evolution of the training loss $L$ for the three exploration strategies. (e-f-g) Corresponding best discoveries (for which $L$ is minimal) for the three exploration strategies. "\
"(h-i) Local training loss and resulting finetuning of the best discoveries with gradient descent." 

html_fig = make_html_fig(fig_idx, fig, width, height, None)
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [25]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

The final type of reuse we explore is not a direct reuse of the constructed behavioral catalogs, but rather a reuse of the proposed automated tools to reveal different kinds of behaviors in a bioengineering context. A common problem in synthetic biology is to optimize the configuration and parameters of a gene model network to optimally perform a desired functionality, also known as gene circuit engineering [^volkBiosystemsDesignMachine2020]. Recent approaches rely on optimization-driven machine learning strategies, such as evolutionary algorithms and stochastic gradient descent. However, choosing the right loss function and parameter initialization for these optimization methods is a well-known problem in machine learning. These issues can lead to optimization algorithms getting trapped in local minima within the complex landscape of possibilities. In response to these challenges, we propose to investigate whether the curiosity-driven exploration strategy can be employed as an alternative (diversity-driven) strategy. Whereas traditionally-employed for exploratory purposes, these exploration strategies were also shown to facilitate the resolution of external, pre-defined tasks characterized by sparse or deceptive rewards [^colasGEPPGDecouplingExploration2018], by effectively exploring solution space.

Here, we consider the target application of oscillator circuit engineering followed in [^hiscockAdaptingMachinelearningAlgorithms2019], where parameters of a gene circuit model are optimized to produce oscillation patterns with target amplitude $A$, frequency $w$ and offset $b$. This time, the intervention space includes both genetic interventions (setting kinematic parameters of regulatory rules) and environmental interventions (setting the initial state $y_{0}$). We then compare three alternative exploration strategies: curiosity search, random search and a global optimization strategy using gradient descent as proposed in [^hiscockAdaptingMachinelearningAlgorithms2019], all given the same experimental budget $(N = 5000)$. For curiosity search, the behavior space $Z$ is defined as the image space of the discrete Fourier transform of the observation. We then use the exact same IMGEP algorithm as before, but operating within the novel problem spaces $(I,Z)$. For gradient descent, we follow the procedure proposed in [^hiscockAdaptingMachinelearningAlgorithms2019]. We define a loss function which measures the mean square error between the observed node activation levels $y$ and the target oscillation (represented as a cosine wave). We then randomly initialize the parameters $i \sim U(I)$ and use Adam optimizer for N=5000 optimization steps. In addition, we also use gradient descent for local refinement of the best discoveries made by the other exploration strategies (curiosity search and random search), this time with a limited budget of $N = 100$ optimization steps.

In Figure 9, we show that curiosity search is again significantly more efficient than random search in revealing a diversity of possible oscillator behaviors. Out of 5000 trials, random search was able to find only 42 configurations leading to sustained oscillations whereas curiosity search was able to find 1167 (and gradient descent did not find any). Without focusing on the target objective, curiosity search is able to efficiently cover the analytic $(A,\omega,b)$ space (Figure 9, a-c), thus discovering oscillators close to the target one (Figure 9-e). Instead, when starting from a random initial condition, gradient descent is very likely to get trapped in a local minimum where it converges to the target offset *b* but fails to produce oscillations (Figure 9-d and 9-g). However, whereas the global optimization is unsuccessful in this example, gradient descent seems to be useful to locally refine close-enough solutions, as can be seen here when refining the best discoveries made by curiosity search and random search (Figure 9-h, 9-i). These results suggest that a diversity-driven exploration strategy, eventually combined with a more advanced local optimization strategy, can offer promising and cost-effective alternatives for the design of synthetic gene networks. More generally, as our framework only relies on empirical investigation for inferring the mapping between interventions and behaviors (treating them as abstract variables in observable problem spaces), we believe it offers an exciting perspective to be deployed across various problem spaces and classes of organisms.


## Discussion

This paper presents a novel framework aimed at uncovering the navigation competencies of gene regulatory networks (GRNs). The framework conceptualizes GRNs as agents actively navigating the transcriptional space and provides a set of tools, leveraging computational models of curiosity-driven learning and exploration, with a battery of empirical tests inspired from behaviorist tradition, for automated experimentation and behavioral characterization. The proposed framework is novel in two central ways. First, it introduces a novel AI-based toolbox to the field of biological network analysis. We show how this toolbox, leveraging the successful ingredients of recent intrinsically motivated learning algorithms - originally developed to enable robotic AI agents to explore and learn diverse skills in novel and unstructured environments [^baranesActiveLearningInverse2013][^forestierIntrinsicallyMotivatedGoal2022] - can be transposed to assist efficient discovery of behavioral abilities within biological pathway models like GRNs. Secondly, rather than merely mapping the attractor states [^kauffman1993origins][^kauffman1995home][^dangComputingReachableStates2011] or analyzing their sensitivity to model parameter changes [^ingallsFrequencyDomainApproach2004][^ingallsSensitivityAnalysisModel2008] as extensively proposed in conventional GRN analysis methods, our framework investigates the dynamic adaptability of these networks' navigation competencies in response to various changing environmental conditions. With this approach, our aim is to uncover whether diverse competencies, analogous to the ones exhibited by living agents, can be found within physiological network dynamics. Notably, these competencies are discovered without necessitating structural alterations to network properties or connectivity. Importantly, our framework and its associated tools do not make any assumptions about the structure or origin of the biological network, making it in theory adaptable to the study of diverse unconventional intelligences across various domains.

By applying this framework to a curated database of GRN models, we discovered a diverse range of behavioral responses that GRN can exhibit under different initial conditions and characterized their robustness to various perturbations. Notably, our analysis revealed a number of interesting aspects of navigation of the state space which can be leveraged in several contexts. These automated tools form the first step towards cost-effective *in silico* simulation and interrogation platforms; as the "behavioral catalogs" produced by this process can be a first stepping stone for better understanding the GRN functionalities as well as for designing drug-driven interventions in a biomedical or bioengineering context.

There are several limitations and avenues for future work to this study. First, these networks are studied as a model in isolation and it is possible that some of the ODE models (or solvers) provide spurious behaviors within certain parameter ranges which might not map to observable phenotypes *in vitro*. Interestingly, this limitation also suggests an interesting further direction to this work: using the automated discovery toolbox to assist model inference, allowing to efficiently identify the rare or unexpected behaviors of the ODE model and suggest whether further refinement is needed or not. Another interesting direction for future work, as our framework considers the GRN model as a black-box and works with limited experimental budget, would be to directly apply it to *in vitro* GRN models at the bench. One could for instance integrate experimental constraints to the search by defining families of empirically-testable interventions and perturbations, as well as specify clinically-relevant goal spaces and perturbations. Even if in a biological setting versatility and robustness phenomena may be harder to detect, or harder to alter, these results can be used to (1) design synthetic biology circuits with advanced capabilities [^pandiVersatileActiveLearning2022], and (2) conduct studies of subcellular proto-cognitive phylogenetics, to help understand the evolutionary pressures for and against reprogrammability in cell regulatory machinery. Another limitation of our work is that we consider predefined problem spaces, here the space of GRN steady states (or Fourier descriptors of the dynamics in the bioengineering example). The dynamics of gene regulatory networks are relatively simple (usually converge to stable points or periodic orbits) allowing such hand-defined descriptors. To scale the framework to higher-dimensional and more complex problem spaces, recent works from the IMGEP literature suggest using unsupervised learning of goal space representations [^reinkeIntrinsicallyMotivatedDiscovery2020][^etcheverryHierarchicallyOrganizedLatent2020]. Whereas these works were applied to abstract models of multicellular patterning, similar works could be envisaged in more realistic systems, such as sophisticated model of multicellular morphogen and/or bioelectrical patterning which were used to suggest in-vitro experimental manipulations [^libbyAutomatedDesignPluripotent2019][^pietakExploringInstructivePhysiological2016].

The tools presented here, and the behavioral repertoire we identified, are just the beginning, and much work remains. Future efforts must test additional competencies across the spectrum of cognition (memory, creative problem-solving, valence, etc.) and extend the tools we presented here to explore them . The predictions made by our computational tools can now be tested in real cells, using emerging tools for physiological profiling in the living state and a diverse set of biochemical, biomechanical, and bioelectrical perturbations. We anticipate a tight and productive feedback loop between computational theory that suggests new experiments, and results in living cells that greatly extend our computational perspective on what they can do [^koseskaCellSignalingCognitive2017][^baluskaCellularSentiencePrimary2022][^baluskaCellularEvolutionaryPerspectives2023][^reberCognitionSurprisingPlaces2021][^baluskaCellularOrganismalAgency2021]. Such interdisciplinary work, pulling together concepts and techniques across fields, is likely to have major implications for fundamental understanding of evolution, intelligence, and dynamical control, as well as drive novel kinds of therapeutics that leverage the innate behavioral competencies of living matter[^levinDarwinAgentialMaterials2023][^bernheim-groswasserLivingMatterMesoscopic2018].

## Methods

<!-- start_details -->

   
### GRN models and numerical simulation

This study employs ordinary differential equation (ODE) models to represent molecular pathways, with nodes representing pathway components and edges capturing their interactions. The continuous node states, encompassing variables like gene expression levels and protein concentrations, are interconnected through a system of ODEs, enabling the modeling of complex regulatory dynamics. ODE models are often available in the Systems Biology Markup Language (SBML), a standardized format that contains essential information about variables, parameters, equations, and model metadata in XML files.

To perform numerical simulations of ODE SBML models, we rely on the SBMLtoODEjax python library, a recent development that automates the parsing and conversion of SBML models into python models written entirely in JAX [^etcheverrySBMLtoODEjaxEfficientSimulation2023]. Taking advantage of JAX computing capabilities, SBMLtoODEjax enables efficient and parallel numerical solutions for gene expression levels and other node states by recursively invoking the generated python models to integrate the ODE equations with current gene expression levels. Additionally, we have developed a python library ([https://github.com/flowersteam/autodiscjax](https://github.com/flowersteam/autodiscjax)) comprising additional modules and pipelines that facilitate interventions on the GRN models such as genome or drug interventions, as well as other perturbations such as noise, pushes, and walls that can be applied to the states and kinematic parameters of gene regulatory networks.

Given the model species initial state $y(t = 0)$, the desired rollout length $T(secs)$ and step size $\Delta T$, as well as the chosen intervention $i$ and/or perturbation $u$, the model rollout iteratively 1) integrates the system of ODE-governed equations that specifies the rate of species changes $\frac{dy}{dt}$ using JAX odeint solver to update model species $y(t) \rightarrow y(t + \Delta T)$, 2) calls the model assignment rules to update kinematic parameters if needed, and 3) apply the intervention and/or perturbation function to update $\left( y(t + \Delta T),w(t + \Delta T),c \right)$ accordingly. In this paper we use $T = 2500secs$ and $\Delta T = 0.1$ (25 001 time points per rollout including $t_{0}$). The ODE solver uses an absolute tolerance of $1e^{- 6}$ and relative tolerance of $1e^{- 12}$, with maximum number of solver steps of $1000$. For a step-by-step guide on utilizing these libraries within the proposed framework, we refer interested readers to our tutorial ([https://developmentalsystems.org/curious-exploration-of-grn-competencies/tuto1.html](https://developmentalsystems.org/curious-exploration-of-grn-competencies/tuto1.html)), which offers practical examples and detailed instructions.

### Experimental setup

In our computational models, we are able to record the activities of all nodes during a model rollout. The observation space $O \subset {\mathbb{R}}_{+}^{n \times \frac{T}{\Delta T}}$ is such that $o = \left( y(0),\ldots,y(T) \right)$ where $y(t)$ represents the n-dimensional vector of node states at each time step, with T being the total reaction time. The boundaries of the observation space are not known.

Regarding the exploration of problem spaces, namely the intervention space I and behavior space Z for the experimental campaign, we specify them as follows.

The intervention space $I \subset {\mathbb{R}}_{+}^{n}$consists of initial node states sampled from the hyper-rectangle $\left\lbrack y_{0,\min},y_{0,\max} \right\rbrack$ where $y_{0,\min} = \frac{1}{r} \times y_{d,\min}$ and $y_{0,\max} = r \times y_{d,\max}$ with $r = 20$ and $\left( y_{d,\min},y_{d,\max} \right)$ the minimum and maximum of each node of the model over the default time course simulation (with initial conditions provided in the SBML file and T=25000). On the other hand, the behavior space $Z \subset {\mathbb{R}}_{+}^{2}$ endpoint states $z = \left( y_{i}(T),y_{j}(T) \right)$ where $(i,j)$ corresponds to the target phenotype nodes. We ensure that most trajectories have reached stable states at T = 2500 (as elaborated in the next section) such that Z can be viewed as the space of reachable endpoints, whose boundaries are not known.

### Database creation

#### Biological networks database

All the ODE models we use in this work are downloaded from the BioModels database [^glontBioModelsExpandingHorizons2018][^malik-sheriffBioModels15Years2020] in SBML format. From all models referenced on the website, we only consider the ones that are curated, that have at least 3 nodes, and that are handled by the SBMLtoODEjax simulator (as SBMLtoODEjax does not handle models with discrete events, custom functions or other specific cases as detailed in [^etcheverrySBMLtoODEjaxEfficientSimulation2023]. To ensure the inclusion of models suitable for our analyses, we applied specific filters to the collected models.

First, we simulated the default model rollout for each model to obtain the concentration profiles of the pathway components over a short time span (T=10 secs and $\Delta T = 0.1$). We discarded simulation results containing invalid values (NaN or negative concentrations) or those that took an excessive amount of time (\>1sec). While it is acceptable that a rollout sometimes returns NaN values (when there are no solutions given ODE tolerance options for specific initial conditions), we consider the model invalid if this occurs for the default initial conditions provided in the SBML file.

For the remaining models, we conducted further simulations with an extended time span (T=2500) and 50 random initial conditions uniformly sampled within the model's intervention space $I$ (as defined before). Once again we discarded models whose batch simulations took an excessive amount of time ($>15$ secs). From the remaining models, we derived the resulting 50 trajectories for each node pair (i, j) and subjected them to additional filters to refine the database. We removed node pairs where either 1) \[filter F1\] a substantial proportion of trajectories $\left( \ge 20\% \right)$ exhibited invalid concentrations (NaN or negative) or unsettled behaviors $(\exists t \ge 2400 \text{ such that } |y(t)-y(T)| \ge0.02 \times |y(T)-y(0)|)$ or periodic patterns $(\exists f>0 \text{ such that } |S(f)| \ge 40 \text{ where } S=DFT(y(\frac{T}{2}, \dots, y(T)))$; or \[filter F2\] the reached space in $Z$ was too small$\left( \left( \max_{k = 1\cdots 50}y^{k}(T) - \min_{k = 1\cdots 5}y^{k}(T) \right) < 0.1 \right)$ to discard cases where "diversity" could result from floating point rounding errors; or \[filter F3\] the number of attractors was less than four $($ \{$ y^k(T)$\}$_{k = 1 \dots 50}\text{ cover } \leq 4 \text{ bins over a }20 \times 20 \text{ binning of } Z)$.

Upon completion of the filtering process, our final database comprised 30 models, consisting of a total of 432 systems, as detailed in Supplementary Table S1. These curated models and systems served as the foundation for our subsequent analyses and investigations into the navigation competencies of the molecular pathways.

#### Random networks database

Following the methodology proposed in [^biswasLearningTranscriptionalNetwork2023], we aimed to create a database of synthetic networks with topologies similar to those of the biological networks, but with random regulatory rules instead of evolved ones. The objective was to compare the versatility and robustness competencies between biological and random networks, akin to the approach used for memory competencies in [^biswasLearningTranscriptionalNetwork2023]. To achieve this, we initially generated 300 networks based on the transcriptional gene circuit model [^reinitzMechanismEveStripe1995], ensuring that they had the same distribution of network size (number of nodes) and connectivity (nodes in-degree) as the biological network database (using fitted gaussian distributions). The kinematic parameters $W,b,\tau$ of these networks were randomized $( W \sim [-30,~30]^{n\times n}, ~ B\sim [-10,~10]^n, ~ \tau \sim [1,~15])$ where model step is defined as $y(t + 1) = \frac{\Delta T}{\tau} \times sigmoid(Wy + B) + \left( 1 - \frac{\Delta T}{\tau} \right) \times y$ and in-degree connectivity is enforced by setting some weights of $W$ to zero. However, during the creation process, we observed that none of the generated networks met the criterion for exhibiting a sufficient number of steady states (criterion F3). This limitation arose from the inherent constraints imposed by the gene circuit model's shape of ODE equations, limiting the diversity of possible dynamical behaviors. As our focus was on networks with a possible spectrum of steady states, akin to the biological network database, we decided not to pursue further analyses on these networks.

Instead, we selected the systems (models and pairs of nodes) that demonstrated the highest versatility (metric detailed below) from among all the generated systems that passed the filters F1 and F2. The selected networks' versatility is presented in Figure 7, but for future research, it would be interesting to explore broader and more complex classes of equations to assess their potential for achieving higher behavioral diversity.

### Curiosity-driven exploration

This section provides additional information about the internal models and hyperparameters of the intrinsically-motivated goal exploration process. The overall IMGEP pipeline is illustrated in Figure 1-c. To sample a goal, the IMGEP uses a uniform sampling strategy within the bounding hyper-rectangle of currently reached goals (scaled by a factor 1.3). Hence sampling bounds adapt to the discoveries and do not need to be predefined via expert knowledge. The volume of the hyper-rectangle is larger compared to the cloud of currently-reached goals, which incentivizes targeting unexplored areas outside of the cloud and promotes diversity in the exploration process. Then, to generate an intervention for achieving the sampled goal, the IMGEP selects the nearest previously reached goal in $Z$, identifies its associated intervention, and performs a local random step from that point $(stepsize \sim \mathcal{N}(0, 0. 1 \cdot [y_{0,\max} - y_{0,\min}])$ in the intervention space.

While our implementation choices for the IMGEP goal representation, goal generation, and goal-conditioned optimization are relatively straightforward, it is worth noting that alternative strategies could be considered for each of these components for more complex problems. The python library AutoDiscJax ([https://github.com/flowersteam/autodiscjax](https://github.com/flowersteam/autodiscjax)) that accompanies this paper can be used to implement this and other IMGEP variants in JAX.

### Robustness tests

We define 3 family of perturbations: 1) the noise perturbation $U_{n}\left( \sigma_{n},p_{n} | y \right)$ which is parametrized by its standard-deviation (scaled proportionally to the extent of the observed trajectory $y$ prior perturbation) and period (secs); 2) the push perturbation $U_{p}\left( m_{p},n_{p} | y \right)$ parametrized by its magnitude (proportional to the extent of $y$) and number of occurrences; 3) the wall perturbation $U_{w}\left( l_{w},n_{w} | y \right)$ parametrized by its length (proportional to the extent of $y$) and number, and where walls are generated in locations of the space that the GRN would "naturally" visit without the induced perturbation. Details about the implementation of walls are provided in Supplementary Figure S3.

To assess the robustness of the GRN systems in our database, we employ an evaluation procedure, as depicted in Figure 1-d. For each system $(I,Z)$ in the database with its corresponding behavioral catalog $H$ discovered using the curiosity-search algorithm, we perform the following steps. We first retrieve $K$ representative trajectories out of the $N$ discoveries, i.e. ones that cover well the reachable space. To do so, we randomly sample tuples of K discoveries (among N) 500 times, and select the one with the maximum diversity. One could test all trajectories with K=N but here we use K=N/10 mainly for compute reasons, as we run the experimental campaign on all 432 systems. Next, we subject each of these K trajectories \{${ y}_{k},k = 1\ldots K$\} to s=18 different perturbation distributions, each representing various levels of difficulty:<br>
$\left( \sigma_{n},p_{n} \right) \in$ \{$(0.001,5),(0.005,5),(0.1,5),(0.005,10),(0.005,5),(0.005,1)$\},<br> 
$\left( m_{p},n_{p} \right) \in $ \{$(0.05,1),(0.1,1),(0.15,1),(1,0.1),(2,0.1),(3,0.1)$\}, <br>
$\left( l_{w},n_{w} \right) \in $ \{$(0.05,1),(0.1,1),(0.15,1),(1,0.1),(2,0.1),(3,0.1)$\}. <br>
In each perturbation distribution, we sample r=3 random perturbations, resulting in $P = s \ast r$ perturbations. For each perturbation in the set \{${ u}_{p},p = 1\ldots P$\}, we re-run the trajectory starting from the same initial state $i$ but with the sampled perturbation applied $\left( i,u_{p} \right)$, and observe the resulting outcome $\left( o_{p} \right)$ and reached endpoint $\left( z_{p} \right)$.

At the end of this process, the behavioral catalog is augmented with the perturbed trajectories<br> $H =$ \{$( i_{k},o_{k},z_{k},~( u_{p},o_{p},z_{p}),~~p = 1\ldots P$\} $),~~k = 1\ldots K$\}.

### Evaluation Metrics

#### Diversity measure

Diversity is measured by the area that explored observations cover in behavior space Z. Each single exploration results in a new point in this space, such that diversity measures how much area the algorithms explored in those spaces.

In general, existing approaches in the NS, QD and IMGEP literature use binning-based metrics [^reinkeIntrinsicallyMotivatedDiscovery2020][^etcheverryHierarchicallyOrganizedLatent2020][^pugh2015confronting] or distance-based metric from ecology [^scheinerCompilationTypologyAbundance2019] to quantify the diversity of a set of explored instances. However, those metrics are sensitive to the binning strategy, or fail to discriminate between qualitatively significantly different explorations [^benureauSelfExplorationSensorimotor]. Another approach, called the threshold coverage, measures diversity as the volume of the union of the set of hyperballs of radius $\epsilon$ that have for centers the observed effects <br>\{$z \in Z$\}. This diversity measure, while difficult to compute in high-dimensional spaces, avoids the pitfalls of bin-based and distance-based metrics and is easily computable in 2-dimensional spaces [^benureauSelfExplorationSensorimotor].

Threshold coverage quantifies the area of the space that has been reached at a given precision $\epsilon$(the threshold), and is what we used in Figure 3 to compare random search and curiosity-driven exploration strategies.

#### Sensitivity measure

In general, existing approaches in systems biology and evolutionary genetics measure sensitivity (opposite of robustness) in a relative manner with respect to 1) a functionality [^kitanoTheoryBiologicalRobustness2007] or phenotypic trait [^felixPervasiveRobustnessBiological2015] of interest, 2) specific perturbations (environmental or genetic changes), and 3) a measure of the degree of variation. Here, we adopt a similar metric where 1) the phenotypic trait of interest is defined as a goal state $z \in Z$ discovered by curiosity search, 2) the set of perturbation \{$ u_{p}$\} is defined in previous section and conditioned on the GRN goal-reaching trajectory $i \rightarrow z$, and 3) variation is measured as the Euclidean distance in behavior space, normalized by the extent of the trajectory prior perturbation in Z.

This distance-based sensitivity measure proves straightforward as we explicitly use "spaces" to observe and analyze behaviors. The results of this sensitivity analysis are presented in Figure 5.

#### Versatility-Robustness measure

In this study, we introduce the terms "diversity" and "versatility" to characterize the competencies of the exploration agent (IMGEP) and the gene regulatory network agent (GRN), respectively. Diversity refers to the ability of the IMGEP agent to reveal a wide range of behaviors in the GRN, while versatility refers to the capability of the GRN agent to reach diverse goal states. The GRN versatility is unknown, and can only be approximated via proxy metric. Here, we consider that the diversity of the IMGEP (measured with the threshold coverage metric) is a good approximation of the versatility of a given GRN, as the IMGEP was shown to efficiently drive the GRN into diverse possible goal states.<br>
In Figure 7a, we employ this diversity metric to categorize the versatility of surveyed networks based on the class of organism they belong to. For the random networks, as they all have less or equal than 4 attractors, the versatility remains below $0.026 = 4 \times\frac{\pi\epsilon^{2}}{(1+2\epsilon)^{2}}.$

Figure 7b, we introduce the versatility-robustness metric, which conditions the diversity metric on a sensitivity threshold. Only goal states with sensitivity to perturbations below this threshold are considered when computing the reached area of the space. A high versatility-robustness score indicates that diverse goal states are achieved with a high level of precision.

### Experiments on the RKIP-ERK signaling pathway 

This section details the additional experiments conducted on the RKIP-ERK signaling pathway [^kwang-hyunMathematicalModelingInfluence2003]. We refer to the accompanying notebook tutorial for reproducing these experiments: [[https://developmentalsystems.org/curious-exploration-of-grn-competencies/tuto1.html]{.underline}](https://developmentalsystems.org/curious-exploration-of-grn-competencies/tuto1.html).

For Figure 4, clustering in behavior space was performed using the HDBSCAN algorithm [^mcinnes2017hdbscan] with hyperparameters set as min_cluster_size=10 and cluster_selection_epsilon=0.1. Points in the 10-dimensional intervention space are visualized by applying a TSNE 2-dimensional reduction. To visualize the clusters in behavior space (and corresponding clusters in intervention space), we fitted polygons on the cluster points using shapely library unary_union, dilatation, and erosion operations [^gillies_sean_2022_7428463].

In Figure 6, we generated trajectory-based energy landscapes following the method proposed in [^venkatachalapathyTrajectorybasedEnergyLandscapes2021]. Energy landscapes provide an intuitive way to understand how a system with multiple steady states behave, by picturing it as a ball rolling downhill towards low-energy valleys (steady states). Given a set of trajectories in behavior space Z, we constructed a probability distribution (P) of system states and converted it into a pseudopotential energy surface (U = −ln(P)). This energy surface was smoothed using cubic spline interpolation and visualized using Plotly 3D surface plots. Figure 6a, 6b, and 6c differed by the input set of trajectories used for generating the landscape: a) employed the set of trajectories discovered by random search, b) used the set of trajectories discovered by curiosity search, and c) utilized the set of trajectories generated by robustness tests.

In Figure 8, the "healthy" and "disease" clusters were the same as in Figure 4 and visualized similarly. We displayed trajectories with the lowest sensitivity (averaged over all $P = 3 \times 18$ perturbations). The stimuli-based intervention shown in Figure 8b was found using a simple random search procedure. First, we defined an arbitrary target node and a stepwise node-activation function, clamping MKEPP values to desired values $x = \left\lbrack {y_{MEKPP}}^{(1)},\cdots,{y_{MEKPP}}^{(10)} \right\rbrack$ every 10 seconds for 100 seconds. Then, we randomly sampled x within a range of values near the MKEPP current steady states (endpoints from the 6 "disease" trajectories, assuming that the drug intervention cannot drastically remodel those values). For each candidate x, we ran new trajectories starting from the disease states and applying the intervention x under a distribution of noise, push, and wall perturbations. Finally, we selected the intervention x that most successfully brought ERK-RKIP levels back to the target setpoint (centroid of the healthy region). The resulting intervention (shown in Figure 8b) succeeds to robustly reset all 6 disease state points despite perturbations, as shown in Figure 8c. We refer to the notebook for reproducing the experiments.

### Experiments on synthetic gene networks

This section details the additional experiments conducted on the synthetic gene networks (Figure 9). We refer to the second accompanying tutorial for the full codebase: [https://developmentalsystems.org/curious-exploration-of-grn-competencies/tuto2.html](https://developmentalsystems.org/curious-exploration-of-grn-competencies/tuto1.html).

In these experiments, we consider the target application of gene circuit engineering followed in [^hiscockAdaptingMachinelearningAlgorithms2019], where parameters of a gene circuit model are optimized to produce target oscillator patterns. The gene circuit model employed in [^hiscockAdaptingMachinelearningAlgorithms2019] is the same than the one used for the random networks database (Eq 1), with $\tau = 1$. Hence the *intervention space* is a $n^{2} + 2n$ dimensional space defined as $I = \left\lbrack y_{t = 0,\min},y_{t = 0,\max} \right\rbrack \oplus \left\lbrack W_{\min},W_{\max} \right\rbrack \oplus \left\lbrack B_{\min},B_{\max} \right\rbrack$, with $y_{0,\min} = 0,$ $y_{0,\max} = 1,$ $W_{\min} = - 30,$ $W_{\max} = 30,$ $B_{\min} = - 10,$ $B_{\max} = 10$. Here we consider networks of n=3 nodes, with the first node being the target phenotype node. Thus, what we seek here is kinematic parameters $(W,B)$ and initial concentrations $y_{0}$ that would produce a periodic pattern $y =[y_{n=0}(0), ~\cdots~y_{n=0}(T)]$ with target amplitude $A$, frequency $w$ and offset $b$. Here, the target $(A,\omega,b)$ are sample randomly with $A \sim U\left( \lbrack 0.1,0.5\rbrack \right),$ $b \sim U\left( \lbrack A,1 - A\rbrack \right),$ $\omega \sim Beta(\alpha = 2,\beta = 8)$.

We then compare three alternative exploration strategies: 1) curiosity search, 2) random search and 3) gradient descent, i.e. pure optimization-driven search as proposed in [^hiscockAdaptingMachinelearningAlgorithms2019], all given the same experimental budget $N = 5000$.

For curiosity search, the behavior space $Z$ is defined as the image space of the discrete Fourier transform of the 1d-signal $y$, where distance in the space measures average difference in spectral amplitude. The IMGEP algorithm is then the same that the one previously used, as detailed in Figure 1-c, but operating within the novel problem spaces $(I,Z)$.

For random search, interventions are sample uniformly $\left( i_1,~ \cdots ~,i_{N} \right) \sim U(I)$.

For gradient descent, we follow the procedure proposed in [^hiscockAdaptingMachinelearningAlgorithms2019]. We define a loss function which, for a set of parameters $i = \left( W,B,y_{0} \right)$, measures the mean square error between the phenotype node activation levels $y$ and the target oscillation represented as a cosine wave with the desired $(A,\omega,b)$ : $L = \sum_{t}(y(t) - (A\cos(2\pi\omega \times t) + b))^2$. We then sample a random parameter $i \sim U(I)$ and use Adam optimizer with $l_{r} = 10^{- 3},$ $b1 = 0.02,$ $b3 = 0.001,$ $\epsilon = 10^{- 8}$ for $N = 5000$ optimization steps (same number of model rollouts allowed than for curiosity search and random search).

In addition, we use gradient descent for *local* refinement of the best discoveries made by the other exploration strategies (curiosity search and random search), this time with a limited budget of $N = 100$ optimization steps.

Visualizations in Figure 9 show: (a-b) the oscillators discovered by random search and curiosity search (gradient descent did not find any oscillator in this example) in the $(A,\omega,b)$ space, (c) the corresponding diversity (using this time a binning-based space coverage measure with $20^{3}$bins as the space is 3-dimensional), (d) the evolution of the training loss $L$ throughout the N=5000 trials for the three exploration strategies, (e-f-g) the corresponding best discoveries (for which $L$ is minimal) for the three exploration strategies, and (h-i) the local training loss and resulting finetuning of the best discoveries with gradient descent.

### Statistics
Statistical analyses were performed using custom code in python 3.9 (relevant libraries include jax 0.4.8 and scipy 1.10 and plotly 5.16.1). Welch’s two-sample t-tests reported in Figure 3 are two-tailed.  

<!-- end_details -->

## Data Availability
The datasets generated and analyzed in this study for the generation of the main figures  are provided with the code repository (see Code availability). 

## Code Availability
All source code is available on GitHub at [https://github.com/flowersteam/curious-exploration-of-grn-competencies](https://github.com/flowersteam/curious-exploration-of-grn-competencies). It contains experimental data and an executable jupyter notebook version of the paper to reproduce all paper figures. It also contains two jupyter notebooks with step-by-step tutorials to reproduce results from scratch for Figures 4, 6 and 8 (tutorial 1) and Figure 9 (tutorial 2), as well as the python codebase to reproduce the whole experimental campaign. All our codebase is open-source under MIT License.

## Acknowledgments
We thank Patrick Erickson and Randall Jordan Ellis for review and discussion, as well as Tom Cirrito, Wesley Clawson and Santosh Manicka for useful discussions. We also thank Alexander Mordvinstev for providing the executable paper template, as well as Julia Poirier for assistance with the manuscript. 

The authors acknowledge support from the biotechnology company Poietis and the French National Association of Research and Technology (ANRT), as well as from the French National Research Agency (ANR, DeepCuriosity AI chair project). M.L. gratefully acknowledges funding support from Astonishing Labs, and from the Templeton World Charity Foundation via grant TWCF0606.

This work also benefited from the use of the Jean Zay supercomputer associated with the Genci grant A0151011996.

## Author Contributions
M.E, M.L, PY.O and C.MF conceived the project together. M.E. wrote the code and performed the computational experiments and data analysis. M.L, PY.O and C.MF supervised the project. M.E, M.L, PY.O and C.MF wrote the paper.

## Corresponding Author
Correspondence to Michael Levin: michael.levin@tufts.edu 

## Competing Interests Statement
M.L.’s lab receives funding in the form of a sponsored research agreement from, and consults for, Astonishing Labs, which has interest in therapeutic applications of GRN learning behaviors.

## Supplementary Material

<!-- start_details -->

In [26]:
#@title [Figure 1S1]
fig_idx = "S1"

if nb_mode == "run":
        
    fig = make_subplots(rows=1, cols=3, 
                        subplot_titles=("<b>(a) simulation in batch mode</b>", 
                                        "<b>(b) example drug intervention</b>", 
                                        "<b>(b) example genome intervention</b>"), horizontal_spacing=0.1, vertical_spacing=0.1)
    fig.update_layout(default_layout)
    fig.update_annotations(default_annotation_layout)
    
    tutofig_to_rowcol = {'9': (1, 1), '4': (1, 2), '5': (1, 3)}
    show_tutofig1_legend = False
    
    for tutofig_idx, (row, col) in tutofig_to_rowcol.items():
        tuto_fig = plotly.io.read_json(f"figures/tuto1_fig_{tutofig_idx}.json")
        plot_idx = fig._grid_ref[row-1][col-1][0].trace_kwargs['xaxis'][1:]

        for d in tuto_fig.data:
            if d.xaxis == "x":
                continue
            else:
                d.xaxis = f'x{plot_idx}'
                d.yaxis = f'y{plot_idx}'
                
                d.showlegend = False

                if tutofig_idx == '2':
                    d.marker.colorbar.xanchor="left"
                    d.marker.colorbar.x = 0.4
                    d.marker.colorbar.yanchor="top"
                    d.marker.colorbar.y = 1.
                    d.marker.colorbar.len = 0.2
                else:
                    d.marker.colorbar = {}

                fig.add_trace(d, row=row, col=col)

        for a in tuto_fig.layout.annotations:
            if a.xref == "x":
                continue
            else:
                if a.xref is not None:
                    a.xref = re.sub('\d', plot_idx, a.xref)
                if a.yref is not None:
                    a.yref = re.sub('\d', plot_idx, a.yref)
                if a.axref is not None:
                    a.axref = re.sub('\d', plot_idx, a.axref)
                if a.ayref is not None:
                    a.ayref = re.sub('\d', plot_idx, a.ayref)

            fig.add_annotation(a, row=row, col=col)
        
        if not hasattr(tuto_fig.layout, 'xaxis2'):
            fig.update_xaxes(tuto_fig.layout.xaxis, **default_layout.xaxis, row=row, col=col)
            fig.update_yaxes(tuto_fig.layout.yaxis, **default_layout.yaxis, row=row, col=col)
        else:
            xaxes = tuto_fig.layout.xaxis2.to_plotly_json()
            xaxes.pop('anchor', None)
            xaxes.pop('domain', None)
            fig.update_xaxes(xaxes, **default_layout.xaxis, row=row, col=col)
            yaxes = tuto_fig.layout.yaxis2.to_plotly_json()
            yaxes.pop('anchor', None)
            yaxes.pop('domain', None)
            fig.update_yaxes(yaxes, **default_layout.yaxis, row=row, col=col)
            
        if show_tutofig1_legend and tutofig_idx == '1':
            legend = tuto_fig.layout.legend
            legend.x=0.28
            legend.xanchor="right"
            legend.font.size=10
            fig.update_layout(legend=legend)
        

    # Serialize fig to json and save
    if nb_save_figs:
        fig.write_json(f"figures/paper_fig_{fig_idx}.json")
        
            
elif nb_mode == "load":
    json_fig = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.json").text
    fig = plotly.io.from_json(json_fig)

    
# Fig size and title
width, height = 940, 280
t = "Examples of interventions that can be implemented within the accompanying AutodiscJax software. All those examples can be reproduced in the accompanying tutorial 1. "\
"(a) Numerical simulations with interventions can be performed in parallel by vectorizing simulations over different intervention parameters, simply using the jax vmap operator. "\
"This offers a convenient (and fast) way to test several interventions in the biological network, as shown here for testing the network under various initial conditions in batch mode. "\
'Examples of other possible "drug" or "genome" interventions that can be implemented in the accompanying software, as well as the possibility to perform interventions (or perturbations) in parallel using batched computations. '\
'In this example, despite the numerous interventions, the GRN trajectories still converge to the same endpoint B. '\
r"(b) Example intervention where species amounts are clamped to specific values. In this example the node MEKPP is clamped to $2.5\mu M$ for 10 seconds at t=0 and then to $1\mu M$ for 10 additional seconds at t=400. "\
"In this example, after the first clamping the GRN trajectory still follows a similar S-shape curve and arrives close to the original endpoint B but after the second clamping, ERK expression levels are shifted to a higher steady state B'. "\
"(c) Example intervention where the numerical value of one kinematic parameter of the model (k5) is changed from 0.0315 to 0.1. In this example we can see that changing the parameter k5 shifts the trajectory end point quite significantly, but qualitatively the trajectory seems to preserve a similar S-shape."

# Render Fig
html_fig = make_html_fig(fig_idx, fig, width, height, None)
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [27]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

In [28]:

import markdown
#@title [Table S1]
database = []
keys = ["BioModel ID reference", "number of nodes", "organism class", "systems (observed nodes pairs)"]
abs_to_rel_idx = {}
with open("../experimental_campaign/resources/bio_models_database.csv", "r") as f:
        reader = csv.DictReader(f)
        for rel_idx, row in enumerate(reader):
            row_data = dict.fromkeys(keys, "")
            model_idx = int(row['model_idx'])
            abs_to_rel_idx[model_idx] = rel_idx
            row_data["BioModel ID reference"] = f"[BIOMD{model_idx:010d}](https://www.ebi.ac.uk/biomodels/BIOMD{model_idx:010d})"
            row_data["number of nodes"] = row['n_nodes']
            row_data["organism class"] = row['model_class']
            #row_data["cellular process"] = row['model_class_2']
            row_data["systems (observed nodes pairs)"] = []
            database.append(row_data)
with open("../experimental_campaign/resources/bio_models_observed_nodes_database.csv", "r") as f:
        reader = csv.DictReader(f)
        for row in reader:
            model_idx = int(row['model_idx'])
            rel_idx = abs_to_rel_idx[model_idx]
            database[rel_idx]["systems (observed nodes pairs)"].append(tuple(eval(row['observed_node_names'])))
for row_data in database:
    row_data["systems (observed nodes pairs)"] = str(row_data["systems (observed nodes pairs)"])[1:-1]
#print(database)
database_md = markdown_table(database).set_params(quote=False, row_sep="markdown").get_markdown()
d = []
for s in database_md.splitlines():
    d.append(s[1:-1].strip())
database_md = "\n".join(d)
table_title = '\n<span style="font-size: 0.8em; color: rgba(0, 0, 0, 0.6);  width:100%"><b style="font-size: 1em;">Table S1: </b>List of biological networks from Biomodels used in this study. '\
'The resulting database includes 30 biological networks (one row per network) and a total of 432 systems, which is defined as a (GRN model, behavior space (Z)) tuple and where the pairs of observed nodes (used as behavior spaces) per network are given in the last column. </span><br><br>'


table_html = markdown.markdown(database_md, extensions=['tables'])
table_html = table_html.replace("<th>","<th style='width:15%'>",1)
# print(Markdown(database_md))
display(HTML(table_html))
display(HTML(table_title))
# print(database_md)
# print(table_title)

In [29]:
#@title [Figure S2]
fig_idx = "S2"

if nb_mode == "run":

    tutofig_idx = 25
    fig = plotly.io.read_json(f"figures/tuto1_fig_{tutofig_idx}.json")

    # Serialize fig to json and save
    if nb_save_figs:
        fig.write_json(f"figures/paper_fig_{fig_idx}.json")
        
            
elif nb_mode == "load":
    json_fig = requests.get(f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.json").text
    fig = plotly.io.from_json(json_fig)

# Display Fig
width, height = 940, 1200
t = 'Additional results complementing Figure 8 of the main paper. This figure shows the resulting trajectories after applying the discovered stimuli-based intervention (shown in Figure 8-b) '\
'to the example RKIP-ERK signaling pathway [^kwang-hyunMathematicalModelingInfluence2003] for the 6 "disease" trajectories originally discovered in the behavioral catalog (shown in Figure 8-a). '\
'(a) For each trajectory (one per row), we see that the intervention successfully re-sets the disease setpoint (startpoint of the trajectory shown in red in the orange region) to a healthy set-point (endpoint of the trajectory shown in cyan in the green region). '\
'(b-c) Similar results are achieved despite adding push perturbations (b) or wall perturbations (c) in addition to the stimuli-based intervention.'

html_fig = make_html_fig(fig_idx, fig, width, height, None)
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [30]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

In [31]:
#@title [Figure S3]
fig_idx = "S3"

if nb_mode == "run":
    fig = f"figures/paper_fig_{fig_idx}.jpg"
     
            
elif nb_mode == "load":
    fig = f"https://raw.githubusercontent.com/flowersteam/curious-exploration-of-grn-competencies/main/notebooks/figures/paper_fig_{fig_idx}.jpg"
    
# Fig size and title
width, height = int(1122*0.7), int(837*0.7)
t = r'Wall implementation. Walls are implemented within the 2D space spanned by the 2 observed nodes. Within that space, we can interpret the node activation levels $y(0),\cdots,y(t)$ as the trajectory of a particle moving. '\
'In order to simulate the interaction with "walls" in that space, several implementations could be envisaged. Within the accompanying software AutoDiscJax we propose two possible variants: perfectly elastic collision (equivalent to a discontinuous force field) and some continuous force field variant. '\
'The second variant (continuous force field) is employed for the main results of this paper. (a) For the first variant, we consider a perfectly elastic collision without loss of kinetic energy. '\
r'In that case, when the trajectory is touching the wall at position $p$ with speed $v = v_{\bot} + v_{\parallel}$ we deviate the trajectory in such a way that is "bouncing" against the wall such that $v_{\parallel}$ is unchanged and $v_{\bot} \leftarrow - v_{\bot}$. '\
r'To implement it, we simply check whether the segment $\left\lbrack y(t),y(t + \Delta t) \right\rbrack$ intersect the wall at each time step. It it does, we compute the intersection point $p$ and time $t_{1}$, and set the activation level $y(t + \Delta t)$ to $p + (\Delta t - t1) \cdot \left\lbrack - v_{\bot} + v_{\parallel} \right\rbrack$. '\
'(b) For the second variant, we implement walls as energy barriers acting as a new force field in the environment, constraining the GRN traversal of the space. '\
r'This time, instead of having a discontinuous effect on the perpendicular speed $v_{\bot}$ we define a wall force $f_{\bot} = \pm \alpha v_{\bot}$ (+ if $v_{\bot}$ is going toward wall, - otherwise ) and use it to update the perpendicular component of the trajectory speed as $v_{\bot} \leftarrow v_{\bot} + f_{\bot} \cdot \Delta T$. '\
r'Here $\alpha \in \lbrack 0, - 2\rbrack$ and is calculated as a function of the distance between the point and the wall. As illustrated in the figure, this basically results in a stadium-shaped force field around the wall.'


# Render Fig
html_fig = make_html_fig(fig_idx, fig, width, height, None, config={'scrollZoom': True})
display(HTML(html_fig))

if nb_export_figs:
    export_img_fig(fig_idx, fig, width, height)

In [32]:
title = make_title(fig_idx, fig,t)
display(HTML(title))

<!-- end_details -->

## References

[^venkatachalapathyTrajectorybasedEnergyLandscapes2021]: H. Venkatachalapathy, S. M. Azarin, and C. A. Sarkar, “Trajectory-based energy landscapes of gene regulatory networks,” Biophys J, vol. 120, no. 4, pp. 687–698, Feb. 2021, doi: [10.1016/j.bpj.2020.11.2279](https://doi.org/10.1016/j.bpj.2020.11.2279). 

[^timsitIdeaMolecularBrains2021]: Y. Timsit and S.-P. Grégoire, “Towards the Idea of Molecular Brains,” International Journal of Molecular Sciences, vol. 22, no. 21, Art. no. 21, Jan. 2021, doi: [10.3390/ijms222111868](https://doi.org/10.3390/ijms222111868). 

[^kitanoTheoryBiologicalRobustness2007]: H. Kitano, “Towards a theory of biological robustness,” Molecular Systems Biology, vol. 3, no. 1, p. 137, Jan. 2007, doi: [10.1038/msb4100179](https://doi.org/10.1038/msb4100179). 

[^ingoliaTopologyRobustnessDrosophila2004]: N. T. Ingolia, “Topology and Robustness in the Drosophila Segment Polarity Network,” PLOS Biology, vol. 2, no. 6, p. e123, Jun. 2004, doi: [10.1371/journal.pbio.0020123](https://doi.org/10.1371/journal.pbio.0020123). 

[^pezzuloTopdownModelsBiology2016]: G. Pezzulo and M. Levin, “Top-down models in biology: explanation and control of complex living systems above the molecular level,” Journal of The Royal Society Interface, vol. 13, no. 124, p. 20160555, Nov. 2016, doi: [10.1098/rsif.2016.0555](https://doi.org/10.1098/rsif.2016.0555). 

[^bongardTherePlentyRoom2023]: J. Bongard and M. Levin, “There’s Plenty of Room Right Here: Biological Systems as Evolved, Overloaded, Multi-Scale Machines,” Biomimetics, vol. 8, no. 1, Art. no. 1, Mar. 2023, doi: [10.3390/biomimetics8010110](https://doi.org/10.3390/biomimetics8010110). 

[^vondassowSegmentPolarityNetwork2000]: G. von Dassow, E. Meir, E. M. Munro, and G. M. Odell, “The segment polarity network is a robust developmental module,” Nature, vol. 406, no. 6792, Art. no. 6792, Jul. 2000, doi: [10.1038/35018085](https://doi.org/10.1038/35018085). 

[^chooPhenotypeControlKernel2018]: S.-M. Choo, B. Ban, J. I. Joo, and K.-H. Cho, “The phenotype control kernel of a biomolecular regulatory network,” BMC Systems Biology, vol. 12, no. 1, p. 49, Apr. 2018, doi: [10.1186/s12918-018-0576-8](https://doi.org/10.1186/s12918-018-0576-8). 

[^kauffman1993origins]: S. A. Kauffman, The origins of order: Self-organization and selection in evolution. Oxford University Press, USA, 1993.
[^xiaoImpactFunctionPerturbations2007]: Y. Xiao and E. R. Dougherty, “The impact of function perturbations in Boolean networks,” Bioinformatics, vol. 23, no. 10, pp. 1265–1273, May 2007, doi: [10.1093/bioinformatics/btm093](https://doi.org/10.1093/bioinformatics/btm093). 

[^qinExplorationDiseasespecificGene2019]: G. Qin, L. Yang, Y. Ma, J. Liu, and Q. Huo, “The exploration of disease-specific gene regulatory networks in esophageal carcinoma and stomach adenocarcinoma,” BMC Bioinformatics, vol. 20, no. 22, p. 717, Dec. 2019, doi: [10.1186/s12859-019-3230-6](https://doi.org/10.1186/s12859-019-3230-6). 

[^manickaCognitiveLensPrimer2019]: S. Manicka and M. Levin, “The Cognitive Lens: a primer on conceptual tools for analysing information processing in developmental and regenerative morphogenesis,” Philosophical Transactions of the Royal Society B: Biological Sciences, vol. 374, no. 1774, p. 20180369, Apr. 2019, doi: [10.1098/rstb.2018.0369](https://doi.org/10.1098/rstb.2018.0369). 

[^lyonCognitiveCellBacterial2015]: P. Lyon, “The cognitive cell: bacterial behavior reconsidered,” Frontiers in Microbiology, vol. 6, 2015, Accessed: Apr. 21, 2023. [Online]. Available: https://www.frontiersin.org/articles/10.3389/fmicb.2015.00264 

[^lyonBiogenicApproachCognition2006]: P. Lyon, “The biogenic approach to cognition,” Cogn Process, vol. 7, no. 1, pp. 11–29, Mar. 2006, doi: [10.1007/s10339-005-0016-8](https://doi.org/10.1007/s10339-005-0016-8). 

[^luschiTestingNavigationalAbilities2001]: P. Luschi et al., “Testing the Navigational Abilities of Ocean Migrants: Displacement Experiments on Green Sea Turtles (Chelonia mydas),” Behavioral Ecology and Sociobiology, vol. 50, no. 6, pp. 528–534, 2001.
[^levinTechnologicalApproachMind2022]: M. Levin, “Technological Approach to Mind Everywhere: An Experimentally-Grounded Framework for Understanding Diverse Bodies and Minds,” Frontiers in Systems Neuroscience, vol. 16, 2022, Accessed: Jun. 12, 2023. [Online]. Available: https://www.frontiersin.org/articles/10.3389/fnsys.2022.768201 

[^daviesSyntheticMorphologyActive2022]: J. Davies and M. Levin, “Synthetic morphology via active and agential matter.” OSF Preprints, Jun. 10, 2022. doi: [10.31219/osf.io/xrv8h](https://doi.org/10.31219/osf.io/xrv8h). 

[^santorelliSyntheticDevelopmentBuilding2019]: M. Santorelli, C. Lam, and L. Morsut, “Synthetic development: building mammalian multicellular structures with artificial genetic programs,” Current Opinion in Biotechnology, vol. 59, pp. 130–140, Oct. 2019, doi: [10.1016/j.copbio.2019.03.016](https://doi.org/10.1016/j.copbio.2019.03.016). 

[^zanudoStructurebasedControlComplex2017]: J. G. T. Zañudo, G. Yang, and R. Albert, “Structure-based control of complex networks with nonlinear dynamics,” Proceedings of the National Academy of Sciences, vol. 114, no. 28, pp. 7234–7239, Jul. 2017, doi: [10.1073/pnas.1617387114](https://doi.org/10.1073/pnas.1617387114). 

[^stuckiStabilityAnalysisBiochemical1979]: J. W. Stucki, “Stability analysis of biochemical systems— A practical guide,” Progress in Biophysics and Molecular Biology, vol. 33, pp. 99–187, Jan. 1979, doi: [10.1016/0079-6107(79)90027-0](https://doi.org/10.1016/0079-6107(79)90027-0). 

[^latiesSocietyExperimentalAnalysis1987]: V. G. Laties, “Society for the Experimental Analysis of Behavior: The first thirty years (1957–1987),” J Exp Anal Behav, vol. 48, no. 3, pp. 495–512, Nov. 1987, doi: [10.1901/jeab.1987.48-495](https://doi.org/10.1901/jeab.1987.48-495). 

[^vallverduSlimeMouldFundamental2018]: J. Vallverdú et al., “Slime mould: The fundamental mechanisms of biological cognition,” Biosystems, vol. 165, pp. 57–70, Mar. 2018, doi: [10.1016/j.biosystems.2017.12.011](https://doi.org/10.1016/j.biosystems.2017.12.011). 

[^reidSlimeMoldUses2012]: C. R. Reid, T. Latty, A. Dussutour, and M. Beekman, “Slime mold uses an externalized spatial ‘memory’ to navigate in complex environments,” Proceedings of the National Academy of Sciences, vol. 109, no. 43, pp. 17490–17494, Oct. 2012, doi: [10.1073/pnas.1215037109](https://doi.org/10.1073/pnas.1215037109). 

[^gillies_sean_2022_7428463]: S. Gillies et al., “Shapely.” Zenodo, Dec. 2022. doi: [10.5281/zenodo.7428463](https://doi.org/10.5281/zenodo.7428463). 

[^ingallsSensitivityAnalysisModel2008]: B. Ingalls, “Sensitivity analysis: from model parameters to system behaviour,” Essays in Biochemistry, vol. 45, pp. 177–194, Sep. 2008, doi: [10.1042/bse0450177](https://doi.org/10.1042/bse0450177). 

[^benureauSelfExplorationSensorimotor]: F. Benureau, “Self Exploration of Sensorimotor Spaces in Robots.”.
[^etcheverrySBMLtoODEjaxEfficientSimulation2023]: M. Etcheverry, M. Levin, C. Moulin-Frier, and P.-Y. Oudeyer, “SBMLtoODEjax: efficient simulation and optimization of ODE SBML models in JAX.” arXiv, Jul. 17, 2023. doi: [10.48550/arXiv.2307.08452](https://doi.org/10.48550/arXiv.2307.08452). 

[^maRobustnessModularDesign2006]: W. Ma, L. Lai, Q. Ouyang, and C. Tang, “Robustness and modular design of the Drosophila segment polarity network,” Molecular Systems Biology, vol. 2, no. 1, p. 70, Jan. 2006, doi: [10.1038/msb4100111](https://doi.org/10.1038/msb4100111). 

[^donzeRobustnessAnalysisBehavior2011]: A. Donzé, E. Fanchon, L. M. Gattepaille, O. Maler, and P. Tracqui, “Robustness Analysis and Behavior Discrimination in Enzymatic Reaction Networks,” PLOS ONE, vol. 6, no. 9, p. e24246, Sep. 2011, doi: [10.1371/journal.pone.0024246](https://doi.org/10.1371/journal.pone.0024246). 

[^cullyRobotsThatCan2015]: A. Cully, J. Clune, D. Tarapore, and J.-B. Mouret, “Robots that can adapt like animals,” Nature, vol. 521, no. 7553, Art. no. 7553, May 2015, doi: [10.1038/nature14422](https://doi.org/10.1038/nature14422). 

[^wongRevealingTargetedTherapy2008]: D. J. Wong et al., “Revealing Targeted Therapy for Human Cancer by Gene Module Maps,” Cancer Research, vol. 68, no. 2, pp. 369–378, Jan. 2008, doi: [10.1158/0008-5472.CAN-07-0382](https://doi.org/10.1158/0008-5472.CAN-07-0382). 

[^pezzuloRememberingBodyApplications2015]: G. Pezzulo and M. Levin, “Re-membering the body: applications of computational neuroscience to the top-down control of regeneration of limbs and other complex organs,” Integr Biol (Camb), vol. 7, no. 12, pp. 1487–1517, Dec. 2015, doi: [10.1039/c5ib00221d](https://doi.org/10.1039/c5ib00221d). 

[^liQuantifyingCellFate2013]: C. Li and J. Wang, “Quantifying Cell Fate Decisions for Differentiation and Reprogramming of a Human Stem Cell Network: Landscape and Biological Paths,” PLOS Computational Biology, vol. 9, no. 8, p. e1003165, Aug. 2013, doi: [10.1371/journal.pcbi.1003165](https://doi.org/10.1371/journal.pcbi.1003165). 

[^pughQualityDiversityNew2016]: J. K. Pugh, L. B. Soros, and K. O. Stanley, “Quality Diversity: A New Frontier for Evolutionary Computation,” Frontiers in Robotics and AI, vol. 3, 2016, Accessed: Jun. 13, 2023. [Online]. Available: https://www.frontiersin.org/articles/10.3389/frobt.2016.00040 

[^todaProgrammingSelforganizingMulticellular2018]: S. Toda, L. R. Blauch, S. K. Y. Tang, L. Morsut, and W. A. Lim, “Programming self-organizing multicellular structures with synthetic cell-cell signaling,” Science, vol. 361, no. 6398, pp. 156–162, Jul. 2018, doi: [10.1126/science.aat0271](https://doi.org/10.1126/science.aat0271). 

[^bellPrinciplesMechanismsNongenetic2020]: C. C. Bell and O. Gilan, “Principles and mechanisms of non-genetic resistance in cancer,” Br J Cancer, vol. 122, no. 4, Art. no. 4, Feb. 2020, doi: [10.1038/s41416-019-0648-6](https://doi.org/10.1038/s41416-019-0648-6). 

[^walcottPigeonHomingObservations1996]: C. Walcott, “Pigeon Homing: Observations, Experiments and Confusions,” Journal of Experimental Biology, vol. 199, no. 1, pp. 21–27, Jan. 1996, doi: [10.1242/jeb.199.1.21](https://doi.org/10.1242/jeb.199.1.21). 

[^felixPervasiveRobustnessBiological2015]: M.-A. Félix and M. Barkoulas, “Pervasive robustness in biological systems,” Nat Rev Genet, vol. 16, no. 8, Art. no. 8, Aug. 2015, doi: [10.1038/nrg3949](https://doi.org/10.1038/nrg3949). 

[^molinelliPerturbationBiologyInferring2013]: E. J. Molinelli et al., “Perturbation Biology: Inferring Signaling Networks in Cellular Systems,” PLOS Computational Biology, vol. 9, no. 12, p. e1003290, Dec. 2013, doi: [10.1371/journal.pcbi.1003290](https://doi.org/10.1371/journal.pcbi.1003290). 

[^donzeParameterSynthesisNonlinear2010]: A. Donzé, G. Clermont, and C. J. Langmead, “Parameter synthesis in nonlinear dynamical systems: application to systems biology,” J Comput Biol, vol. 17, no. 3, pp. 325–336, Mar. 2010, doi: [10.1089/cmb.2009.0172](https://doi.org/10.1089/cmb.2009.0172). 

[^mikhaltsovParameciumBursaria2013]: A. Mikhaltsov, Paramecium bursaria. 2013. [Online]. Available: https://commons.wikimedia.org/wiki/File:Paramecium_bursaria.jpg 

[^barandiaranWhatMakesCertain2006]: X. Barandiaran and A. Moreno, “On What Makes Certain Dynamical Systems Cognitive: A Minimally Cognitive                 Organization Program,” Adaptive Behavior, vol. 14, no. 2, pp. 171–185, Jun. 2006, doi: [10.1177/105971230601400208](https://doi.org/10.1177/105971230601400208). 

[^baluskaHavingNoHead2016]: F. Baluška and M. Levin, “On Having No Head: Cognition throughout Biological Systems,” Frontiers in Psychology, vol. 7, 2016, Accessed: Jun. 12, 2023. [Online]. Available: https://www.frontiersin.org/articles/10.3389/fpsyg.2016.00902 

[^doncieuxNoveltySearchTheoretical2019]: S. Doncieux, A. Laflaquière, and A. Coninx, “Novelty search: a theoretical perspective,” in Proceedings of the Genetic and Evolutionary Computation Conference, Prague Czech Republic: ACM, Jul. 2019, pp. 99–106. doi: [10.1145/3321707.3321752](https://doi.org/10.1145/3321707.3321752). 

[^hoNovelSyntheticBiology2021]: C. Ho and L. Morsut, “Novel synthetic biology approaches for developmental systems,” Stem Cell Reports, vol. 16, no. 5, pp. 1051–1064, May 2021, doi: [10.1016/j.stemcr.2021.04.007](https://doi.org/10.1016/j.stemcr.2021.04.007). 

[^camachoNextGenerationMachineLearning2018]: D. M. Camacho, K. M. Collins, R. K. Powers, J. C. Costello, and J. J. Collins, “Next-Generation Machine Learning for Biological Networks,” Cell, vol. 173, no. 7, pp. 1581–1592, Jun. 2018, doi: [10.1016/j.cell.2018.05.015](https://doi.org/10.1016/j.cell.2018.05.015). 

[^fetrowNewComputationalApproaches2018]: J. S. Fetrow and P. C. Babbitt, “New computational approaches to understanding molecular protein function,” PLOS Computational Biology, vol. 14, no. 4, p. e1005756, Apr. 2018, doi: [10.1371/journal.pcbi.1005756](https://doi.org/10.1371/journal.pcbi.1005756). 

[^deutscherMultipleKnockoutAnalysis2006]: D. Deutscher, I. Meilijson, M. Kupiec, and E. Ruppin, “Multiple knockout analysis of genetic robustness in the yeast metabolic network,” Nat Genet, vol. 38, no. 9, Art. no. 9, Sep. 2006, doi: [10.1038/ng1856](https://doi.org/10.1038/ng1856). 

[^hanczycModelsMinimalPhysical2011]: M. M. Hanczyc, F. Caschera, and S. Rasmussen, “Models of Minimal Physical Intelligence,” Procedia Computer Science, vol. 7, pp. 275–277, Jan. 2011, doi: [10.1016/j.procs.2011.09.058](https://doi.org/10.1016/j.procs.2011.09.058). 

[^dejongModelingSimulationGenetic2002]: H. de Jong, “Modeling and Simulation of Genetic Regulatory Systems: A Literature Review,” Journal of Computational Biology, vol. 9, no. 1, pp. 67–103, Jan. 2002, doi: [10.1089/10665270252833208](https://doi.org/10.1089/10665270252833208). 

[^chooMinimalInterveningControl2019]: S.-M. Choo, S.-M. Park, and K.-H. Cho, “Minimal intervening control of biomolecular networks leading to a desired cellular state,” Sci Rep, vol. 9, no. 1, Art. no. 1, Sep. 2019, doi: [10.1038/s41598-019-49571-6](https://doi.org/10.1038/s41598-019-49571-6). 

[^di2000minimal]: F. di Primio, B. S. Müller, and J. W. Lengeler, “Minimal cognition in unicellular organisms,” From Animals to Animats, pp. 3–12, 2000.
[^muruganMechanosensationMediatesLongRange2021]: N. J. Murugan et al., “Mechanosensation Mediates Long-Range Spatial Decision-Making in an Aneural Organism,” Adv Mater, vol. 33, no. 34, p. e2008161, Aug. 2021, doi: [10.1002/adma.202008161](https://doi.org/10.1002/adma.202008161). 

[^reinitzMechanismEveStripe1995]: J. Reinitz and D. H. Sharp, “Mechanism of eve stripe formation,” Mechanisms of Development, vol. 49, no. 1, pp. 133–158, Jan. 1995, doi: [10.1016/0925-4773(94)00310-J](https://doi.org/10.1016/0925-4773(94)00310-J). 

[^amdamMeasuringAnimalPreferences2012]: G. Amdam and A. Hovland, “Measuring Animal Preferences and Choice Behavior,” Nature Education Knowledge, vol. 3, p. 74, Jan. 2012.
[^kwang-hyunMathematicalModelingInfluence2003]: C. Kwang-Hyun, S. Sung-Young, K. Hyun-Woo, O. Wolkenhauer, B. McFerran, and W. Kolch, “Mathematical Modeling of the Influence of RKIP on the ERK Signaling Pathway,” in Computational Methods in Systems Biology, C. Priami, Ed., in Lecture Notes in Computer Science, vol. 2602. Berlin, Heidelberg: Springer Berlin Heidelberg, 2003, pp. 127–141. doi: [10.1007/3-540-36481-1_11](https://doi.org/10.1007/3-540-36481-1_11). 

[^leeLossRafKinase2006]: H. C. Lee, B. Tian, J. M. Sedivy, J. R. Wands, and M. Kim, “Loss of Raf Kinase Inhibitor Protein Promotes Cell Proliferation and Migration of Human Hepatoma Cells,” Gastroenterology, vol. 131, no. 4, pp. 1208–1217, Oct. 2006, doi: [10.1053/j.gastro.2006.07.012](https://doi.org/10.1053/j.gastro.2006.07.012). 

[^bongardLivingThingsAre2021]: J. Bongard and M. Levin, “Living Things Are Not (20th Century) Machines: Updating Mechanism Metaphors in Light of the Modern Science of Machine Behavior,” Frontiers in Ecology and Evolution, vol. 9, 2021, Accessed: Jun. 12, 2023. [Online]. Available: https://www.frontiersin.org/articles/10.3389/fevo.2021.650726 

[^bernheim-groswasserLivingMatterMesoscopic2018]: A. Bernheim-Groswasser, N. S. Gov, S. A. Safran, and S. Tzlil, “Living Matter: Mesoscopic Active Materials,” Advanced Materials, vol. 30, no. 41, p. 1707028, 2018, doi: [10.1002/adma.201707028](https://doi.org/10.1002/adma.201707028). 

[^rozumLeveragingNetworkStructure2022]: J. Rozum and R. Albert, “Leveraging network structure in nonlinear control,” npj Syst Biol Appl, vol. 8, no. 1, Art. no. 1, Oct. 2022, doi: [10.1038/s41540-022-00249-2](https://doi.org/10.1038/s41540-022-00249-2). 

[^hamonLearningSensorimotorAgency2022]: G. Hamon, M. Etcheverry, B. W.-C. Chan, C. Moulin-Frier, and P.-Y. Oudeyer, “Learning Sensorimotor Agency in Cellular Automata,” 2022, Accessed: Apr. 23, 2023. [Online]. Available: https://inria.hal.science/hal-03519319 

[^csermelyLearningSignalingNetworks2020]: P. Csermely et al., “Learning of Signaling Networks: Molecular Mechanisms,” Trends in Biochemical Sciences, vol. 45, no. 4, pp. 284–294, Apr. 2020, doi: [10.1016/j.tibs.2019.12.005](https://doi.org/10.1016/j.tibs.2019.12.005). 

[^biswasLearningTranscriptionalNetwork2023]: S. Biswas, W. Clawson, and M. Levin, “Learning in Transcriptional Network Models: Computational Discovery of Pathway-Level Memory and Effective Interventions,” International Journal of Molecular Sciences, vol. 24, no. 1, Art. no. 1, Jan. 2023, doi: [10.3390/ijms24010285](https://doi.org/10.3390/ijms24010285). 

[^liLandscapeFluxReveal2014]: C. Li and J. Wang, “Landscape and flux reveal a new global view and physical quantification of mammalian cell cycle,” Proceedings of the National Academy of Sciences, vol. 111, no. 39, pp. 14130–14135, Sep. 2014, doi: [10.1073/pnas.1408628111](https://doi.org/10.1073/pnas.1408628111). 

[^forestierIntrinsicallyMotivatedGoal2022]: S. Forestier, R. Portelas, Y. Mollard, and P.-Y. Oudeyer, “Intrinsically Motivated Goal Exploration Processes with Automatic Curriculum Learning.” arXiv, May 05, 2022. Accessed: Apr. 21, 2023. [Online]. Available: http://arxiv.org/abs/1708.02190 

[^reinkeIntrinsicallyMotivatedDiscovery2020]: C. Reinke, M. Etcheverry, and P.-Y. Oudeyer, “Intrinsically Motivated Discovery of Diverse Patterns in Self-Organizing Systems,” presented at the Eighth International Conference on Learning Representations, Apr. 2020. Accessed: Apr. 21, 2023. [Online]. Available: https://iclr.cc/virtual_2020/poster_rkg6sJHYDr.html 

[^nakagakiIntelligentBehaviorsAmoeboid2008]: T. Nakagaki and R. D. Guy, “Intelligent behaviors of amoeboid movement based on complex dynamics of soft matter,” Soft Matter, vol. 4, no. 1, pp. 57–67, 2008, doi: [10.1039/B706317M](https://doi.org/10.1039/B706317M). 

[^baumInsertionalMutagenesisGene2007]: C. Baum, “Insertional mutagenesis in gene therapy and stem cell biology,” Current Opinion in Hematology, vol. 14, no. 4, p. 337, Jul. 2007, doi: [10.1097/MOH.0b013e3281900f01](https://doi.org/10.1097/MOH.0b013e3281900f01). 

[^paladuguSilicoEvolutionFunctional2006]: S. R. Paladugu, V. Chickarmane, A. Deckard, J. P. Frumkin, M. McCormack, and H. M. Sauro, “In silico evolution of functional modules in biochemical networks,” IEE Proceedings - Systems Biology, vol. 153, no. 4, pp. 223–235, Jul. 2006, doi: [10.1049/ip-syb:20050096](https://doi.org/10.1049/ip-syb:20050096). 

[^murrugarraIdentificationControlTargets2016]: D. Murrugarra, A. Veliz-Cuba, B. Aguilar, and R. Laubenbacher, “Identification of control targets in Boolean molecular network models via computational algebra,” BMC Syst Biol, vol. 10, no. 1, p. 94, Sep. 2016, doi: [10.1186/s12918-016-0332-x](https://doi.org/10.1186/s12918-016-0332-x). 

[^kimHowCriticalityGene2018]: H. Kim and H. Sayama, “How Criticality of Gene Regulatory Networks Affects the Resulting Morphogenesis under Genetic Perturbations,” Artificial Life, vol. 24, no. 02, pp. 85–105, May 2018, doi: [10.1162/ARTL_a_00262](https://doi.org/10.1162/ARTL_a_00262). 

[^etcheverryHierarchicallyOrganizedLatent2020]: M. Etcheverry, C. Moulin-Frier, and P.-Y. Oudeyer, “Hierarchically Organized Latent Modules for Exploratory Search in Morphogenetic Systems,” in Advances in Neural Information Processing Systems, Curran Associates, Inc., 2020, pp. 4846–4859. Accessed: Apr. 21, 2023. [Online]. Available: https://proceedings.neurips.cc/paper/2020/hash/33a5435d4f945aa6154b31a73bab3b73-Abstract.html 

[^mcinnes2017hdbscan]: L. McInnes, J. Healy, and S. Astels, “hdbscan: Hierarchical density based clustering,” The Journal of Open Source Software, vol. 2, no. 11, p. 205, 2017.
[^colasGEPPGDecouplingExploration2018]: C. Colas, O. Sigaud, and P.-Y. Oudeyer, “GEP-PG: Decoupling Exploration and Exploitation in Deep Reinforcement Learning Algorithms,” in Proceedings of the 35th International Conference on Machine Learning, PMLR, Jul. 2018, pp. 1039–1048. Accessed: Jul. 15, 2023. [Online]. Available: https://proceedings.mlr.press/v80/colas18a.html 

[^krzysztonGenecircuitTherapyHorizon2021]: R. Krzysztoń, Y. Wan, J. Petreczky, and G. Balázsi, “Gene-circuit therapy on the horizon: Synthetic biology tools for engineered therapeutics,” Acta Biochim Pol, vol. 68, no. 3, pp. 377–383, Aug. 2021, doi: [10.18388/abp.2020_5744](https://doi.org/10.18388/abp.2020_5744). 

[^biswasGeneRegulatoryNetworks2021]: S. Biswas, S. Manicka, E. Hoel, and M. Levin, “Gene regulatory networks exhibit several kinds of memory: Quantification of memory in biological and random transcriptional networks,” iScience, vol. 24, no. 3, p. 102131, Mar. 2021, doi: [10.1016/j.isci.2021.102131](https://doi.org/10.1016/j.isci.2021.102131). 

[^padilla-longoriaGeneRegulatoryNetwork2008]: E. R. A.-B. Padilla-Longoria Enrique Balleza, Mariana Benítez, Carlos Espinosa-Soto, Pablo, “Gene regulatory network models: A dynamic and integrative approach to development,” in Practical Systems Biology, Taylor & Francis, 2008.
[^lagasseFutureMedicineMolecular2023]: E. Lagasse and M. Levin, “Future medicine: from molecular pathways to the collective intelligence of the body,” Trends in Molecular Medicine, vol. 29, no. 9, pp. 687–710, Sep. 2023, doi: [10.1016/j.molmed.2023.06.007](https://doi.org/10.1016/j.molmed.2023.06.007). 

[^shenFindingGeneNetwork2021]: J. Shen, F. Liu, Y. Tu, and C. Tang, “Finding gene network topologies for given biological function with recurrent neural network,” Nat Commun, vol. 12, no. 1, Art. no. 1, May 2021, doi: [10.1038/s41467-021-23420-5](https://doi.org/10.1038/s41467-021-23420-5). 

[^pietakExploringInstructivePhysiological2016]: A. Pietak and M. Levin, “Exploring Instructive Physiological Signaling with the Bioelectric Tissue Simulation Engine,” Frontiers in Bioengineering and Biotechnology, vol. 4, 2016, Accessed: Jun. 24, 2022. [Online]. Available: https://www.frontiersin.org/article/10.3389/fbioe.2016.00055 

[^lehmanExploitingOpenEndednessSolve2008]: J. Lehman and K. O. Stanley, “Exploiting Open-Endedness to Solve Problems Through the Search for Novelty,” presented at the IEEE Symposium on Artificial Life, 2008. Accessed: Jul. 31, 2023. [Online]. Available: https://www.semanticscholar.org/paper/Exploiting-Open-Endedness-to-Solve-Problems-Through-Lehman-Stanley/fb144a1d31aec3b2bece6a59bd11a876a9fafb34 

[^nomanEvolvingRobustGene2015]: N. Noman, T. Monjo, P. Moscato, and H. Iba, “Evolving Robust Gene Regulatory Networks,” PLOS ONE, vol. 10, no. 1, p. e0116258, Jan. 2015, doi: [10.1371/journal.pone.0116258](https://doi.org/10.1371/journal.pone.0116258). 

[^francoisEvolvingPhenotypicNetworks2014]: P. François, “Evolving phenotypic networks in silico,” Seminars in Cell & Developmental Biology, vol. 35, pp. 90–97, Nov. 2014, doi: [10.1016/j.semcdb.2014.06.012](https://doi.org/10.1016/j.semcdb.2014.06.012). 

[^tusscherEvolutionNetworksBody2011]: K. H. ten Tusscher and P. Hogeweg, “Evolution of Networks for Body Plan Patterning; Interplay of Modularity, Robustness and Evolvability,” PLOS Computational Biology, vol. 7, no. 10, p. e1002208, Oct. 2011, doi: [10.1371/journal.pcbi.1002208](https://doi.org/10.1371/journal.pcbi.1002208). 

[^peterEvolutionGeneRegulatory2011]: I. S. Peter and E. H. Davidson, “Evolution of Gene Regulatory Networks Controlling Body Plan Development,” Cell, vol. 144, no. 6, pp. 970–985, Mar. 2011, doi: [10.1016/j.cell.2011.02.017](https://doi.org/10.1016/j.cell.2011.02.017). 

[^todaEngineeringSyntheticMorphogen2020]: S. Toda, W. L. McKeithan, T. J. Hakkinen, P. Lopez, O. D. Klein, and W. A. Lim, “Engineering synthetic morphogen systems that can program multicellular patterning,” Science, vol. 370, no. 6514, pp. 327–331, Oct. 2020, doi: [10.1126/science.abc0033](https://doi.org/10.1126/science.abc0033). 

[^clawsonEndlessFormsMost2022]: W. P. Clawson and M. Levin, “Endless forms most beautiful 2.0: teleonomy and the bioengineering of chimaeric and synthetic organisms,” Biological Journal of the Linnean Society, p. blac073, Jul. 2022, doi: [10.1093/biolinnean/blac073](https://doi.org/10.1093/biolinnean/blac073). 

[^davidsonEmergingPropertiesAnimal2010]: E. H. Davidson, “Emerging properties of animal gene regulatory networks,” Nature, vol. 468, no. 7326, pp. 911–920, Dec. 2010, doi: [10.1038/nature09645](https://doi.org/10.1038/nature09645). 

[^katzEmbodyingProbabilisticInference2018]: Y. Katz, M. Springer, and W. Fontana, “Embodying probabilistic inference in biochemical circuits.” arXiv, Jun. 26, 2018. doi: [10.48550/arXiv.1806.10161](https://doi.org/10.48550/arXiv.1806.10161). 

[^bisch-knadenEgocentricInformationHelps2001]: S. Bisch-Knaden and R. Wehner, “Egocentric information helps desert ants to navigate around familiar obstacles,” Journal of Experimental Biology, vol. 204, no. 24, pp. 4177–4184, Dec. 2001, doi: [10.1242/jeb.204.24.4177](https://doi.org/10.1242/jeb.204.24.4177). 

[^sanz-ezquerroEditorialSignalingPathways2017]: J. J. Sanz-Ezquerro, A. E. Münsterberg, and S. Stricker, “Editorial: Signaling Pathways in Embryonic Development,” Frontiers in Cell and Developmental Biology, vol. 5, 2017, Accessed: Jun. 12, 2023. [Online]. Available: https://www.frontiersin.org/articles/10.3389/fcell.2017.00076 

[^dakosEcologicalResilienceWhat2022]: V. Dakos and S. Kéfi, “Ecological resilience: what to measure and how,” Environ. Res. Lett., vol. 17, no. 4, p. 043003, Mar. 2022, doi: [10.1088/1748-9326/ac5767](https://doi.org/10.1088/1748-9326/ac5767). 

[^jaegerDynamicalAnalysisRegulatory2004]: J. Jaeger et al., “Dynamical Analysis of Regulatory Interactions in the Gap Gene System of Drosophila melanogaster,” Genetics, vol. 167, no. 4, pp. 1721–1737, Aug. 2004, doi: [10.1534/genetics.104.027334](https://doi.org/10.1534/genetics.104.027334). 

[^cejkovaDropletsLiquidRobots2017]: J. Čejková, T. Banno, M. M. Hanczyc, and F. Štěpánek, “Droplets As Liquid Robots,” Artificial Life, vol. 23, no. 4, pp. 528–549, Nov. 2017, doi: [10.1162/ARTL_a_00243](https://doi.org/10.1162/ARTL_a_00243). 

[^singhDifferentialGeneRegulatory2018]: A. J. Singh, S. A. Ramsey, T. M. Filtz, and C. Kioussi, “Differential gene regulatory networks in development and disease,” Cell. Mol. Life Sci., vol. 75, no. 6, pp. 1013–1025, Mar. 2018, doi: [10.1007/s00018-017-2679-6](https://doi.org/10.1007/s00018-017-2679-6). 

[^smithDesigningSyntheticNetworks2017]: R. W. Smith, B. van Sluijs, and C. Fleck, “Designing synthetic networks in silico: a generalised evolutionary algorithm approach,” BMC Systems Biology, vol. 11, no. 1, p. 118, Dec. 2017, doi: [10.1186/s12918-017-0499-9](https://doi.org/10.1186/s12918-017-0499-9). 

[^levinDarwinAgentialMaterials2023]: M. Levin, “Darwin’s agential materials: evolutionary implications of multiscale competency in developmental biology,” Cell. Mol. Life Sci., vol. 80, no. 6, p. 142, May 2023, doi: [10.1007/s00018-023-04790-z](https://doi.org/10.1007/s00018-023-04790-z). 

[^schlittCurrentApproachesGene2007]: T. Schlitt and A. Brazma, “Current approaches to gene regulatory network modelling,” BMC Bioinformatics, vol. 8, no. 6, p. S9, Sep. 2007, doi: [10.1186/1471-2105-8-S6-S9](https://doi.org/10.1186/1471-2105-8-S6-S9). 

[^falkCuriositydrivenSearchNovel2023]: M. J. Falk, F. D. Roach, W. Gilpin, and A. Murugan, “Curiosity-driven search for novel non-equilibrium behaviors.” arXiv, Mar. 17, 2023. Accessed: Apr. 28, 2023. [Online]. Available: http://arxiv.org/abs/2211.02589 

[^samuelCorrectingCalciumDysregulation2018]: T. J. Samuel, R. P. Rosenberry, S. Lee, and Z. Pan, “Correcting Calcium Dysregulation in Chronic Heart Failure Using SERCA2a Gene Therapy,” International Journal of Molecular Sciences, vol. 19, no. 4, Art. no. 4, Apr. 2018, doi: [10.3390/ijms19041086](https://doi.org/10.3390/ijms19041086). 

[^cifuentesfontanalsControlStrategyIdentification2020]: L. Cifuentes Fontanals, E. Tonello, and H. Siebert, “Control Strategy Identification via Trap Spaces in Boolean Networks,” in Computational Methods in Systems Biology, A. Abate, T. Petrov, and V. Wolf, Eds., in Lecture Notes in Computer Science. Cham: Springer International Publishing, 2020, pp. 159–175. doi: [10.1007/978-3-030-60327-4_9](https://doi.org/10.1007/978-3-030-60327-4_9). 

[^pugh2015confronting]: J. K. Pugh, L. B. Soros, P. A. Szerlip, and K. O. Stanley, “Confronting the challenge of quality diversity,” in Proceedings of the 2015 annual conference on genetic and evolutionary computation, 2015, pp. 967–974.
[^dangComputingReachableStates2011]: T. Dang, C. Le Guernic, and O. Maler, “Computing reachable states for nonlinear biological models,” Theoretical Computer Science, vol. 412, no. 21, pp. 2095–2107, May 2011, doi: [10.1016/j.tcs.2011.01.014](https://doi.org/10.1016/j.tcs.2011.01.014). 

[^delgadoComputationalMethodsGene2019]: F. M. Delgado and F. Gómez-Vela, “Computational methods for Gene Regulatory Networks reconstruction and analysis: A review,” Artificial Intelligence in Medicine, vol. 95, pp. 133–145, Apr. 2019, doi: [10.1016/j.artmed.2018.10.006](https://doi.org/10.1016/j.artmed.2018.10.006). 

[^fieldsCompetencyNavigatingArbitrary2022a]: C. Fields and M. Levin, “Competency in Navigating Arbitrary Spaces as an Invariant for Analyzing Cognition in Diverse Embodiments,” Entropy, vol. 24, no. 6, Art. no. 6, Jun. 2022, doi: [10.3390/e24060819](https://doi.org/10.3390/e24060819). 

[^steinwayCombinatorialInterventionsInhibit2015]: S. N. Steinway, J. G. T. Zañudo, P. J. Michel, D. J. Feith, T. P. Loughran, and R. Albert, “Combinatorial interventions inhibit TGFβ-driven epithelial-to-mesenchymal transition and support hybrid cellular phenotypes,” npj Syst Biol Appl, vol. 1, no. 1, Art. no. 1, Nov. 2015, doi: [10.1038/npjsba.2015.14](https://doi.org/10.1038/npjsba.2015.14). 

[^mccreeryCollectiveStrategyObstacle2016]: H. F. McCreery, Z. A. Dix, M. D. Breed, and R. Nagpal, “Collective strategy for obstacle navigation during cooperative transport by ants,” Journal of Experimental Biology, vol. 219, no. 21, pp. 3366–3375, Nov. 2016, doi: [10.1242/jeb.143818](https://doi.org/10.1242/jeb.143818). 

[^reberCognitionSurprisingPlaces2021]: A. S. Reber and F. Baluška, “Cognition in some surprising places,” Biochemical and Biophysical Research Communications, vol. 564, pp. 150–157, Jul. 2021, doi: [10.1016/j.bbrc.2020.08.115](https://doi.org/10.1016/j.bbrc.2020.08.115). 

[^dodig-crnkovicCognitionMorphologicalMorphogenetic2022]: G. Dodig-Crnkovic, “Cognition as Morphological/Morphogenetic Embodied Computation In Vivo,” Entropy (Basel), vol. 24, no. 11, p. 1576, Oct. 2022, doi: [10.3390/e24111576](https://doi.org/10.3390/e24111576). 

[^wagnerCircuitTopologyEvolution2005]: A. Wagner, “Circuit topology and the evolution of robustness in two-gene circadian oscillators,” Proceedings of the National Academy of Sciences, vol. 102, no. 33, pp. 11775–11780, Aug. 2005, doi: [10.1073/pnas.0501094102](https://doi.org/10.1073/pnas.0501094102). 

[^mathewsCellularSignalingPathways2023]: J. Mathews, A. (Jaelyn) Chang, L. Devlin, and M. Levin, “Cellular signaling pathways as plastic, proto-cognitive systems: Implications for biomedicine,” Patterns, vol. 4, no. 5, p. 100737, May 2023, doi: [10.1016/j.patter.2023.100737](https://doi.org/10.1016/j.patter.2023.100737). 

[^baluskaCellularSentiencePrimary2022]: F. Baluška, A. S. Reber, and W. B. Miller, “Cellular sentience as the primary source of biological order and evolution,” Biosystems, vol. 218, p. 104694, Aug. 2022, doi: [10.1016/j.biosystems.2022.104694](https://doi.org/10.1016/j.biosystems.2022.104694). 

[^baluskaCellularOrganismalAgency2021]: F. Baluška and A. S. Reber, “Cellular and organismal agency - Not based on genes: A comment on Baverstock,” Prog Biophys Mol Biol, vol. 167, pp. 161–162, Dec. 2021, doi: [10.1016/j.pbiomolbio.2021.11.001](https://doi.org/10.1016/j.pbiomolbio.2021.11.001). 

[^baluskaCellularEvolutionaryPerspectives2023]: F. Baluška, W. B. Miller, and A. S. Reber, “Cellular and evolutionary perspectives on organismal cognition: from unicellular to multicellular organisms,” Biological Journal of the Linnean Society, vol. 139, no. 4, pp. 503–513, Aug. 2023, doi: [10.1093/biolinnean/blac005](https://doi.org/10.1093/biolinnean/blac005). 

[^koseskaCellSignalingCognitive2017]: A. Koseska and P. I. Bastiaens, “Cell signaling as a cognitive process,” The EMBO Journal, vol. 36, no. 5, pp. 568–582, Mar. 2017, doi: [10.15252/embj.201695383](https://doi.org/10.15252/embj.201695383). 

[^huangCellFatesHighDimensional2005]: S. Huang, G. Eichler, Y. Bar-Yam, and D. E. Ingber, “Cell Fates as High-Dimensional Attractor States of a Complex Gene Regulatory Network,” Phys. Rev. Lett., vol. 94, no. 12, p. 128701, Apr. 2005, doi: [10.1103/PhysRevLett.94.128701](https://doi.org/10.1103/PhysRevLett.94.128701). 

[^zanudoCellFateReprogramming2015]: J. G. T. Zañudo and R. Albert, “Cell Fate Reprogramming by Control of Intracellular Network Dynamics,” PLOS Computational Biology, vol. 11, no. 4, p. e1004193, Apr. 2015, doi: [10.1371/journal.pcbi.1004193](https://doi.org/10.1371/journal.pcbi.1004193). 

[^beekmanBrainlessMultiHeadedDecision2015]: M. Beekman and T. Latty, “Brainless but Multi-Headed: Decision Making by the Acellular Slime Mould Physarum polycephalum,” Journal of Molecular Biology, vol. 427, no. 23, pp. 3734–3743, Nov. 2015, doi: [10.1016/j.jmb.2015.07.007](https://doi.org/10.1016/j.jmb.2015.07.007). 

[^volkBiosystemsDesignMachine2020]: M. J. Volk, I. Lourentzou, S. Mishra, L. T. Vo, C. Zhai, and H. Zhao, “Biosystems Design by Machine Learning,” ACS Synth. Biol., vol. 9, no. 7, pp. 1514–1533, Jul. 2020, doi: [10.1021/acssynbio.0c00129](https://doi.org/10.1021/acssynbio.0c00129). 

[^glontBioModelsExpandingHorizons2018]: M. Glont et al., “BioModels: expanding horizons to include more modelling approaches and formats,” Nucleic Acids Research, vol. 46, no. D1, pp. D1248–D1253, Jan. 2018, doi: [10.1093/nar/gkx1023](https://doi.org/10.1093/nar/gkx1023). 

[^malik-sheriffBioModels15Years2020]: R. S. Malik-Sheriff et al., “BioModels—15 years of sharing computational models in life science,” Nucleic Acids Research, vol. 48, no. D1, pp. D407–D415, Jan. 2020, doi: [10.1093/nar/gkz1055](https://doi.org/10.1093/nar/gkz1055). 

[^srivastavaCasualResemblanceRigorous2021]: M. Srivastava, “Beyond Casual Resemblance: Rigorous Frameworks for Comparing Regeneration Across Species,” Annual Review of Cell and Developmental Biology, vol. 37, no. 1, pp. 415–440, 2021, doi: [10.1146/annurev-cellbio-120319-114716](https://doi.org/10.1146/annurev-cellbio-120319-114716). 

[^stadterBenchmarkingNumericalIntegration2021]: P. Städter, Y. Schälte, L. Schmiester, J. Hasenauer, and P. L. Stapor, “Benchmarking of numerical integration methods for ODE models of biological systems,” Sci Rep, vol. 11, no. 1, Art. no. 1, Jan. 2021, doi: [10.1038/s41598-021-82196-2](https://doi.org/10.1038/s41598-021-82196-2). 

[^abramsonBehavioristApproachesInvestigating2021]: C. I. Abramson and M. Levin, “Behaviorist approaches to investigating memory and learning: A primer for synthetic biology and bioengineering,” Communicative & Integrative Biology, vol. 14, no. 1, pp. 230–247, Jan. 2021, doi: [10.1080/19420889.2021.2005863](https://doi.org/10.1080/19420889.2021.2005863). 

[^mcleoldBehavioralPerspectivePsychology2022]: S. McLeold, “Behavioral Perspective in Psychology [Behaviorism Theory],” Nov. 03, 2022. https://www.simplypsychology.org/behaviorism.html (accessed Jun. 16, 2023).
[^rosenbluethBehaviorPurposeTeleology1943]: A. Rosenblueth, N. Wiener, and J. Bigelow, “Behavior, Purpose and Teleology,” Philosophy of Science, vol. 10, no. 1, pp. 18–24, Jan. 1943, doi: [10.1086/286788](https://doi.org/10.1086/286788). 

[^libbyAutomatedDesignPluripotent2019]: A. R. G. Libby et al., “Automated Design of Pluripotent Stem Cell Self-Organization,” Cell Systems, vol. 9, no. 5, pp. 483-495.e10, Nov. 2019, doi: [10.1016/j.cels.2019.10.008](https://doi.org/10.1016/j.cels.2019.10.008). 

[^heinoAttractorLandscapesUnifying2022]: M. T. J. Heino, D. Proverbio, G. Marchand, K. Resnicow, and N. Hankonen, “Attractor landscapes: a unifying conceptual model for understanding behaviour change across scales of observation,” Health Psychology Review, vol. 0, no. 0, pp. 1–18, Nov. 2022, doi: [10.1080/17437199.2022.2146598](https://doi.org/10.1080/17437199.2022.2146598). 

[^kauffman1995home]: S. A. Kauffman, At home in the universe: The search for laws of self-organization and complexity. Oxford University Press, USA, 1995.
[^watsonAssociativeMemoryGene2010]: R. Watson, C. L. Buckley, R. Mills, and A. Davies, “Associative memory in gene regulation networks,” H. Fellerman, M. Dörr, M. M. Hanczyc, L. Ladegaard Laursen, S. Maurer, D. Merkle, P.-A. Monnard, K. Stoy, and S. Rasmussen, Eds., MIT Press, 2010, pp. 659–666. Accessed: Sep. 05, 2023. [Online]. Available: https://eprints.soton.ac.uk/339763/ 

[^cotterellAtlasGeneRegulatory2010]: J. Cotterell and J. Sharpe, “An atlas of gene regulatory networks reveals multiple three-gene mechanisms for interpreting morphogen gradients,” Molecular Systems Biology, vol. 6, no. 1, p. 425, Jan. 2010, doi: [10.1038/msb.2010.74](https://doi.org/10.1038/msb.2010.74). 

[^saigusaAmoebaeAnticipatePeriodic2008]: T. Saigusa, A. Tero, T. Nakagaki, and Y. Kuramoto, “Amoebae Anticipate Periodic Events,” Phys. Rev. Lett., vol. 100, no. 1, p. 018101, Jan. 2008, doi: [10.1103/PhysRevLett.100.018101](https://doi.org/10.1103/PhysRevLett.100.018101). 

[^hiscockAdaptingMachinelearningAlgorithms2019]: T. W. Hiscock, “Adapting machine-learning algorithms to design gene circuits,” BMC Bioinformatics, vol. 20, no. 1, p. 214, Apr. 2019, doi: [10.1186/s12859-019-2788-3](https://doi.org/10.1186/s12859-019-2788-3). 

[^gyurkoAdaptationLearningMolecular2013]: D. M. Gyurkó, D. V. Veres, D. Módos, K. Lenti, T. Korcsmáros, and P. Csermely, “Adaptation and learning of molecular networks as a description of cancer development at the systems-level: Potential use in anti-cancer therapies,” Seminars in Cancer Biology, vol. 23, no. 4, pp. 262–269, Aug. 2013, doi: [10.1016/j.semcancer.2013.06.005](https://doi.org/10.1016/j.semcancer.2013.06.005). 

[^mcgivernActiveMaterialsMinimal2020]: P. McGivern, “Active materials: minimal models of cognition?,” Adaptive Behavior, vol. 28, no. 6, pp. 441–451, Dec. 2020, doi: [10.1177/1059712319891742](https://doi.org/10.1177/1059712319891742). 

[^baranesActiveLearningInverse2013]: A. Baranes and P.-Y. Oudeyer, “Active learning of inverse models with intrinsically motivated goal exploration in robots,” Robotics and Autonomous Systems, vol. 61, no. 1, pp. 49–73, Jan. 2013, doi: [10.1016/j.robot.2012.05.008](https://doi.org/10.1016/j.robot.2012.05.008). 

[^lehmanAbandoningObjectivesEvolution2011]: J. Lehman and K. O. Stanley, “Abandoning Objectives: Evolution Through the Search for Novelty Alone,” Evolutionary Computation, vol. 19, no. 2, pp. 189–223, Jun. 2011, doi: [10.1162/EVCO_a_00025](https://doi.org/10.1162/EVCO_a_00025). 

[^pandiVersatileActiveLearning2022]: A. Pandi et al., “A versatile active learning workflow for optimization of genetic and metabolic networks,” Nat Commun, vol. 13, no. 1, Art. no. 1, Jul. 2022, doi: [10.1038/s41467-022-31245-z](https://doi.org/10.1038/s41467-022-31245-z). 

[^kristSimpleTheoryMolecular2021]: K. T. Krist, A. Sen, and W. G. Noid, “A simple theory for molecular chemotaxis driven by specific binding interactions,” The Journal of Chemical Physics, vol. 155, no. 16, p. 164902, Oct. 2021, doi: [10.1063/5.0061376](https://doi.org/10.1063/5.0061376). 

[^kitanoRobustnessbasedApproachSystemsoriented2007]: H. Kitano, “A robustness-based approach to systems-oriented drug design,” Nat Rev Drug Discov, vol. 6, no. 3, Art. no. 3, Mar. 2007, doi: [10.1038/nrd2195](https://doi.org/10.1038/nrd2195). 

[^abramson1994primer]: C. I. Abramson and others, A primer of invertebrate learning: the behavioral perspective. American Psychological Association, 1994.
[^loboLinearencodingModelExplains2014]: D. Lobo, M. Solano, G. A. Bubenik, and M. Levin, “A linear-encoding model explains the variability of the target morphology in regeneration,” Journal of The Royal Society Interface, vol. 11, no. 92, p. 20130918, Mar. 2014, doi: [10.1098/rsif.2013.0918](https://doi.org/10.1098/rsif.2013.0918). 

[^rizkGeneralComputationalMethod2009]: A. Rizk, G. Batt, F. Fages, and S. Soliman, “A general computational method for robustness analysis with applications to synthetic gene networks,” Bioinformatics, vol. 25, no. 12, pp. i169–i178, Jun. 2009, doi: [10.1093/bioinformatics/btp200](https://doi.org/10.1093/bioinformatics/btp200). 

[^fazilatyGeneRegulatoryNetwork2019]: H. Fazilaty et al., “A gene regulatory network to control EMT programs in development and disease,” Nat Commun, vol. 10, no. 1, Art. no. 1, Nov. 2019, doi: [10.1038/s41467-019-13091-8](https://doi.org/10.1038/s41467-019-13091-8). 

[^ingallsFrequencyDomainApproach2004]: B. P. Ingalls, “A Frequency Domain Approach to Sensitivity Analysis of Biochemical Networks,” J. Phys. Chem. B, vol. 108, no. 3, pp. 1143–1152, Jan. 2004, doi: [10.1021/jp036567u](https://doi.org/10.1021/jp036567u). 

[^grizouCuriousFormulationRobot2020]: J. Grizou, L. J. Points, A. Sharma, and L. Cronin, “A curious formulation robot enables the discovery of a novel protocell behavior,” Science Advances, vol. 6, no. 5, p. eaay4237, Jan. 2020, doi: [10.1126/sciadv.aay4237](https://doi.org/10.1126/sciadv.aay4237). 

[^scheinerCompilationTypologyAbundance2019]: S. M. Scheiner, “A compilation of and typology for abundance-, phylogenetic-and functional-based diversity metrics,” BioRxiv, p. 530782, 2019.

